---

<h1 align="center">Deployment for Intelligent Video Analytics using DeepStream</h1>

We know how deployment could be a delicate and laborious task given the diversity of objects, environments and camera types, let alone live video stream handling and scalability support. To address these issues, DeepStream offers a complete framework for deploying AI-based solutions for Intelligent Video Analytics (IVA) projects.


<br/>

<img src='images/ds2car.png'/> 

<p style="text-align: center;color:gray">Figure 1. DeepStream's reference application output</p>

DeepStream allows you to focus on the core deep learning and IP components of your IVA system rather than designing an end-to-end solution from scratch.

_Please note that this training assumes you are familiar with fundamentals of video processing, computer vision based deep learning tasks, including image classification and object detection, as well as the basics of the C and C++ programming languages._


This tutorial covers the following topics:

* [1. DeepStream Overview](#overview)
    * [1.1 Simplifying IVA Applications](#IVA)
    * [1.2 Performance](#performance)
    * [1.3 Scalability](#scalability)
    * [1.4 DeepStream SDK overview](#ds-sdk)
* [2. GStreamer Foundations](#gs-found)
    * [2.1 Elements ](#elements)
    * [2.2 Pads ](#pads)
    * [2.3 Caps (Capabilities)](#caps)
    * [2.4 Buffers ](#buffers)
    * [2.5 Plugin Based Architecture ](#plugin-arc)
* [3. Setup Prerequisites](#setup)
    * [3.1 Installation Procedure](#install)
    * [3.2 Directory Layout](#dir-layout)
* [4. Building a sample application](#sample_application)
    * [4.1 Application Walk-Through ](#app-4)
    * [4.2 Using Configuration Files](#config-4)
    * [4.3 Pipeline Architecture ](#PIPELINE-1)
* [5. Build A Multi-DNN Application  ](#build-mdnn)
    * [5.1 Pipeline ](#PIPELINE-2)
    * [5.2 Application code walk-through ](#CODE_WALK-THROUGH-2)
    * [5.3 New Configuration Parameters ](#new-config)
    * [5.4 Accessing Metadata](#access-meta)
* [6. Custom Parsers and Networks  ](#custom-parser)
    * [6.1 Pipeline](#PIPELINE-3)
    * [6.2 Using Custom Parsers ](#custom-parsers-6)
* [7. Custom Plugins and OpenCV based Detection ](#custom-plugins)
    * [7.1 Building Pipelines at the Command Line ](#building-pipeline-7)
    * [7.2 Pipeline Architecture](#PIPELINE-7)
    * [7.3 Custom Plugin Library Structure ](#custom-plugin-lib)
    * [7.4 Motion Detection with OpenCV ](#MD-CV)
    * [7.5 GStreamer Plugin Mechanics ](#gs-plug)
    * [7.6 Compile and Run](#comp-run-7)
    * [7.7 Visualizing the Pipeline](#vis-pipeline)
    * [7.8 Evaluate the Output](#ev-output)
* [8. Object Detection on Multiple Input Streams ](#od-multiple)
    * [8.1 Batching Input Streams ](#batch-input)
    * [8.2 Composing a Pipeline ](#compose-pipline)
* [9. Dewarping 360° camera streams](#dewarp)
* [10. Using "nvmsgconv" and "nvmsgbroker" plugins in the pipeline](#msgconv)
    * [10.1 The  gst-nvmsgconv plugin](#gst-nvmsgconv)
    * [10.2 The  gst-nvmsgbroker plugin](#gst-nvmsgbroker)
    * [10.3 The "nvmsgconv" and "nvmsgbroker" example application](#example-10)
* [11. Performance Analysis](#PERFORMANCE_ANALYSIS)
    * [11.1 Generating Performance KPIs ](#gen-kpi)
    * [11.2 Throughput](#throughput)
    * [11.3 GPU Performance Metrics](#gpu-perf)
    * [11.4 Generating Latency Metrics with GStreamer Logs](#gen_latency)
    * [11.5 More on GPU Utilization](#util-2)

---

Here we will go through a series of sample programs, each highlighting different aspects of DeepStream. By the end of this we will have a strong understanding of how DeepStream applications work and how we can get started building your own.

# Note :

* While recent advancements in deep learning and computer vision offer human-like classification and object detection capabilities, building IVA applications to utilize these techniques is a challenging task. Building video analytics applications still takes extensive effort, not to mention tuning and optimizing of these systems is tedious.


<a id='overview'></a>
## 1. DeepStream Overview

<a id='IVA'></a>
### 1.1 Simplifying IVA Applications

DeepStream simplifies building IVA applications by separating the application into components managed and built by the user and components managed by DeepStream. 

<img src='images/DeepstreamWorkflowfinal600x410-07.jpg'/> 

<p style="text-align: center;color:gray">Figure 2. Video analysis tasks by DeepStream vs developer</p>


As developers, we build components to manage important business tasks like:

- Selecting the kind and number of video streams we want to analyze
- Choosing the type of analysis, we want to do on the video
- Handling and interacting with the results of our analysis


We __don't__ need to build components to manage difficult tasks like:
- Efficiently leverage the GPU for accelerated processing and inference
- Efficiently process data from multiple video streams at once
- Keeping track of metadata associated with each frame of video from multiple sources
- Optimizing our pipeline for maximum data throughput
- Optimizing our neural networks for high-speed inference

These are __mundane__ tasks that the DeepStream SDK manages for us. That lets us focus on the more __important__ tasks related to the project's goal and impact. DeepStream lets us focus on the intelligence portion of the application.

<a id='performance'></a>
### 1.2 Performance

To give an overview of performance improvement when using DeepStream SDK, we will scrutinize the DeepStream-app reference application included within the release package. Figure 3 shows that the performance is doubled using DeepStream 3.0 when tested on T4 compared to the previous version P4, while it consumes the same amount of power and equal number of streams. The reference application includes a primary detector, three classifiers and a tracker.



<img src='images/ds_perf_2.png' width='900px'/>
<p style="text-align: center;color:gray"> Figure 3. Performance measurement for the DeepStream reference application</p>

<a id='scalability'></a>
### 1.3 Scalability

DeepStream provides scalability at different levels of the system hierarchy. For example, the DeepStream SDK 3.0 supports processing a higher number of concurrent streams, in addition to utilizing multiple GPUs upon availability. Furthermore DeepStream-in-containers provide flexibility to the deployment phase as shown below:

<img src='images/ds_dockerfig8-1.png' width='900px'/>
<p style="text-align: center;color:gray">Figure 4. Scalability of DeepStream applications</p>


<a id='ds-sdk'></a>
### 1.4 DeepStream SDK overview

The DeepStream SDK consists of a set of building blocks which bridge the gap between low level APIs (such as TensorRT, Video Codec SDK) and the user application. By utilizing the DeepStream SDK, you can accelerate development of the IVA applications by focusing on building core deep learning models instead of designing end-to-end applications from scratch. 

Below, you can see a schematic presentation of the DeepStream SDK in a series of potential applications.

<img src='images/deepstream-sdk.png' width='900px'/>
<p style="text-align: center;color:gray">Figure 5. DeepStream application structure</p>



In addition, the DeepStream SDK extends these capabilities by providing several other hardware accelerated building blocks.  This includes support for TensorRT 5, CUDA 10, and Turing GPUs. In addition, DeepStream applications can be deployed as a part of a larger multi-GPU cluster or a microservice in containers. This allows highly flexible system architectures and opens new application capabilities.

Below, you can see a shortened list of new capabilities provided by DeepStream:

 - Allowing addition and removal of video stream dynamically and during the pipeline execution, in addition to frame rate and resolution adjustments
 - Extending the video processing capabilities by supporting custom layers, and user-defined parsing of detector outputs
 - Providing Support for 360-degree camera using GPU-accelerated dewarping libraries
 - Augmenting the meta-data with application-specific, user-defined insights
 - Providing pruned and efficient inference models
 - Getting detailed performance analysis with the NVIDIA Nsight system profiler tool.


The DeepStream SDK is based on the __GStreamer multimedia framework__ and provides a pipeline of GPU accelerated plugins as shown in figure 6. The SDK facilitates application implementation procedure by providing plugins for video inputs, video decoding, image pre-processing, TensorRT-based inference, object tracking and display. You can utilize these capabilities to assemble flexible, multi-stream video analytics applications.


<img src='images/general-pipeline.png' width='900px'/>
<p style="text-align: center;color:gray">Figure 6. Sample DeepStream pipeline</p>


  
<a id='gs-found'></a>
## 2. GStreamer Foundations 

The DeepStream SDK is based on the open source [GStreamer multimedia framework](https://gstreamer.freedesktop.org/). There are a few key concepts in GStreamer that we need to touch on before getting started. These include Elements, Pads, Buffers, and Caps. We will be describing them at a high level, but encourage those who are interested in the details to read the [GStreamer Basics](https://gstreamer.freedesktop.org/documentation/application-development/basics/index.html) documentation to learn more. 

<a id='elements'></a>
### 2.1 Elements 

Elements are the core building block with which we make pipelines. Every process in-between the source (i.e. input of the pipeline, e.g. camera and video files) and sink elements (e.g. screen display) is passed through elements. Video decoding and encoding, neural network inference, and displaying text on top of video streams are examples of "element". DeepStream allows us to instantiate elements and weave them into pipelines. 

  

<br /> <br /> 

<img src='images/element.png'/> 

<p style="text-align: center;color:gray">Figure 7. Example pipeline with three <b>elements</b></p> 

<a id='pads'></a>
### 2.2 Pads 

Pads are the interfaces between elements. When data flows from element to another element in a pipeline, it flows from the sink pad of one element to the source pad of another. Note that each element might have zero, one or many source/sink elements. 

<br /> <br /> 

<img src='images/pads.jpg'/> 
<p style="text-align: center;color:gray">Figure 8. Elements with source/sink pads</p> 

<a id='caps'></a>
### 2.3 Caps (Capabilities) 

Caps (or Capabilities), are the data types that a pad is permitted to utilize or emit. Because pads can allow multiple data types, sometimes the data flow is ambiguous. Pads are "negotiated" in order to explicitly define the type of data that can flow through the pad. Caps streamline this process and allow elements of our pipeline with ambiguous pads to negotiate the correct data flow process. Later in this course, we will use caps to pass certain video data types (NV12, RGB) to the downstream elements in the pipeline. 

<a id='buffers'></a>
### 2.4 Buffers 

Buffers carry the data that will passed on through the pipeline. Buffers are timestamped, contain metadata such as how many elements are using it, flags, and pointers to objects in memory. When we write application code, we rely on accessing data attached to the buffer. 
  
<a id='plugin-arc'></a>
### 2.5 Plugin Based Architecture 

DeepStream applications can be thought of as pipelines consisting of individual components (plugins). Each plugin represents a functional block like inference using TensorRT or multi-stream decode. Where applicable, plugins are accelerated using the underlying hardware to deliver maximum performance. DeepStream’s key value is in making deep learning for video easily accessible, to allow you to concentrate on quickly building and customizing efficient and scalable video analytics applications.  

The plugin architecture provides functionality such as video encode/decode, scaling, inferencing, and more. By connecting plugins into a pipeline, we can build complex applications. Because DeepStream is built on top of GStreamer, we can inspect plugins using `gst-inspect-1.0`. Let's inspect a plugin to learn more about it (we use the `!` symbol to execute at the command line). 

In [2]:
!gst-inspect-1.0 h264parse

Factory Details:
  Rank                     primary + 1 (257)
  Long-name                H.264 parser
  Klass                    Codec/Parser/Converter/Video
  Description              Parses H.264 streams
  Author                   Mark Nauwelaerts <mark.nauwelaerts@collabora.co.uk>

Plugin Details:
  Name                     videoparsersbad
  Description              videoparsers
  Filename                 /usr/lib/x86_64-linux-gnu/gstreamer-1.0/libgstvideoparsersbad.so
  Version                  1.8.3
  License                  LGPL
  Source module            gst-plugins-bad
  Source release date      2016-08-19
  Binary package           GStreamer Bad Plugins (Ubuntu)
  Origin URL               https://launchpad.net/distros/ubuntu/+source/gst-plugins-bad1.0

GObject
 +----GInitiallyUnowned
       +----GstObject
             +----GstElement
                   +----GstBaseParse
                         +----GstH264Parse

Pad Templates:
  SRC template: 'src'
    Availability: Always
 

We see a lot of useful information, but for now let's focus on the `Descriptions`. By inspecting the `h264parse` plugin, we can see that this is meant for parsing H.264 streams. Cameras typically stream encoded data to a processor. We commonly use [MPEG-4 (H.264)](https://en.wikipedia.org/wiki/H.264/MPEG-4_AVC) for compression and encoding, but other options like H.265, VC1, and MPEG-2, to name a few, are available. Compression facilitates accelerated processing by reducing the amount of data transmitted from one place to another. When we are building a pipeline, we can use this plugin if we need to parse H.264 video streams. 
<a id='q1'></a>
 Let's inspect a DeepStream specific plugin: `nvosd`.


In [1]:
!gst-inspect-1.0 nvosd

Factory Details:
  Rank                     primary (256)
  Long-name                NvOsd plugin
  Klass                    NvOsd functionality
  Description              Gstreamer bounding box draw element
  Author                   NVIDIA Corporation. Post on Deepstream for Tesla forum for any queries @ https://devtalk.nvidia.com/default/board/209/

Plugin Details:
  Name                     nvosd
  Description              Gstreamer plugin to draw rectangles and text
  Filename                 /usr/lib/x86_64-linux-gnu/gstreamer-1.0/libnvdsgst_osd.so
  Version                  3.0
  License                  Proprietary
  Source module            nvosd
  Binary package           GStreamer nvosd Plugin
  Origin URL               http://nvidia.com/

GObject
 +----GInitiallyUnowned
       +----GstObject
             +----GstElement
                   +----GstBaseTransform
                         +----GstNvOsd

Pad Templates:
  SINK template: 'sink'
    Availability: Always
    Capabil

This plugin is designed draw to rectangles and text. By weaving this plugin into a pipeline, we can easily display bounding boxes and class labels on our video streams based on the results of a inference model.  

<a id='setup'></a>
## 3. Setup Prerequisites

DeepStream has the following requirements:


    Ubuntu 16.04
    NVIDIA driver 410+
    CUDA 10
    TensorRT 5.0.2+
    GStreamer 1.8.3
    OpenCV 3.4.1 [Download and compile OpenCV-3.4.0 with CUDA 10]
    
---

To install prerequisites, refer to section “Quick Start Guide” in the user guide file included in __DeepStream_Release/docs__.

<a id='install'></a>
### 3.1 Installation Procedure
Run the following commands. With this, the SDK installation is complete.

In [3]:
!export PKG_CONFIG_PATH=/usr/lib/x86_64-linux-gnu/gstreamer-1.0
!$PKG_CONFIG_PATH

In [ ]:
"""
%%bash

make -C DeepStream_Release/sources/apps/deepstream-test1 clean
make -C DeepStream_Release/sources/apps/deepstream-test2 clean
make -C DeepStream_Release/sources/apps/deepstream-test3 clean
make -C DeepStream_Release/sources/apps/deepstream-test4 clean
make -C DeepStream_Release/sources/libs/nvparsebbox clean
make -C DeepStream_Release/sources/gst-plugins/gst-dsexample clean
"""

In [5]:
# Clear the cache
!rm -rf $HOME/.cache/gstreamer-1.0/

<a id='dir-layout'></a>
### 3.2 Directory Layout

When you download the DeepStream package and untar it, you will find similar folders to what is described next. We will briefly mention the contents through several of the directories as they will be particularly useful for you when designing your own applications.

* In the __samples__ directory, configuration files required for the reference application are provided. 

* In the __samples/Models__ directory, four ResNet based neural networks are provided as a part of the package. 

    * __Primary Detector__ is ResNet10 based 4 class detector. It detects vehicle, person, two-wheeler, and road sign. The network resolution of this model is 640x368 pixels. 

    * __Secondary_CarColor__: It is 12 class color classifier. 

    * __Secondary_CarMake__: It is 20 class car make classifier. 

    * __Secondary_VehicleTypes__: It is 6 class car-type classifier. 

    * The three secondary models are ResNet18 based car classifiers. These Networks operate on 224x224 resolution. 

* In the __sources/apps__ directory, four test applications and sample template plugin (to integrate custom IP) are provided. We will go through some of these applications in this lab. 

* In the __includes__ directory, you can find header files to develop your own application and plugin. 

* __nvparsebbox__ contains the sample code for a bounding box parser function. This parser function is for ResNet-10 based neural network detector. We will see more about it in lab exercise. 

* binaries.tbz2 file contains NVIDIA GStreamer plugins and their supporting libraries. 

<a id='sample_application'></a>
## 4. Building a sample application

In this section, we are going to “Build a sample application”. This is the “Hello world” of DeepStream SDK. This will introduce you to the building blocks of the DeepStream SDK, how to implement a simple application using these building blocks, and will give us an overview of metadata handling.  This application decodes the input file and then detects the objects in the frame using neural networks. 

Since this is the first exercise introducing the pipeline declaration, we will spend extra time describing the code and building blocks of the pipeline. 

At the end of this section, you will be familiar with how to write an application based on the Deepstream SDK. 

<a id='app-4'></a>
### 4.1 Application Walk-Through 

* Walk through what's going on in our application. 

--- 
<a id='init-set'></a>
#### Initialization and setting up a pipeline 

First, we initialize the GStreamer container and create a container element called `pipeline` in __main__ using `gst_pipeline_new`, which is going to contain all the elements shown in the pipeline diagram we saw previously.  

```c 

  /* Standard GStreamer initialization */ 
  gst_init (&argc, &argv); 
  loop = g_main_loop_new (NULL, FALSE); 
  /* Create gstreamer elements */ 
  /* Create Pipeline element that will form a connection of other elements */ 
  pipeline = gst_pipeline_new ("dstest1-pipeline"); 

``` 
<a id='video-source'></a>
#### Setting the video source 

Then, we create all the elements required in the pipeline using `gst_element_factory_make`. We start by specifing the input source as a video file on disk: 

```c 
/* Source element for reading from the file */ 
  source = gst_element_factory_make ("filesrc", "file-source"); 

``` 
<a id='h264'></a>
#### H264 parser and encoder 

We need to create h264 parser and decoders. Our video source is encoded using h264 codec and `nvdec_h264` allows us to perform GPU-accelerated decoding: 

```c 
  /* Since the data format in the input file is elementary h264 stream, 
   * we need a h264parser */ 
  h264parser = gst_element_factory_make ("h264parse", "h264-parser"); 
  /* Use nvdec_h264 for hardware accelerated decode on GPU */ 
  decoder = gst_element_factory_make ("nvdec_h264", "nvh264-decoder"); 

``` 
<a id='nvinfer'></a>
#### nvinfer, the inference plugin 

The `nvinfer plugin` provides TensorRT-based inference for detection and tracking.  The low-level library (libnvds_infer) operates either on float RGB or BGR planar data with dimensions of Network Height and Network Width. The plugin accepts NV12/RGBA data from upstream components like the decoder, muxer, and dewarper.  

The Gst-nvinfer plugin also performs preprocessing operations like format conversion, scaling, mean subtraction, and produces final float RGB/BGR planar data which is passed to the low-level library. The low-level library uses the TensorRT engine for inferencing. It outputs each classified object’s class and each detected object’s bounding boxes (Bboxes) after clustering. 

```c 
  /* Use nvinfer to run inferencing on decoder's output, 
   * behavior of inferencing is set through config file */ 
  pgie = gst_element_factory_make ("nvinfer", "primary-nvinference-engine"); 

``` 
<br /> 
<img src='images/nvinfer.jpg'/> 
<p style="text-align: center;color:gray">Figure 9. The nvinfer plugin</p> 

<a id='nvvidconv'></a>
#### nvvidconv for video conversions 

Next, we create the `nvvidconv` plugin that performs color format conversions, which is required to make data ready for the `nvosd` plugin: 

```c 
  /* Use convertor to convert from NV12 to RGBA as required by nvosd */ 
  nvvidconv = gst_element_factory_make ("nvvidconv", "nvvideo-converter"); 
``` 
<br /> 

<img src='images/nvvidconv.jpg'/> 
<p style="text-align: center;color:gray">Figure 10. The nvvidconv plugin</p> 

<a id='annotate-nvosd'></a>
#### Annotating using nvosd 

The `nvosd` plugin draws bounding boxes, text, and RoI (Regions of Interest) polygons (Polygons are presented as a set of lines). 

The plugin accepts an RGBA buffer with attached metadata from the upstream component. It draws bounding boxes, which may be shaded depending on the configuration (e.g. width, color, and opacity) of a given bounding box. It also draws text and RoI polygons at specified locations in the frame. Text and polygon parameters are configurable through metadata. 

```c 

  /* Create OSD to draw on the converted RGBA buffer */ 
  nvosd = gst_element_factory_make ("nvosd", "nv-onscreendisplay"); 
``` 
<br /> 

<img src='images/nvosd.jpg'/> 
<p style="text-align: center;color:gray">Figure 11. The nvosd plugin</p> 

<a id='write-stream'></a>
#### Writing the stream back to the disk 

Next, we are creating another nvvidconv to convert the video back to the NV12 format (after being consumed by the `nvosd` element)  

```c 
  nvvidconv1 = gst_element_factory_make("nvvidconv", "nvvideo-converter1"); 
  videoconvert = gst_element_factory_make("videoconvert", "converter"); 
``` 

We would like to save video files on the drive using the sink element of the pipeline. To save a video file, we need to encode the stream using the h264 codec of `x264enc` element and pass it to the `filesink` to be written on disk. 

```c 
  x264enc = gst_element_factory_make("x264enc", "h264 encoder"); 
  qtmux = gst_element_factory_make("qtmux", "muxer"); 

  /* Finally render the osd output */ 
  sink = gst_element_factory_make ("filesink", "filesink"); 

``` 
<a id='more-caps'></a>
#### More on caps... 

The `capsfilter` does not modify the incoming data, however it allows only certain types of data to be passed through the element. We use these filters to pass the required video data formats through the `nvosd` element. 

```c
  /* caps filter for nvvidconv to convert NV12 to RGBA as nvosd expects input 
   * in RGBA format */ 
  filter1 = gst_element_factory_make ("capsfilter", "filter1"); 
  filter2 = gst_element_factory_make ("capsfilter", "filter2"); 
  filter3 = gst_element_factory_make ("capsfilter", "filter3"); 
  filter4 = gst_element_factory_make ("capsfilter", "filter4"); 

``` 
<a id='set-elements'></a>
#### Setting element properties... 

Before creating the actual pipeline, we need to set properties of some of the elements. for example, the `filesrc` element requires the name of a video file. Below, you can review a few examples of properties we have set in the source file: 

```c 
  /* we set the input filename to the source element */ 
  g_object_set (G_OBJECT (source), "location", argv[1], NULL); 
  g_object_set(G_OBJECT(sink), "location", "out_test1.mp4", NULL); 

  /* Set all the necessary properties of the nvinfer element, 
   * the necessary ones are : */ 

  g_object_set (G_OBJECT (pgie), 

``` 
<a id='access-meta-4'></a>
#### Accessing Metadata Results 

We use [probes](https://gstreamer.freedesktop.org/documentation/application-development/advanced/pipeline-manipulation.html#using-probes) to access our metadata. Probes are simply callback functions that interact with the pads of elements. They let us easily interact with data flowing through our pipeline. 

```c 
  /* Let's add probe to get informed of the meta data generated, we add probe to 
   * the sink pad of the osd element, since by that time, the buffer would have 
   * had got all the metadata. */ 
  osd_sink_pad = gst_element_get_static_pad (nvosd, "sink"); 
  if (!osd_sink_pad) 
    g_print ("Unable to get sink pad\n"); 
  else { 
    osd_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER, 
        osd_sink_pad_buffer_probe, NULL, NULL); 

``` 

Inside the callback function, __osd_sink_pad_buffer_probe__, we iterate through all the metadata types which are attached to the buffer. The DeepStream components attach metadata of type `NVDS_META_FRAME_INFO` to the buffer. We access the object metadata to count the number of vehicles in the frame. In this example we are using 4 class detectors (vehicle, person, two-wheeler and road sign). The class_id of class “vehicle” is 0. So, we will count the objects having class id = 0. In the same way, we can find the number of people in the frame.  

```c 

osd_sink_pad_buffer_probe (GstPad * pad, GstPadProbeInfo * info, 
    gpointer u_data) 
{ 
... 
    while ((gst_meta = gst_buffer_iterate_meta (buf, &state))) { 
        if (gst_meta_api_type_has_tag (gst_meta->info->api, _nvdsmeta_quark)) { 
          nvdsmeta = (NvDsMeta *) gst_meta; 
          /* We are interested only in intercepting Meta of type 
           * "NVDS_META_FRAME_INFO" as they are from infer elements. */ 
          if (nvdsmeta->meta_type == NVDS_META_FRAME_INFO) { 
            frame_meta = (NvDsFrameMeta *) nvdsmeta->meta_data; 
... 
            for (rect_index = 0; rect_index < num_rects; rect_index++) { 
              //show class names, count etc. Refer to the source file for more information 
... 
            } 
          } 
        } 
      } 
... 
      return GST_PAD_PROBE_OK; 
} 

``` 

 We will learn more about handling metadata and probes in Exercise 2 and Exercise 6. 
 
<a id='link-elements'></a>
#### Adding elements to the pipeline and linking them together 

We configure these elements with the required parameters so that each component does one of the operations we need. Next, we add all these elements to the pipeline (`gst_bin_add_many`). This function accepts a list of elements to be added, ending with NULL. Individual elements also can be added with `gst_bin_add`. 

```c 
  gst_bin_add_many (GST_BIN (pipeline), 
      source, h264parser, decoder, pgie, 
      filter1, nvvidconv, filter2, nvosd, nvvidconv1, filter3, 
      videoconvert, filter4, x264enc, qtmux, sink, NULL); 
``` 

__Note__: While `gst_bin_add_many` adds elements to the pipeline, it does not link them together. The elements of the above function are not ordered. In order to link the items, we need to call the `gst_element_link_many` function. 

We link all these elements in the order data will flow through the pipeline (`gst_element_link_many`). 

```c 
  gst_element_link_many (source, h264parser, decoder, pgie, filter1, 
      nvvidconv, filter2, nvosd, nvvidconv1, filter3, 
      videoconvert, filter4, 
      x264enc, qtmux, sink, NULL); 
``` 
<a id='run-pipeline'></a>
#### Running the pipeline 

With a pipeline defined and the elements linked, we install a callback function on the sink pad of the OSD component and then we put the pipeline in “PLAYING” state. When the buffer arrives on the sink pad of the OSD component, the callback function is called. When the pipeline is finished, we put the pipeline into the "NULL" state to clean up. 

```c 
  g_print ("Now playing: %s\n", argv[1]); 
  gst_element_set_state (pipeline, GST_STATE_PLAYING); 

  /* Wait till pipeline encounters an error or EOS */ 

  g_print ("Running...\n"); 
  g_main_loop_run (loop); 

``` 
<a id='config-4'></a>
### 4.2 Using Configuration Files 

Configuration files tell our application how to utilize our deep learning model. The __NvInfer__ component uses this configuration file for inference. Let's look at an example configuration file to go over the common parameters. 

```c 
gpu-id=0 
net-scale-factor=0.0039215697906911373 
model-file=../../../samples/models/Primary_Detector/resnet10.caffemodel 
proto-file=../../../samples/models/Primary_Detector/resnet10.prototxt 
labelfile-path=../../../samples/models/Primary_Detector/labels.txt 
int8-calib-file=../../../samples/models/Primary_Detector/cal_trt4.bin 
batch-size=1 
network-mode=1 
num-detected-classes=4 
interval=0 
gie-unique-id=1 
parse-func=4 
output-blob-names=conv2d_bbox;conv2d_cov/Sigmoid 

``` 

The config file contains the list of parameters required for the neural network as well as a few parameters required for the application. 

* __gpu-id__: Indicates which GPU to be used for inference in case of multiple GPUs. 
* __net-scale-factor__: A pixel normalization factor. A parameter required for ResNet model. 
* __model-file__: The path to the Caffe model file 
* __proto-file__: The path to prototext file. This contains the network architecture. 
* __labelfile-path__: A path to the text file containing the labels of the objects (vehicle, person, two wheeler, road sign). This file is used by the DeepStream reference application.  
* __int8-calib-file__: Calibration file for dynamic range adjustment with an FP32 model. 
* __batch-size__: The number of frames or objects to be inferred together in a batch. 
* __network-mode__: The data format to be used by inference. We can set it to int8 or FP32. 
* __parse-func__: The type of detector bounding box parser function. Set it to 0 for your own trained model and it’s bounding-box  parser function. We will see more about this in our 3rd lab exercise. 
* __output-blob-names__: The name of the name of the coverage layer for the Caffe model. 

<a id='PIPELINE-1'></a> 
### 4.3 Pipeline Architecture 

This is the pipeline architecture of the test application. 

<img src='images/Lab1_pipeline.png' style='width:80%'/> 
<p style="text-align: center;color:gray">Figure 12. deepstream-test1 pipeline</p> 

#### In a nutshell: 

 To begin, the __FileSrc__ component will read data from the compressed file and feed it to the decoder. 

__NvDec__ will decode the incoming data and the output frames will be given to the __NvInfer__ component. 

The __NvInfer__ component is configured with Resnet-10 based neural network parameters (e.g. model file, prototxt, batch-size) to detect and classify the objects. After inference, it attaches the output metadata - <i>i.e. object type, it’s bounding boxes </i> - to the buffer. 

Then the video data on the buffer, along with its metadata, is sent to the on-screen display component to draw bounding boxes and texts describing attributes of the objects (using __Nvvidconv__ along the way to convert the format). 

To access the metadata in the application, we install a callback function on the sink pad of the __OSD__ component. The application can then use this metadata to solve the given problem (in this case, counting the number of people, number of vehicles, etc.). 

### deepstream_test1_app.c

In [ ]:
"""

#include <gst/gst.h>
#include <glib.h>
#include <sys/time.h>
#include "gstnvdsmeta.h"

#define MAX_DISPLAY_LEN 64

#define PGIE_CLASS_ID_VEHICLE 0
#define PGIE_CLASS_ID_PERSON 2

gint frame_number = 0;
gchar pgie_classes_str[4][32] = { "Vehicle", "TwoWheeler", "Person",
  "Roadsign"
};

static GstPadProbeReturn
sink_bin_buf_probe (GstPad * pad, GstPadProbeInfo * info, gpointer u_data)
{

  static struct timeval last_fps_time;
  static struct timeval curr_fps_time;
  static int numbuff = 0;

  /* this parameter determines after how many frames fps metrics are reported */
  const int FPS_DISPLAY_FREQ = 10; 

  if ((numbuff++ % FPS_DISPLAY_FREQ) == 0) {
    //last fps is not recorded
    if (last_fps_time.tv_sec == 0
        && last_fps_time.tv_usec == 0)
      /* first time around */
      gettimeofday (&last_fps_time, NULL); 
    else {
      gettimeofday (&curr_fps_time, NULL);
      gdouble elapsedtime  =
          (curr_fps_time.tv_sec +
            curr_fps_time.tv_usec / 1000000.0) -
          (last_fps_time.tv_sec +
            last_fps_time.tv_usec / 1000000.0);
      g_print ("%.2f fps\n", (FPS_DISPLAY_FREQ/elapsedtime));
      last_fps_time = curr_fps_time;
    }

  }
  return GST_PAD_PROBE_OK;

}




/* osd_sink_pad_buffer_probe  will extract metadata received on OSD sink pad
 * and update params for drawing rectangle, object information etc. */

static GstPadProbeReturn
osd_sink_pad_buffer_probe (GstPad * pad, GstPadProbeInfo * info,
    gpointer u_data)
{

  GstMeta *gst_meta = NULL;
  NvDsMeta *nvdsmeta = NULL;
  gpointer state = NULL;
  static GQuark _nvdsmeta_quark = 0;
  GstBuffer *buf = (GstBuffer *) info->data;
  NvDsFrameMeta *frame_meta = NULL;
  guint num_rects = 0, rect_index = 0, l_index = 0;
  NvDsObjectParams *obj_meta = NULL;
  guint i = 0;
  NvOSD_TextParams *txt_params = NULL;
  guint vehicle_count = 0;
  guint person_count = 0;

  if (!_nvdsmeta_quark)
    _nvdsmeta_quark = g_quark_from_static_string (NVDS_META_STRING);

  while ((gst_meta = gst_buffer_iterate_meta (buf, &state))) {
    if (gst_meta_api_type_has_tag (gst_meta->info->api, _nvdsmeta_quark)) {

      nvdsmeta = (NvDsMeta *) gst_meta;

      /* We are interested only in intercepting Meta of type
       * "NVDS_META_FRAME_INFO" as they are from our infer elements. */
      if (nvdsmeta->meta_type == NVDS_META_FRAME_INFO) {
        frame_meta = (NvDsFrameMeta *) nvdsmeta->meta_data;
        if (frame_meta == NULL) {
          g_print ("NvDS Meta contained NULL meta \n");
          return GST_PAD_PROBE_OK;
        }

        /* We reset the num_strings here as we plan to iterate through the
         *  the detected objects and form our own strings.
         *  The pipeline generated strings shall be discarded.
         */
        frame_meta->num_strings = 0;

        num_rects = frame_meta->num_rects;

        /* This means we have num_rects in frame_meta->obj_params,
         * now lets iterate through them */

        for (rect_index = 0; rect_index < num_rects; rect_index++) {
          /* Now using above information we need to form a text that should
           * be displayed on top of the bounding box, so lets form it here. */

          obj_meta = (NvDsObjectParams *) & frame_meta->obj_params[rect_index];

          txt_params = &(obj_meta->text_params);
          if (txt_params->display_text)
            g_free (txt_params->display_text);

          txt_params->display_text = g_malloc0 (MAX_DISPLAY_LEN);

          g_snprintf (txt_params->display_text, MAX_DISPLAY_LEN, "%s ",
              pgie_classes_str[obj_meta->class_id]);

          if (obj_meta->class_id == PGIE_CLASS_ID_VEHICLE)
            vehicle_count++;
          if (obj_meta->class_id == PGIE_CLASS_ID_PERSON)
            person_count++;

          /* Now set the offsets where the string should appear */
          txt_params->x_offset = obj_meta->rect_params.left;
          txt_params->y_offset = obj_meta->rect_params.top - 25;

          /* Font , font-color and font-size */
          txt_params->font_params.font_name = "Arial";
          txt_params->font_params.font_size = 10;
          txt_params->font_params.font_color.red = 1.0;
          txt_params->font_params.font_color.green = 1.0;
          txt_params->font_params.font_color.blue = 1.0;
          txt_params->font_params.font_color.alpha = 1.0;

          /* Text background color */
          txt_params->set_bg_clr = 1;
          txt_params->text_bg_clr.red = 0.0;
          txt_params->text_bg_clr.green = 0.0;
          txt_params->text_bg_clr.blue = 0.0;
          txt_params->text_bg_clr.alpha = 1.0;

          frame_meta->num_strings++;
        }
      }
    }
  }
  g_print ("Frame Number = %d Number of objects = %d "
      "Vehicle Count = %d Person Count = %d\n",
      frame_number, num_rects, vehicle_count, person_count);
  frame_number++;

  return GST_PAD_PROBE_OK;
}

static gboolean
bus_call (GstBus * bus, GstMessage * msg, gpointer data)
{
  GMainLoop *loop = (GMainLoop *) data;
  switch (GST_MESSAGE_TYPE (msg)) {
    case GST_MESSAGE_EOS:
      g_print ("End of stream\n");
      g_main_loop_quit (loop);
      break;
    case GST_MESSAGE_ERROR:{
      gchar *debug;
      GError *error;
      gst_message_parse_error (msg, &error, &debug);
      g_printerr ("ERROR from element %s: %s\n",
          GST_OBJECT_NAME (msg->src), error->message);
      if (debug)
        g_printerr ("Error details: %s\n", debug);
      g_free (debug);
      g_error_free (error);
      g_main_loop_quit (loop);
      break;
    }
    default:
      break;
  }
  return TRUE;
}

int
main (int argc, char *argv[])
{
  GMainLoop *loop = NULL;
  GstElement *pipeline = NULL, *source = NULL, *h264parser =
      NULL,
      *decoder = NULL, *sink = NULL, *pgie = NULL, *nvvidconv =
      NULL, *nvosd = NULL, *filter1 = NULL, *filter2 = NULL;
  GstBus *bus = NULL;
  guint bus_watch_id;
  GstCaps *caps1 = NULL, *caps2 = NULL;
  gulong osd_probe_id = 0;
  gulong perf_probe_id = 0;
  GstPad *osd_sink_pad = NULL;

  GstElement *nvvidconv1 = NULL;
  GstElement *filter3 = NULL;
  GstElement *videoconvert = NULL;
  GstElement *filter4 = NULL;
  GstElement *x264enc = NULL;
  GstElement *qtmux = NULL;
  GstCaps *caps3 = NULL, *caps4 = NULL;

  /* Check input arguments */
  if (argc != 2) {
    g_printerr ("Usage: %s <H264 filename>\n", argv[0]);
    return -1;
  }

  /* Standard GStreamer initialization */
  gst_init (&argc, &argv);
  loop = g_main_loop_new (NULL, FALSE);

  /* Create gstreamer elements */
  /* Create Pipeline element that will form a connection of other elements */
  pipeline = gst_pipeline_new ("dstest1-pipeline");

  /* Source element for reading from the file */
  source = gst_element_factory_make ("filesrc", "file-source");

  /* Since the data format in the input file is elementary h264 stream,
   * we need a h264parser */
  h264parser = gst_element_factory_make ("h264parse", "h264-parser");

  /* Use nvdec_h264 for hardware accelerated decode on GPU */
  decoder = gst_element_factory_make ("nvdec_h264", "nvh264-decoder");

  /* Use nvinfer to run inferencing on decoder's output,
   * behaviour of inferencing is set through config file */
  pgie = gst_element_factory_make ("nvinfer", "primary-nvinference-engine");

  /* Use convertor to convert from NV12 to RGBA as required by nvosd */
  nvvidconv = gst_element_factory_make ("nvvidconv", "nvvideo-converter");

  /* Create OSD to draw on the converted RGBA buffer */
  nvosd = gst_element_factory_make ("nvosd", "nv-onscreendisplay");

  nvvidconv1 = gst_element_factory_make("nvvidconv", "nvvideo-converter1");
  videoconvert = gst_element_factory_make("videoconvert", "converter");
  x264enc = gst_element_factory_make("x264enc", "h264 encoder");
  qtmux = gst_element_factory_make("qtmux", "muxer");

  /* Finally render the osd output */
  sink = gst_element_factory_make ("filesink", "filesink");

  /* caps filter for nvvidconv to convert NV12 to RGBA as nvosd expects input
   * in RGBA format */
  filter1 = gst_element_factory_make ("capsfilter", "filter1");
  filter2 = gst_element_factory_make ("capsfilter", "filter2");
  filter3 = gst_element_factory_make ("capsfilter", "filter3");
  filter4 = gst_element_factory_make ("capsfilter", "filter4");
  if (!pipeline || !source || !h264parser || !decoder || !pgie
      || !filter1 || !nvvidconv || !filter2 || !nvosd || !sink) {
    g_printerr ("One element could not be created. Exiting.\n");
    return -1;
  }

  if (!nvvidconv1 || !x264enc || !qtmux || !filter3 || !filter4) {
    g_printerr("one element could not be created. Exiting.\n");
    return -1;
  }

  /* we set the input filename to the source element */
  g_object_set (G_OBJECT (source), "location", argv[1], NULL);

  g_object_set(G_OBJECT(sink), "location", "out_test1.mp4", NULL);

  /* Set all the necessary properties of the nvinfer element,
   * the necessary ones are : */
  g_object_set (G_OBJECT (pgie),
      "config-file-path", "dstest1_pgie_config.txt", NULL);

  /* we set the osd properties here */
  g_object_set (G_OBJECT (nvosd), "font-size", 15, NULL);

  /* we add a message handler */
  bus = gst_pipeline_get_bus (GST_PIPELINE (pipeline));
  bus_watch_id = gst_bus_add_watch (bus, bus_call, loop);
  gst_object_unref (bus);

  /*
    ////////////////////////////////////////////////////////////////////
    // <1> Set up the pipeline by adding all the elements
    ////////////////////////////////////////////////////////////////////
    // TODO1
    // Hints:
    //     1> Some elements are missing from the pipeline. You can refer to the elements defined above
         to see which ones aren't currently incorporated.
         2> Think about the kind of data stream we're handling
    */

  gst_bin_add_many (GST_BIN (pipeline),
      source, h264parser, decoder, pgie,
      filter1, nvvidconv, filter2, nvosd, nvvidconv1, filter3,
      videoconvert, filter4, x264enc, qtmux, sink, NULL);

  caps1 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=NV12");
  g_object_set (G_OBJECT (filter1), "caps", caps1, NULL);
  gst_caps_unref (caps1);
  caps2 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=RGBA");
  g_object_set (G_OBJECT (filter2), "caps", caps2, NULL);
  gst_caps_unref (caps2);
  caps3 = gst_caps_from_string("video/x-raw, format=RGBA");
  g_object_set(G_OBJECT(filter3), "caps", caps3, NULL);
  gst_caps_unref(caps3);
  caps4 = gst_caps_from_string("video/x-raw, format=NV12");
  g_object_set(G_OBJECT(filter4), "caps", caps4, NULL);
  gst_caps_unref(caps4);
  

  /* we link the elements together */
  /* file-source -> h264-parser -> nvh264-decoder ->
   * nvinfer -> filter1 -> nvvidconv -> filter2 -> nvosd -> video-renderer */
  gst_element_link_many (source, h264parser, decoder, pgie, filter1,
      nvvidconv, filter2, nvosd, nvvidconv1, filter3,
      videoconvert, filter4,
      x264enc, qtmux, sink, NULL);

  /* Lets add probe to get informed of the meta data generated, we add probe to
   * the sink pad of the osd element, since by that time, the buffer would have
   * had got all the metadata. */
  osd_sink_pad = gst_element_get_static_pad (nvosd, "sink");
  if (!osd_sink_pad)
    g_print ("Unable to get sink pad\n");
  else {
    osd_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER, 
        osd_sink_pad_buffer_probe, NULL, NULL); 

    /* enable this for Performance Analysis Exercise */
   // perf_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER,
    //        sink_bin_buf_probe, NULL, NULL);
  }
 /*
    ////////////////////////////////////////////////////////////////////
    // <1> Set the pipeline state to actually render incoming data
    ////////////////////////////////////////////////////////////////////
    // TODO2
    // Hints:
    //   1> See https://gstreamer.freedesktop.org/documentation/plugin-development/basics/states.html
            to find the list of possible states
         2> We want to choose the state that allows us to send data all the way through
    */
  g_print ("Now playing: %s\n", argv[1]);
  gst_element_set_state (pipeline, GST_STATE_PLAYING);

  /* Wait till pipeline encounters an error or EOS */
  g_print ("Running...\n");
  g_main_loop_run (loop);

  /* Out of the main loop, clean up nicely */
  g_print ("Returned, stopping playback\n");

  /*
    ////////////////////////////////////////////////////////////////////
    // <1> Change the pipeline state to close devices and clean up
    ////////////////////////////////////////////////////////////////////
    // TODO2
    // Hints:
    //   1> See https://gstreamer.freedesktop.org/documentation/plugin-development/basics/states.html
            to find the list of possible states
         2> We want to choose the state that clears our resources.
    */
  
  gst_element_set_state (pipeline, GST_STATE_NULL);
  g_print ("Deleting pipeline\n");
  gst_object_unref (GST_OBJECT (pipeline));
  g_source_remove (bus_watch_id);
  g_main_loop_unref (loop);
  return 0;


}

"""

In [ ]:
!make -C DeepStream_Release/sources/apps/deepstream-test1 clean
!make -C DeepStream_Release/sources/apps/deepstream-test1/

!cd DeepStream_Release/sources/apps/deepstream-test1 && \
./deepstream-test1-app  ../../../samples/streams/sample_720p.h264

<a id='EXPECTED_OUTPUT-1'></a>
### Expected Output


<a id='CONSOLE_OUTPUT-1'></a>
##### <font color = '#76b900'>Console Output</font>
---
When you run the application, at each iteration, you should see the frame number, number of objects in the frame, vehicle count and person count. 

    .....
    make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
    rm -rf deepstream_test1_app.o deepstream-test1-app
    make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
    make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
    cc -I../../includes `pkg-config --cflags gstreamer-1.0`   -c -o deepstream_test1_app.o deepstream_test1_app.c
    cc -o deepstream-test1-app deepstream_test1_app.o `pkg-config --libs gstreamer-1.0`
    make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
    Now playing: ../../../samples/streams/sample_720p.h264
    >>> Generating new TRT model engine
    Using INT8 data type.

     ***** Storing serialized engine file as /dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1/../../../samples/models/Primary_Detector/resnet10.caffemodel_b1_int8.engine batchsize = 1 *****

    Running...
    End of stream
    Returned, stopping playback
    Deleting pipeline

<a id='DISPLAY_OUTPUT-1'></a>
##### <font color = '#76b900'>Display Output</font>
---
Check the output:

In [7]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="DeepStream_Release/sources/apps/deepstream-test1/out_test1.mp4" type="video/mp4">
    </video>
""".format())

In the output video, we can see green bounding boxes and class labels around detected cars and people. The number of detections in each frame of the video corresponds to the log output printed while the `deepstream-test1` application was running. What's controlling how many detections are made? 

<a id='change-config'></a>
 ### Changing the Configuration 

The ResNet model generates class prediction scores between 0 and 1 for each of the four classes; we must choose a threshold for the predictions to decide when we should apply the label for any given class. We can change many parameters in the configuration, but this one is critical to get results from our model. Let's see what happens to the output video if we increase our threshold for the prediction of our classes. 

Let's start fresh by removing our old compiled application and output. 

In [9]:
!make -C DeepStream_Release/sources/apps/deepstream-test1 clean

make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
rm -rf deepstream_test1_app.o deepstream-test1-app
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'


Now we can change the configuration and recompile our application. Open the configuration and update the element of `threshold` to be `0.8`. This will cange the threshold for all of the classes. Save the file, then remake the application with the code below. 

In [ ]:
"""
[property]
gpu-id=0
net-scale-factor=0.0039215697906911373
model-file=../../../samples/models/Primary_Detector/resnet10.caffemodel
proto-file=../../../samples/models/Primary_Detector/resnet10.prototxt
labelfile-path=../../../samples/models/Primary_Detector/labels.txt
int8-calib-file=../../../samples/models/Primary_Detector/cal_trt4.bin
batch-size=1
network-mode=1
num-detected-classes=4
interval=0
gie-unique-id=1
parse-func=4
output-blob-names=conv2d_bbox;conv2d_cov/Sigmoid

[class-attrs-all]
threshold=0.2
eps=0.2
group-threshold=1
"""

In [11]:
!make -C DeepStream_Release/sources/apps/deepstream-test1/

make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
cc -I../../includes `pkg-config --cflags gstreamer-1.0`   -c -o deepstream_test1_app.o deepstream_test1_app.c
cc -o deepstream-test1-app deepstream_test1_app.o `pkg-config --libs gstreamer-1.0`
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'


With a higher threshold for predicting our classes, we would expect to see fewer detections. Let's see how this plays out when we run the application.

In [12]:
!cd DeepStream_Release/sources/apps/deepstream-test1 && \
./deepstream-test1-app  ../../../samples/streams/sample_720p.h264

Now playing: ../../../samples/streams/sample_720p.h264
>>> Generating new TRT model engine
Using INT8 data type.

 ***** Storing serialized engine file as /dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1/../../../samples/models/Primary_Detector/resnet10.caffemodel_b1_int8.engine batchsize = 1 *****

Running...
Frame Number = 0 Number of objects = 1 Vehicle Count = 0 Person Count = 1
Frame Number = 1 Number of objects = 1 Vehicle Count = 0 Person Count = 1
Frame Number = 2 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 3 Number of objects = 1 Vehicle Count = 0 Person Count = 1
Frame Number = 4 Number of objects = 2 Vehicle Count = 1 Person Count = 1
Frame Number = 5 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 6 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 7 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 8 Number of objects = 1 Vehicle Count = 0 Person Count = 

Frame Number = 106 Number of objects = 3 Vehicle Count = 1 Person Count = 2
Frame Number = 107 Number of objects = 2 Vehicle Count = 0 Person Count = 2
Frame Number = 108 Number of objects = 3 Vehicle Count = 1 Person Count = 2
Frame Number = 109 Number of objects = 2 Vehicle Count = 0 Person Count = 2
Frame Number = 110 Number of objects = 2 Vehicle Count = 0 Person Count = 2
Frame Number = 111 Number of objects = 3 Vehicle Count = 1 Person Count = 2
Frame Number = 112 Number of objects = 3 Vehicle Count = 1 Person Count = 2
Frame Number = 113 Number of objects = 2 Vehicle Count = 0 Person Count = 2
Frame Number = 114 Number of objects = 2 Vehicle Count = 1 Person Count = 1
Frame Number = 115 Number of objects = 3 Vehicle Count = 1 Person Count = 2
Frame Number = 116 Number of objects = 2 Vehicle Count = 1 Person Count = 1
Frame Number = 117 Number of objects = 2 Vehicle Count = 1 Person Count = 1
Frame Number = 118 Number of objects = 2 Vehicle Count = 1 Person Count = 1
Frame Number

Frame Number = 215 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 216 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 217 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 218 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 219 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 220 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 221 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 222 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 223 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 224 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 225 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 226 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 227 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number

Frame Number = 323 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 324 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 325 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 326 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 327 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 328 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 329 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 330 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 331 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 332 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 333 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 334 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 335 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number

Frame Number = 432 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 433 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 434 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 435 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 436 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 437 Number of objects = 3 Vehicle Count = 3 Person Count = 0
Frame Number = 438 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 439 Number of objects = 3 Vehicle Count = 3 Person Count = 0
Frame Number = 440 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 441 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 442 Number of objects = 3 Vehicle Count = 3 Person Count = 0
Frame Number = 443 Number of objects = 3 Vehicle Count = 3 Person Count = 0
Frame Number = 444 Number of objects = 3 Vehicle Count = 3 Person Count = 0
Frame Number

...

Frame Number = 978 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 979 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 980 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 981 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 982 Number of objects = 5 Vehicle Count = 4 Person Count = 1
Frame Number = 983 Number of objects = 4 Vehicle Count = 3 Person Count = 1
Frame Number = 984 Number of objects = 5 Vehicle Count = 4 Person Count = 1
Frame Number = 985 Number of objects = 5 Vehicle Count = 4 Person Count = 1
Frame Number = 986 Number of objects = 5 Vehicle Count = 4 Person Count = 1
Frame Number = 987 Number of objects = 5 Vehicle Count = 4 Person Count = 1
Frame Number = 988 Number of objects = 5 Vehicle Count = 4 Person Count = 1
Frame Number = 989 Number of objects = 6 Vehicle Count = 3 Person Count = 3
Frame Number = 990 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number

Frame Number = 1088 Number of objects = 3 Vehicle Count = 1 Person Count = 2
Frame Number = 1089 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1090 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1091 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1092 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1093 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1094 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1095 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1096 Number of objects = 3 Vehicle Count = 2 Person Count = 1
Frame Number = 1097 Number of objects = 2 Vehicle Count = 1 Person Count = 1
Frame Number = 1098 Number of objects = 3 Vehicle Count = 1 Person Count = 2
Frame Number = 1099 Number of objects = 3 Vehicle Count = 2 Person Count = 1
Frame Number = 1100 Number of objects = 3 Vehicle Count = 1 Person Count = 2

Frame Number = 1198 Number of objects = 1 Vehicle Count = 0 Person Count = 1
Frame Number = 1199 Number of objects = 2 Vehicle Count = 1 Person Count = 1
Frame Number = 1200 Number of objects = 1 Vehicle Count = 0 Person Count = 1
Frame Number = 1201 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1202 Number of objects = 1 Vehicle Count = 0 Person Count = 1
Frame Number = 1203 Number of objects = 1 Vehicle Count = 0 Person Count = 1
Frame Number = 1204 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1205 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1206 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1207 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 1208 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1209 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 1210 Number of objects = 1 Vehicle Count = 1 Person Count = 0

Frame Number = 1306 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 1307 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 1308 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1309 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1310 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1311 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1312 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1313 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1314 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1315 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1316 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1317 Number of objects = 0 Vehicle Count = 0 Person Count = 0
Frame Number = 1318 Number of objects = 0 Vehicle Count = 0 Person Count = 0

Frame Number = 1415 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 1416 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 1417 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 1418 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 1419 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 1420 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 1421 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 1422 Number of objects = 3 Vehicle Count = 3 Person Count = 0
Frame Number = 1423 Number of objects = 3 Vehicle Count = 3 Person Count = 0
Frame Number = 1424 Number of objects = 3 Vehicle Count = 3 Person Count = 0
Frame Number = 1425 Number of objects = 2 Vehicle Count = 2 Person Count = 0
Frame Number = 1426 Number of objects = 1 Vehicle Count = 1 Person Count = 0
Frame Number = 1427 Number of objects = 1 Vehicle Count = 1 Person Count = 0

In [13]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="DeepStream_Release/sources/apps/deepstream-test1/out_test1.mp4" type="video/mp4">
    </video>
""".format())

Right away, it is clear we are detecting fewer cars and people. In the printed output, we can see fewer detections of our classes in almost every single frame. In the video output, we see fewer green bounding boxes around cars and people. 

With just a simple tweak to a configuration parameter, DeepStream lets us interact with our deep learning model and get very different results. 

<a id='build-mdnn'></a>
## 5. Build A Multi-DNN Application  

In this section, we will incorporate object tracking, cascaded inferencing, and metadata handling by adding more neural networks to the pipeline. DeepStream makes it easy to build a relatively complex solution with only a few, simple additional steps. 

<a id='PIPELINE-2'></a> 
### 5.1 Pipeline 

Below, we can explore the architecture diagram of the application. Here, we have 3 additional models that identify car color, make and type respectively. Plugging in additional models is like adding the original classifier, however there are configuration considerations that we are going to explore later in this section.

<img src='images/Lab2_pipeline.png' style='width:80%'/> 

<p style="text-align: center;color:gray">Figure 13. deepstream-test2 pipeline</p>  

You should notice that, while there is more going on than the previous pipeline, the plugins are generally the same. We still need to use `NvDec`, `NvInver`, `NvOSD`, and most of the other components. We are using a new plugin though. After the first NvInfer component, we add the **NvTracker** component to track the objects and generate unique-ids for them.  

#### NvTracker  element 

The `NvTracker  ` plugin operates on Luma data and tracks detected objects and gives each new object a unique ID. 

```c 
  /* We need to have a tracker to track the identified objects */ 
  nvtracker = gst_element_factory_make ("nvtracker", "tracker"); 
``` 

The plugin accepts NV12/RGBA data from the upstream component and scales (converts) the input buffer to a Luma buffer with a specific tracker width and height. (Tracker width and height must be specified in the configuration file's [tracker] section.) 

The low-level library uses a CPU based implementation of the __Kanade Lucas Tomasi (KLT)__ tracker algorithm. The plugin also supports the Intersection of Union (IoU) tracker algorithm, which uses the intersection of the detector’s bounding boxes across frames to determine the object's unique ID. 

<br /> 
<img src='images/tracker.jpg'/> 
<p style="text-align: center;color:gray">Figure 14. The nvtracker plugin</p> 

The tracker component updates the object’s metadata with a tracker-id. After this component, we add three cascaded secondary neural network classifiers. These classifiers work on the objects detected as “vehicles or cars”. The first classifier classifies the car color. The second classifier classifies the car make, and the third classifier classifies car type (e.g. coupe, sedan, etc.). Each classifier, after inference on a car object, will append the metadata to their results. Then, the application, using a callback function, can access the metadata to understand and analyze the attributes of the objects. 

<a id='CODE_WALK-THROUGH-2'></a> 
### 5.2 Application code walk-through 

##### <font color = '#76b900'>Creation of Elements & Linking</font> 
--- 

Earlier, we composed a pipeline by creating the elements and adding them to the pipeline. In this example, we create a tracker element and 3 additional NvInfer elements which serve as secondary classifiers. We configure them with appropriate network parameters as we did in the first example.  

<a id='new-config'></a>
 ### 5.3 New Configuration Parameters 

Because these secondary classifiers are only intended to execute on objects that we believe are vehicles, we will need to add new configuration parameters to generate this behavior. 

Two new parameters, __operate-on-gie-id__ and __operate-on-class-ids__ will let us control this behavior. 

The first, __operate-on-gie-id__, lets us configure a classifier to only execute on objects from a different classifier. In this case, we will configure the secondary classifier to only execute on objects detected by the primary classifier. The second, __operate-on-class-ids__, lets us configure a classifier to only execute on objects __of a specific class__. By combining these two, our secondary classifiers will be configured to only evaluate the make, model, and color of objects classified as cars by our primary model. 

Open up the configuration file for the first secondary classifier and create __operate-on-gie-id__ and __operate-on-class-ids__ parameters. Set __operate-on-gie-id__ equal to 1, telling the classifier to execute on objects from the first detector network. Set __operate-on-class-ids__ equal to 0, telling the classifier to execute only when the `class_id` is 0, corresponding to the `vehicle` class. 

In [ ]:
"""
[property]
gpu-id=0
net-scale-factor=1
model-file=../../../samples/models/Secondary_CarColor/resnet18.caffemodel
proto-file=../../../samples/models/Secondary_CarColor/resnet18.prototxt
mean-file=../../../samples/models/Secondary_CarColor/mean.ppm
labelfile-path=../../../samples/models/Secondary_CarColor/labels.txt
int8-calib-file=../../../samples/models/Secondary_CarColor/cal_trt4.bin
batch-size=16
# 0=FP32 and 1=INT8 mode
network-mode=1
input-object-min-width=64
input-object-min-height=64
model-color-format=1
gpu-id=0
gie-unique-id=2
operate-on-gie-id=1
operate-on-class-ids=0
is-classifier=1
output-blob-names=predictions/Softmax
classifier-async-mode=1
classifier-threshold=0.51
gie-mode=2

"""


After adding the two new configuration parameters and saving the file, the next step is to compile and run the application.

--- 

### TODO TASKS

In [ ]:
"""

/*
 * Copyright (c) 2018 NVIDIA Corporation.  All rights reserved.
 *
 * NVIDIA Corporation and its licensors retain all intellectual property
 * and proprietary rights in and to this software, related documentation
 * and any modifications thereto.  Any use, reproduction, disclosure or
 * distribution of this software and related documentation without an express
 * license agreement from NVIDIA Corporation is strictly prohibited.
 *
 */

#include <gst/gst.h>
#include <glib.h>

#include "gstnvdsmeta.h"

#define PGIE_CONFIG_FILE  "dstest2_pgie_config.txt"
#define SGIE1_CONFIG_FILE "dstest2_sgie1_config.txt"
#define SGIE2_CONFIG_FILE "dstest2_sgie2_config.txt"
#define SGIE3_CONFIG_FILE "dstest2_sgie3_config.txt"
#define MAX_DISPLAY_LEN 64

#define PGIE_CLASS_ID_VEHICLE 0
#define PGIE_CLASS_ID_PERSON 2


/* These are the strings of the labels for the respective models */
gchar sgie1_classes_str[12][32] = { "black", "blue", "brown", "gold", "green",
  "grey", "maroon", "orange", "red", "silver", "white", "yellow"
};

gchar sgie2_classes_str[20][32] =
    { "Acura", "Audi", "BMW", "Chevrolet", "Chrysler",
  "Dodge", "Ford", "GMC", "Honda", "Hyundai", "Infiniti", "Jeep", "Kia",
      "Lexus", "Mazda", "Mercedes", "Nissan",
  "Subaru", "Toyota", "Volkswagen"
};

gchar sgie3_classes_str[6][32] = { "coupe", "largevehicle", "sedan", "suv",
  "truck", "van"
};

gchar pgie_classes_str[4][32] =
    { "Vehicle", "TwoWheeler", "Person", "RoadSign" };

/* gie_unique_id is one of the properties in the above dstest2_sgiex_config.txt
 * files. These should be unique and known when we want to parse the Metadata
 * respective to the sgie labels. Ideally these should be read from the config
 * files but for brevity we ensure they are same. */

guint sgie1_unique_id = 2;
guint sgie2_unique_id = 3;
guint sgie3_unique_id = 4;

/* This is the buffer probe function that we have registered on the sink pad
 * of the OSD element. All the infer elements in the pipeline shall attach
 * their metadata to the GstBuffer, here we will iterate & process the metadata
 * forex: class ids to strings, counting of class_id objects etc. */
static GstPadProbeReturn
osd_sink_pad_buffer_probe (GstPad * pad, GstPadProbeInfo * info,
    gpointer u_data)
{
  GstMeta *gst_meta = NULL;
  NvDsMeta *nvdsmeta = NULL;
  gpointer state = NULL;
  static GQuark _nvdsmeta_quark = 0;
  GstBuffer *buf = (GstBuffer *) info->data;
  NvDsFrameMeta *frame_meta = NULL;
  guint num_rects = 0, rect_index = 0, l_index = 0;
  NvDsObjectParams *obj_meta = NULL;
  guint i = 0;
  gint sgie1_class_id = -1;
  NvDsAttrInfo *sgie1_attrs = NULL;
  gint sgie2_class_id = -1;
  NvDsAttrInfo *sgie2_attrs = NULL;
  gint sgie3_class_id = -1;
  NvDsAttrInfo *sgie3_attrs = NULL;
  NvOSD_TextParams *txt_params = NULL;
  guint tracking_id = 0;
  guint vehicle_count = 0;
  guint person_count = 0;
  static guint frame_number = 0;

  if (!_nvdsmeta_quark)
    _nvdsmeta_quark = g_quark_from_static_string (NVDS_META_STRING);

  while ((gst_meta = gst_buffer_iterate_meta (buf, &state))) {
    if (gst_meta_api_type_has_tag (gst_meta->info->api, _nvdsmeta_quark)) {

      nvdsmeta = (NvDsMeta *) gst_meta;

      /* We are interested only in intercepting Meta of type
       * "NVDS_META_FRAME_INFO" as they are from our infer elements. */
      if (nvdsmeta->meta_type == NVDS_META_FRAME_INFO) {
        frame_meta = (NvDsFrameMeta *) nvdsmeta->meta_data;
        if (frame_meta == NULL) {
          g_print ("NVDS Meta contained NULL meta \n");
          return GST_PAD_PROBE_OK;
        }

        /* We reset the num_strings here as we plan to iterate through the
         *  the detected objects and form our own strings by mapping the sgie
         *  class id label & its label string. The pipeline generated strings
         *  shall be discarded.
         */
        frame_meta->num_strings = 0;

        num_rects = frame_meta->num_rects;
        /* This means we have num_rects in frame_meta->obj_params,
         * now lets iterate through them */

        for (rect_index = 0; rect_index < num_rects; rect_index++) {

          /* Reset class string indexes per object detected */
          sgie1_class_id = -1;
          sgie2_class_id = -1;
          sgie3_class_id = -1;

          obj_meta = (NvDsObjectParams *) & frame_meta->obj_params[rect_index];
      /*
        ////////////////////////////////////////////////////////////////////
        // <2> Correctly add to the count of vehicles and people in a frame
        ////////////////////////////////////////////////////////////////////
        // TODO2
        // Hints:
        //   1> There are four classes, so class_id ranges from 0 to 3.
             2> We defined two of them as constants at the top of this file. 
        */

          if (obj_meta->class_id == FIXME)
            vehicle_count++;
          if (obj_meta->class_id == FIXME)
            person_count++;

          /* Now for each of the obj_meta, we iterate through the attr_infos.
           * gie_unique_id of the sgie instance should be known and it is
           * the index into the obj_meta->attr_info */
            
                
          sgie1_attrs = &(obj_meta->attr_info[sgie1_unique_id]);
          sgie2_attrs = &(obj_meta->attr_info[sgie2_unique_id]);
          sgie3_attrs = &(obj_meta->attr_info[sgie3_unique_id]);
            

          /* Our classifiers are single-class classifiers, hence num_attrs
           * should always be 1, for multi-class secondary classifiers, we
           * would have to iterate through the attr_info to get the respective
           * strings. */
            
          if (sgie1_attrs->num_attrs)
            sgie1_class_id = sgie1_attrs->attrs[0].attr_val;

          if (sgie2_attrs->num_attrs)
            sgie2_class_id = sgie2_attrs->attrs[0].attr_val;

          if (sgie3_attrs->num_attrs)
            sgie3_class_id = sgie3_attrs->attrs[0].attr_val;
            

          tracking_id = obj_meta->tracking_id;

          /* Now using above information we need to form a text that should
           * be displayed on top of the bounding box, so lets form it here.
           * We shall free any previously generated text by the pipeline, hence
           * free it first. */

          txt_params = &(obj_meta->text_params);
          if (txt_params->display_text)
            g_free (txt_params->display_text);

          txt_params->display_text = g_malloc0 (MAX_DISPLAY_LEN);

          g_snprintf (txt_params->display_text, MAX_DISPLAY_LEN, "%s %d",
              pgie_classes_str[obj_meta->class_id], tracking_id);
            

          if (sgie1_class_id != -1) {
            g_strlcat (txt_params->display_text, ": ", MAX_DISPLAY_LEN);
            g_strlcat (txt_params->display_text,
                sgie1_classes_str[sgie1_class_id], MAX_DISPLAY_LEN);
          }
            

          if (sgie2_class_id != -1) {
            g_strlcat (txt_params->display_text, ": ", MAX_DISPLAY_LEN);
            g_strlcat (txt_params->display_text,
                sgie2_classes_str[sgie2_class_id], MAX_DISPLAY_LEN);
          }

          if (sgie3_class_id != -1) {
            g_strlcat (txt_params->display_text, ": ", MAX_DISPLAY_LEN);
            g_strlcat (txt_params->display_text,
                sgie3_classes_str[sgie3_class_id], MAX_DISPLAY_LEN);
          }
                

          /* Now set the offsets where the string should appear */
          txt_params->x_offset = obj_meta->rect_params.left;
          txt_params->y_offset = obj_meta->rect_params.top;

          /* Font , font-color and font-size */
          txt_params->font_params.font_name = "Arial";
          txt_params->font_params.font_size = 12;
          txt_params->font_params.font_color.red = 1.0;
          txt_params->font_params.font_color.green = 1.0;
          txt_params->font_params.font_color.blue = 1.0;
          txt_params->font_params.font_color.alpha = 1.0;

          /* Text background color */
          txt_params->set_bg_clr = 1;
          txt_params->text_bg_clr.red = 0.0;
          txt_params->text_bg_clr.green = 0.0;
          txt_params->text_bg_clr.blue = 0.0;
          txt_params->text_bg_clr.alpha = 1.0;

          frame_meta->num_strings++;
        }
        g_print ("Frame Number = %d Number of objects = %d"
            " Vehicle Count = %d Person Count = %d\n",
            frame_number, num_rects, vehicle_count, person_count);
      }
    }
  }
  frame_number++;
  return GST_PAD_PROBE_OK;
}

static gboolean
bus_call (GstBus * bus, GstMessage * msg, gpointer data)
{
  GMainLoop *loop = (GMainLoop *) data;
  switch (GST_MESSAGE_TYPE (msg)) {
    case GST_MESSAGE_EOS:
      g_print ("End of stream\n");
      g_main_loop_quit (loop);
      break;
    case GST_MESSAGE_ERROR:{
      gchar *debug;
      GError *error;
      gst_message_parse_error (msg, &error, &debug);
      if (debug)
        g_free (debug);
      g_printerr ("Error: %s\n", error->message);
      g_error_free (error);
      g_main_loop_quit (loop);
      break;
    }
    default:
      break;
  }
  return TRUE;
}

int
main (int argc, char *argv[])
{
  GMainLoop *loop = NULL;
  GstElement *pipeline = NULL, *source = NULL, *h264parser = NULL,
      *decoder = NULL, *sink = NULL, *pgie = NULL, *nvvidconv = NULL,
      *nvosd = NULL, *filter1 = NULL, *filter2 = NULL,
      *sgie1 = NULL, *sgie2 = NULL, *sgie3 = NULL, *nvtracker = NULL;
  GstBus *bus = NULL;
  guint bus_watch_id = 0;
  GstCaps *caps1 = NULL, *caps2 = NULL;
  GstPad *osd_sink_pad = NULL;
  gulong osd_probe_id = 0;

  GstElement *nvvidconv1 = NULL;
  GstElement *filter3 = NULL;
  GstElement *videoconvert = NULL;
  GstElement *filter4 = NULL;
  GstElement *x264enc = NULL;
  GstElement *qtmux = NULL;
  GstCaps *caps3 = NULL, *caps4 = NULL;

  /* Check input arguments */
  if (argc != 2) {
    g_printerr ("Usage: %s <elementary H264 filename>\n", argv[0]);
    return -1;
  }

  /* Standard GStreamer initialization */
  gst_init (&argc, &argv);
  loop = g_main_loop_new (NULL, FALSE);

  /* Create gstreamer elements */

  /* Create Pipeline element that will be a container of other elements */
  pipeline = gst_pipeline_new ("dstest2-pipeline");

  /* Source element for reading from the file */
  source = gst_element_factory_make ("filesrc", "file-source");

  /* Since the data format in the input file is elementary h264 stream,
   * we need a h264parser */
  h264parser = gst_element_factory_make ("h264parse", "h264-parser");

  /* Use nvdec_h264 for hardware accelerated decode on GPU */
  decoder = gst_element_factory_make ("nvdec_h264", "nvh264-decoder");

  /* Use nvinfer to run inferencing on decoder's output,
   * behaviour of inferencing is set through config file */
  pgie = gst_element_factory_make ("nvinfer", "primary-nvinference-engine");

  /* We need to have a tracker to track the identified objects */
  nvtracker = gst_element_factory_make ("nvtracker", "tracker");

  /* We need three secondary gies so lets create 3 more instances of
     nvinfer */
  sgie1 = gst_element_factory_make ("nvinfer", "secondary1-nvinference-engine");

  sgie2 = gst_element_factory_make ("nvinfer", "secondary2-nvinference-engine");

  sgie3 = gst_element_factory_make ("nvinfer", "secondary3-nvinference-engine");

  /* Use convertor to convert from NV12 to RGBA as required by nvosd */
  nvvidconv = gst_element_factory_make ("nvvidconv", "nvvideo-converter");

  /* Create OSD to draw on the converted RGBA buffer */
  nvosd = gst_element_factory_make ("nvosd", "nv-onscreendisplay");

  nvvidconv1 = gst_element_factory_make("nvvidconv", "nvvideo-converter1");
  videoconvert = gst_element_factory_make("videoconvert", "converter");
  x264enc = gst_element_factory_make("x264enc", "h264 encoder");
  qtmux = gst_element_factory_make("qtmux", "muxer");

  /* Finally render the osd output */
  sink = gst_element_factory_make ("filesink", "filesink");


  /* caps filter for nvvidconv to convert NV12 to RGBA as nvosd expects input
   * in RGBA format */
  filter1 = gst_element_factory_make ("capsfilter", "filter1");
  filter2 = gst_element_factory_make ("capsfilter", "filter2");
  filter3 = gst_element_factory_make ("capsfilter", "filter3");
  filter4 = gst_element_factory_make ("capsfilter", "filter4");
  if (!pipeline || !source || !h264parser || !decoder || !pgie
      || !filter1 || !nvvidconv || !filter2 || !nvosd || !sink) {
    g_printerr ("One element could not be created. Exiting.\n");
    return -1;
  }

  if (!nvvidconv1 || !x264enc || !qtmux || !filter3 || !filter4) {
    g_printerr("one element could not be created. Exiting.\n");
    return -1;
  }

  /* Set the input filename to the source element */
  g_object_set (G_OBJECT (source), "location", argv[1], NULL);

  g_object_set(G_OBJECT(sink), "location", "out_test2_app.mp4", NULL);

  g_object_set (G_OBJECT (nvosd), "font-size", 15, NULL);

  /*
    ////////////////////////////////////////////////////////////////////
    // <1> Set up all the necessary proprties of the nvinfer element
    ////////////////////////////////////////////////////////////////////
    // TODO1
    // Hints:
    //   1> We need to define properties for each of the four classifiers:
            the primary classifiers, and the three secondary ones.
         2> We need to supply both the elements and the configuration files, which we defined
            as constants at the top of the file.
    */

  g_object_set (G_OBJECT (pgie), "config-file-path", FIXME, NULL);
  g_object_set (G_OBJECT (sgie1), "config-file-path", FIXME, NULL);
  g_object_set (G_OBJECT (sgie2), "config-file-path", FIXME, NULL);
  g_object_set (G_OBJECT (sgie3), "config-file-path", FIXME, NULL);


  /* we add a message handler */
  bus = gst_pipeline_get_bus (GST_PIPELINE (pipeline));
  bus_watch_id = gst_bus_add_watch (bus, bus_call, loop);
  gst_object_unref (bus);


  /* Set up the pipeline */
  /* we add all elements into the pipeline */
  /* decoder | pgie | nvtracker | sgie1 | sgie2 | sgie3 | etc.. */

    
gst_bin_add_many (GST_BIN (pipeline),
      source, h264parser, decoder, pgie, nvtracker, sgie1, sgie2, sgie3,
      filter1, nvvidconv, filter2, nvosd, nvvidconv1, filter3,
      videoconvert, filter4, x264enc, qtmux, sink, NULL);

  caps1 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=NV12");
  g_object_set (G_OBJECT (filter1), "caps", caps1, NULL);
  gst_caps_unref (caps1);
  caps2 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=RGBA");
  g_object_set (G_OBJECT (filter2), "caps", caps2, NULL);
  gst_caps_unref (caps2);
  caps3 = gst_caps_from_string("video/x-raw, format=RGBA");
  g_object_set(G_OBJECT(filter3), "caps", caps3, NULL);
  gst_caps_unref(caps3);
  caps4 = gst_caps_from_string("video/x-raw, format=NV12");
  g_object_set(G_OBJECT(filter4), "caps", caps4, NULL);
  gst_caps_unref(caps4);


  /* Link the elements together */

    gst_element_link_many (source, h264parser, decoder, pgie, nvtracker, sgie1, sgie2, sgie3, filter1,
      nvvidconv, filter2, nvosd, nvvidconv1, filter3,
      videoconvert, filter4,
      x264enc, qtmux, sink, NULL);


  /* Lets add probe to get informed of the meta data generated, we add probe to
   * the sink pad of the osd element, since by that time, the buffer would have
   * had got all the metadata. */
  osd_sink_pad = gst_element_get_static_pad (nvosd, "sink");
  if (!osd_sink_pad)
    g_print ("Unable to get sink pad\n");
  else
    osd_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER,
        osd_sink_pad_buffer_probe, NULL, NULL);

  /* Set the pipeline to "playing" state */
  g_print ("Now playing: %s\n", argv[1]);
  gst_element_set_state (pipeline, GST_STATE_PLAYING);

  /* Iterate */
  g_print ("Running...\n");
  g_main_loop_run (loop);

  /* Out of the main loop, clean up nicely */
  g_print ("Returned, stopping playback\n");
  gst_element_set_state (pipeline, GST_STATE_NULL);
  g_print ("Deleting pipeline\n");
  gst_object_unref (GST_OBJECT (pipeline));
  g_source_remove (bus_watch_id);
  g_main_loop_unref (loop);
  return 0;
}

"""

### Solution

In [ ]:
"""
#include <gst/gst.h>
#include <glib.h>

#include "gstnvdsmeta.h"

#define PGIE_CONFIG_FILE  "dstest2_pgie_config.txt"
#define SGIE1_CONFIG_FILE "dstest2_sgie1_config.txt"
#define SGIE2_CONFIG_FILE "dstest2_sgie2_config.txt"
#define SGIE3_CONFIG_FILE "dstest2_sgie3_config.txt"
#define MAX_DISPLAY_LEN 64

#define PGIE_CLASS_ID_VEHICLE 0
#define PGIE_CLASS_ID_PERSON 2


/* These are the strings of the labels for the respective models */
gchar sgie1_classes_str[12][32] = { "black", "blue", "brown", "gold", "green",
  "grey", "maroon", "orange", "red", "silver", "white", "yellow"
};

gchar sgie2_classes_str[20][32] =
    { "Acura", "Audi", "BMW", "Chevrolet", "Chrysler",
  "Dodge", "Ford", "GMC", "Honda", "Hyundai", "Infiniti", "Jeep", "Kia",
      "Lexus", "Mazda", "Mercedes", "Nissan",
  "Subaru", "Toyota", "Volkswagen"
};

gchar sgie3_classes_str[6][32] = { "coupe", "largevehicle", "sedan", "suv",
  "truck", "van"
};

gchar pgie_classes_str[4][32] =
    { "Vehicle", "TwoWheeler", "Person", "RoadSign" };

/* gie_unique_id is one of the properties in the above dstest2_sgiex_config.txt
 * files. These should be unique and known when we want to parse the Metadata
 * respective to the sgie labels. Ideally these should be read from the config
 * files but for brevity we ensure they are same. */

guint sgie1_unique_id = 2;
guint sgie2_unique_id = 3;
guint sgie3_unique_id = 4;

/* This is the buffer probe function that we have registered on the sink pad
 * of the OSD element. All the infer elements in the pipeline shall attach
 * their metadata to the GstBuffer, here we will iterate & process the metadata
 * forex: class ids to strings, counting of class_id objects etc. */
static GstPadProbeReturn
osd_sink_pad_buffer_probe (GstPad * pad, GstPadProbeInfo * info,
    gpointer u_data)
{
  GstMeta *gst_meta = NULL;
  NvDsMeta *nvdsmeta = NULL;
  gpointer state = NULL;
  static GQuark _nvdsmeta_quark = 0;
  GstBuffer *buf = (GstBuffer *) info->data;
  NvDsFrameMeta *frame_meta = NULL;
  guint num_rects = 0, rect_index = 0, l_index = 0;
  NvDsObjectParams *obj_meta = NULL;
  guint i = 0;
  gint sgie1_class_id = -1;
  NvDsAttrInfo *sgie1_attrs = NULL;
  gint sgie2_class_id = -1;
  NvDsAttrInfo *sgie2_attrs = NULL;
  gint sgie3_class_id = -1;
  NvDsAttrInfo *sgie3_attrs = NULL;
  NvOSD_TextParams *txt_params = NULL;
  guint tracking_id = 0;
  guint vehicle_count = 0;
  guint person_count = 0;
  static guint frame_number = 0;

  if (!_nvdsmeta_quark)
    _nvdsmeta_quark = g_quark_from_static_string (NVDS_META_STRING);

  while ((gst_meta = gst_buffer_iterate_meta (buf, &state))) {
    if (gst_meta_api_type_has_tag (gst_meta->info->api, _nvdsmeta_quark)) {

      nvdsmeta = (NvDsMeta *) gst_meta;

      /* We are interested only in intercepting Meta of type
       * "NVDS_META_FRAME_INFO" as they are from our infer elements. */
      if (nvdsmeta->meta_type == NVDS_META_FRAME_INFO) {
        frame_meta = (NvDsFrameMeta *) nvdsmeta->meta_data;
        if (frame_meta == NULL) {
          g_print ("NVDS Meta contained NULL meta \n");
          return GST_PAD_PROBE_OK;
        }

        /* We reset the num_strings here as we plan to iterate through the
         *  the detected objects and form our own strings by mapping the sgie
         *  class id label & its label string. The pipeline generated strings
         *  shall be discarded.
         */
        frame_meta->num_strings = 0;

        num_rects = frame_meta->num_rects;
        /* This means we have num_rects in frame_meta->obj_params,
         * now lets iterate through them */

        for (rect_index = 0; rect_index < num_rects; rect_index++) {

          /* Reset class string indexes per object detected */
          sgie1_class_id = -1;
          sgie2_class_id = -1;
          sgie3_class_id = -1;

          obj_meta = (NvDsObjectParams *) & frame_meta->obj_params[rect_index];
      /*
        ////////////////////////////////////////////////////////////////////
        // <2> Correctly add to the count of vehicles and people in a frame
        ////////////////////////////////////////////////////////////////////
        // TODO2
        // Hints:
        //   1> There are four classes, so class_id ranges from 0 to 3.
             2> We defined two of them as constants at the top of this file. 
        */

          if (obj_meta->class_id == PGIE_CLASS_ID_VEHICLE)
            vehicle_count++;
          if (obj_meta->class_id == PGIE_CLASS_ID_PERSON)
            person_count++;

          /* Now for each of the obj_meta, we iterate through the attr_infos.
           * gie_unique_id of the sgie instance should be known and it is
           * the index into the obj_meta->attr_info */
            
                
          sgie1_attrs = &(obj_meta->attr_info[sgie1_unique_id]);
          sgie2_attrs = &(obj_meta->attr_info[sgie2_unique_id]);
          sgie3_attrs = &(obj_meta->attr_info[sgie3_unique_id]);
            

          /* Our classifiers are single-class classifiers, hence num_attrs
           * should always be 1, for multi-class secondary classifiers, we
           * would have to iterate through the attr_info to get the respective
           * strings. */
            
          if (sgie1_attrs->num_attrs)
            sgie1_class_id = sgie1_attrs->attrs[0].attr_val;

          if (sgie2_attrs->num_attrs)
            sgie2_class_id = sgie2_attrs->attrs[0].attr_val;

          if (sgie3_attrs->num_attrs)
            sgie3_class_id = sgie3_attrs->attrs[0].attr_val;
            

          tracking_id = obj_meta->tracking_id;

          /* Now using above information we need to form a text that should
           * be displayed on top of the bounding box, so lets form it here.
           * We shall free any previously generated text by the pipeline, hence
           * free it first. */

          txt_params = &(obj_meta->text_params);
          if (txt_params->display_text)
            g_free (txt_params->display_text);

          txt_params->display_text = g_malloc0 (MAX_DISPLAY_LEN);

          g_snprintf (txt_params->display_text, MAX_DISPLAY_LEN, "%s %d",
              pgie_classes_str[obj_meta->class_id], tracking_id);
            

          if (sgie1_class_id != -1) {
            g_strlcat (txt_params->display_text, ": ", MAX_DISPLAY_LEN);
            g_strlcat (txt_params->display_text,
                sgie1_classes_str[sgie1_class_id], MAX_DISPLAY_LEN);
          }
            

          if (sgie2_class_id != -1) {
            g_strlcat (txt_params->display_text, ": ", MAX_DISPLAY_LEN);
            g_strlcat (txt_params->display_text,
                sgie2_classes_str[sgie2_class_id], MAX_DISPLAY_LEN);
          }

          if (sgie3_class_id != -1) {
            g_strlcat (txt_params->display_text, ": ", MAX_DISPLAY_LEN);
            g_strlcat (txt_params->display_text,
                sgie3_classes_str[sgie3_class_id], MAX_DISPLAY_LEN);
          }
                

          /* Now set the offsets where the string should appear */
          txt_params->x_offset = obj_meta->rect_params.left;
          txt_params->y_offset = obj_meta->rect_params.top;

          /* Font , font-color and font-size */
          txt_params->font_params.font_name = "Arial";
          txt_params->font_params.font_size = 12;
          txt_params->font_params.font_color.red = 1.0;
          txt_params->font_params.font_color.green = 1.0;
          txt_params->font_params.font_color.blue = 1.0;
          txt_params->font_params.font_color.alpha = 1.0;

          /* Text background color */
          txt_params->set_bg_clr = 1;
          txt_params->text_bg_clr.red = 0.0;
          txt_params->text_bg_clr.green = 0.0;
          txt_params->text_bg_clr.blue = 0.0;
          txt_params->text_bg_clr.alpha = 1.0;

          frame_meta->num_strings++;
        }
        g_print ("Frame Number = %d Number of objects = %d"
            " Vehicle Count = %d Person Count = %d\n",
            frame_number, num_rects, vehicle_count, person_count);
      }
    }
  }
  frame_number++;
  return GST_PAD_PROBE_OK;
}

static gboolean
bus_call (GstBus * bus, GstMessage * msg, gpointer data)
{
  GMainLoop *loop = (GMainLoop *) data;
  switch (GST_MESSAGE_TYPE (msg)) {
    case GST_MESSAGE_EOS:
      g_print ("End of stream\n");
      g_main_loop_quit (loop);
      break;
    case GST_MESSAGE_ERROR:{
      gchar *debug;
      GError *error;
      gst_message_parse_error (msg, &error, &debug);
      if (debug)
        g_free (debug);
      g_printerr ("Error: %s\n", error->message);
      g_error_free (error);
      g_main_loop_quit (loop);
      break;
    }
    default:
      break;
  }
  return TRUE;
}

int
main (int argc, char *argv[])
{
  GMainLoop *loop = NULL;
  GstElement *pipeline = NULL, *source = NULL, *h264parser = NULL,
      *decoder = NULL, *sink = NULL, *pgie = NULL, *nvvidconv = NULL,
      *nvosd = NULL, *filter1 = NULL, *filter2 = NULL,
      *sgie1 = NULL, *sgie2 = NULL, *sgie3 = NULL, *nvtracker = NULL;
  GstBus *bus = NULL;
  guint bus_watch_id = 0;
  GstCaps *caps1 = NULL, *caps2 = NULL;
  GstPad *osd_sink_pad = NULL;
  gulong osd_probe_id = 0;

  GstElement *nvvidconv1 = NULL;
  GstElement *filter3 = NULL;
  GstElement *videoconvert = NULL;
  GstElement *filter4 = NULL;
  GstElement *x264enc = NULL;
  GstElement *qtmux = NULL;
  GstCaps *caps3 = NULL, *caps4 = NULL;

  /* Check input arguments */
  if (argc != 2) {
    g_printerr ("Usage: %s <elementary H264 filename>\n", argv[0]);
    return -1;
  }

  /* Standard GStreamer initialization */
  gst_init (&argc, &argv);
  loop = g_main_loop_new (NULL, FALSE);

  /* Create gstreamer elements */

  /* Create Pipeline element that will be a container of other elements */
  pipeline = gst_pipeline_new ("dstest2-pipeline");

  /* Source element for reading from the file */
  source = gst_element_factory_make ("filesrc", "file-source");

  /* Since the data format in the input file is elementary h264 stream,
   * we need a h264parser */
  h264parser = gst_element_factory_make ("h264parse", "h264-parser");

  /* Use nvdec_h264 for hardware accelerated decode on GPU */
  decoder = gst_element_factory_make ("nvdec_h264", "nvh264-decoder");

  /* Use nvinfer to run inferencing on decoder's output,
   * behaviour of inferencing is set through config file */
  pgie = gst_element_factory_make ("nvinfer", "primary-nvinference-engine");

  /* We need to have a tracker to track the identified objects */
  nvtracker = gst_element_factory_make ("nvtracker", "tracker");

  /* We need three secondary gies so lets create 3 more instances of
     nvinfer */
  sgie1 = gst_element_factory_make ("nvinfer", "secondary1-nvinference-engine");

  sgie2 = gst_element_factory_make ("nvinfer", "secondary2-nvinference-engine");

  sgie3 = gst_element_factory_make ("nvinfer", "secondary3-nvinference-engine");

  /* Use convertor to convert from NV12 to RGBA as required by nvosd */
  nvvidconv = gst_element_factory_make ("nvvidconv", "nvvideo-converter");

  /* Create OSD to draw on the converted RGBA buffer */
  nvosd = gst_element_factory_make ("nvosd", "nv-onscreendisplay");

  nvvidconv1 = gst_element_factory_make("nvvidconv", "nvvideo-converter1");
  videoconvert = gst_element_factory_make("videoconvert", "converter");
  x264enc = gst_element_factory_make("x264enc", "h264 encoder");
  qtmux = gst_element_factory_make("qtmux", "muxer");

  /* Finally render the osd output */
  sink = gst_element_factory_make ("filesink", "filesink");


  /* caps filter for nvvidconv to convert NV12 to RGBA as nvosd expects input
   * in RGBA format */
  filter1 = gst_element_factory_make ("capsfilter", "filter1");
  filter2 = gst_element_factory_make ("capsfilter", "filter2");
  filter3 = gst_element_factory_make ("capsfilter", "filter3");
  filter4 = gst_element_factory_make ("capsfilter", "filter4");
  if (!pipeline || !source || !h264parser || !decoder || !pgie
      || !filter1 || !nvvidconv || !filter2 || !nvosd || !sink) {
    g_printerr ("One element could not be created. Exiting.\n");
    return -1;
  }

  if (!nvvidconv1 || !x264enc || !qtmux || !filter3 || !filter4) {
    g_printerr("one element could not be created. Exiting.\n");
    return -1;
  }

  /* Set the input filename to the source element */
  g_object_set (G_OBJECT (source), "location", argv[1], NULL);

  g_object_set(G_OBJECT(sink), "location", "out_test2_app.mp4", NULL);

  g_object_set (G_OBJECT (nvosd), "font-size", 15, NULL);

  /*
    ////////////////////////////////////////////////////////////////////
    // <1> Set up all the necessary proprties of the nvinfer element
    ////////////////////////////////////////////////////////////////////
    // TODO1
    // Hints:
    //   1> We need to define properties for each of the four classifiers:
            the primary classifiers, and the three secondary ones.
         2> We need to supply both the elements and the configuration files, which we defined
            as constants at the top of the file.
    */

  g_object_set (G_OBJECT (pgie), "config-file-path", PGIE_CONFIG_FILE, NULL);
  g_object_set (G_OBJECT (sgie1), "config-file-path", SGIE1_CONFIG_FILE, NULL);
  g_object_set (G_OBJECT (sgie2), "config-file-path", SGIE2_CONFIG_FILE, NULL);
  g_object_set (G_OBJECT (sgie3), "config-file-path", SGIE3_CONFIG_FILE, NULL);


  /* we add a message handler */
  bus = gst_pipeline_get_bus (GST_PIPELINE (pipeline));
  bus_watch_id = gst_bus_add_watch (bus, bus_call, loop);
  gst_object_unref (bus);


  /* Set up the pipeline */
  /* we add all elements into the pipeline */
  /* decoder | pgie | nvtracker | sgie1 | sgie2 | sgie3 | etc.. */

    
gst_bin_add_many (GST_BIN (pipeline),
      source, h264parser, decoder, pgie, nvtracker, sgie1, sgie2, sgie3,
      filter1, nvvidconv, filter2, nvosd, nvvidconv1, filter3,
      videoconvert, filter4, x264enc, qtmux, sink, NULL);

  caps1 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=NV12");
  g_object_set (G_OBJECT (filter1), "caps", caps1, NULL);
  gst_caps_unref (caps1);
  caps2 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=RGBA");
  g_object_set (G_OBJECT (filter2), "caps", caps2, NULL);
  gst_caps_unref (caps2);
  caps3 = gst_caps_from_string("video/x-raw, format=RGBA");
  g_object_set(G_OBJECT(filter3), "caps", caps3, NULL);
  gst_caps_unref(caps3);
  caps4 = gst_caps_from_string("video/x-raw, format=NV12");
  g_object_set(G_OBJECT(filter4), "caps", caps4, NULL);
  gst_caps_unref(caps4);


  /* Link the elements together */

    gst_element_link_many (source, h264parser, decoder, pgie, nvtracker, sgie1, sgie2, sgie3, filter1,
      nvvidconv, filter2, nvosd, nvvidconv1, filter3,
      videoconvert, filter4,
      x264enc, qtmux, sink, NULL);


  /* Lets add probe to get informed of the meta data generated, we add probe to
   * the sink pad of the osd element, since by that time, the buffer would have
   * had got all the metadata. */
  osd_sink_pad = gst_element_get_static_pad (nvosd, "sink");
  if (!osd_sink_pad)
    g_print ("Unable to get sink pad\n");
  else
    osd_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER,
        osd_sink_pad_buffer_probe, NULL, NULL);

  /* Set the pipeline to "playing" state */
  g_print ("Now playing: %s\n", argv[1]);
  gst_element_set_state (pipeline, GST_STATE_PLAYING);

  /* Iterate */
  g_print ("Running...\n");
  g_main_loop_run (loop);

  /* Out of the main loop, clean up nicely */
  g_print ("Returned, stopping playback\n");
  gst_element_set_state (pipeline, GST_STATE_NULL);
  g_print ("Deleting pipeline\n");
  gst_object_unref (GST_OBJECT (pipeline));
  g_source_remove (bus_watch_id);
  g_main_loop_unref (loop);
  return 0;
}

"""

In [16]:
# clean up the build directory
!make -C DeepStream_Release/sources/apps/deepstream-test2 clean

make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test2'
rm -rf deepstream_test2_app.o deepstream-test2-app
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test2'


In [17]:
# make and run the deepstream test2 app
!make -C DeepStream_Release/sources/apps/deepstream-test2

! cd DeepStream_Release/sources/apps/deepstream-test2 && \
./deepstream-test2-app  ../../../samples/streams/sample_720p.h264

make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test2'
cc -I../../includes `pkg-config --cflags gstreamer-1.0`   -c -o deepstream_test2_app.o deepstream_test2_app.c
cc -o deepstream-test2-app deepstream_test2_app.o `pkg-config --libs gstreamer-1.0`
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test2'
Now playing: ../../../samples/streams/sample_720p.h264
>>> Generating new TRT model engine
Using INT8 data type.

 ***** Storing serialized engine file as /dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test2/../../../samples/models/Secondary_VehicleTypes/resnet18.caffemodel_b16_int8.engine batchsize = 16 *****

>>> Generating new TRT model engine
Using INT8 data type.

 ***** Storing serialized engine file as /dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test2/../../../samples/models/Secondary_CarMake/resnet18.caffemodel_b16_int8.engine batchsize = 16 *****

>

Frame Number = 190 Number of objects = 8 Vehicle Count = 2 Person Count = 4
Frame Number = 191 Number of objects = 9 Vehicle Count = 2 Person Count = 5
Frame Number = 192 Number of objects = 10 Vehicle Count = 4 Person Count = 5
Frame Number = 193 Number of objects = 12 Vehicle Count = 5 Person Count = 6
Frame Number = 194 Number of objects = 11 Vehicle Count = 5 Person Count = 6
Frame Number = 195 Number of objects = 10 Vehicle Count = 5 Person Count = 5
Frame Number = 196 Number of objects = 10 Vehicle Count = 5 Person Count = 5
Frame Number = 197 Number of objects = 13 Vehicle Count = 7 Person Count = 5
Frame Number = 198 Number of objects = 13 Vehicle Count = 7 Person Count = 5
Frame Number = 199 Number of objects = 15 Vehicle Count = 8 Person Count = 5
Frame Number = 200 Number of objects = 13 Vehicle Count = 8 Person Count = 4
Frame Number = 201 Number of objects = 11 Vehicle Count = 6 Person Count = 4
Frame Number = 202 Number of objects = 9 Vehicle Count = 4 Person Count = 4
Fr

Frame Number = 298 Number of objects = 13 Vehicle Count = 8 Person Count = 4
Frame Number = 299 Number of objects = 13 Vehicle Count = 8 Person Count = 4
Frame Number = 300 Number of objects = 14 Vehicle Count = 9 Person Count = 4
Frame Number = 301 Number of objects = 12 Vehicle Count = 8 Person Count = 3
Frame Number = 302 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 303 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 304 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 305 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 306 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 307 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 308 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 309 Number of objects = 14 Vehicle Count = 10 Person Count = 3
Frame Number = 310 Number of objects = 14 Vehicle Count = 10 Person Count 

Frame Number = 405 Number of objects = 14 Vehicle Count = 6 Person Count = 6
Frame Number = 406 Number of objects = 15 Vehicle Count = 7 Person Count = 6
Frame Number = 407 Number of objects = 15 Vehicle Count = 7 Person Count = 6
Frame Number = 408 Number of objects = 11 Vehicle Count = 5 Person Count = 4
Frame Number = 409 Number of objects = 12 Vehicle Count = 6 Person Count = 4
Frame Number = 410 Number of objects = 11 Vehicle Count = 5 Person Count = 4
Frame Number = 411 Number of objects = 12 Vehicle Count = 5 Person Count = 5
Frame Number = 412 Number of objects = 15 Vehicle Count = 7 Person Count = 5
Frame Number = 413 Number of objects = 16 Vehicle Count = 8 Person Count = 5
Frame Number = 414 Number of objects = 15 Vehicle Count = 7 Person Count = 5
Frame Number = 415 Number of objects = 17 Vehicle Count = 9 Person Count = 6
Frame Number = 416 Number of objects = 19 Vehicle Count = 11 Person Count = 6
Frame Number = 417 Number of objects = 19 Vehicle Count = 12 Person Count =

Frame Number = 512 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 513 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 514 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 515 Number of objects = 12 Vehicle Count = 10 Person Count = 2
Frame Number = 516 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 517 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 518 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 519 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 520 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 521 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 522 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 523 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 524 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame N

...

Frame Number = 945 Number of objects = 12 Vehicle Count = 10 Person Count = 2
Frame Number = 946 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 947 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 948 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 949 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 950 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 951 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 952 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 953 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 954 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 955 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 956 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 957 Number of objects = 9 Vehicle Count = 7 Person Count = 2
F

Frame Number = 1053 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 1054 Number of objects = 15 Vehicle Count = 12 Person Count = 3
Frame Number = 1055 Number of objects = 16 Vehicle Count = 13 Person Count = 3
Frame Number = 1056 Number of objects = 14 Vehicle Count = 11 Person Count = 3
Frame Number = 1057 Number of objects = 15 Vehicle Count = 11 Person Count = 4
Frame Number = 1058 Number of objects = 16 Vehicle Count = 12 Person Count = 4
Frame Number = 1059 Number of objects = 18 Vehicle Count = 14 Person Count = 4
Frame Number = 1060 Number of objects = 16 Vehicle Count = 12 Person Count = 4
Frame Number = 1061 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 1062 Number of objects = 13 Vehicle Count = 8 Person Count = 5
Frame Number = 1063 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 1064 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1065 Number of objects = 10 Vehicle Count 

Frame Number = 1161 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1162 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1163 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1164 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1165 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1166 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1167 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1168 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1169 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1170 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1171 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1172 Number of objects = 12 Vehicle Count = 10 Person Count = 2
Frame Number = 1173 Number of objects = 12 Vehicle Count = 10 Person 

Frame Number = 1270 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1271 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1272 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1273 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1274 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1275 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1276 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1277 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1278 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1279 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1280 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1281 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1282 Number of objects = 7 Vehicle Count = 5 Person Count =

Frame Number = 1377 Number of objects = 12 Vehicle Count = 10 Person Count = 2
Frame Number = 1378 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1379 Number of objects = 12 Vehicle Count = 10 Person Count = 2
Frame Number = 1380 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1381 Number of objects = 13 Vehicle Count = 11 Person Count = 2
Frame Number = 1382 Number of objects = 13 Vehicle Count = 11 Person Count = 2
Frame Number = 1383 Number of objects = 13 Vehicle Count = 11 Person Count = 2
Frame Number = 1384 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1385 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1386 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1387 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1388 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1389 Number of objects = 12 Vehicle Count = 10


<a id='CONSOLE_OUTPUT-2'></a>
##### <font color = '#76b900'>Console Output</font>
---
On the screen you should see the frame number, number of objects in the frame, vehicle count and person count. 

    .....
    Now playing: ../../../samples/streams/sample_720p.h264
    >>> Generating new GIE model cache
    Using INT8 data type.
    ...
    Running...
    [ INFO:0] Initialize OpenCL runtime...
    Frame Number = 0 Number of objects = 4 Vehicle Count = 3 Person Count = 1
    Frame Number = 1 Number of objects = 4 Vehicle Count = 3 Person Count = 1
    Frame Number = 2 Number of objects = 4 Vehicle Count = 3 Person Count = 1
    ...
    Frame Number = 594 Number of objects = 6 Vehicle Count = 6 Person Count = 0
    Frame Number = 595 Number of objects = 6 Vehicle Count = 6 Person Count = 0
    Frame Number = 596 Number of objects = 6 Vehicle Count = 6 Person Count = 0
    End of stream
    Returned, stopping playback
    Deleting pipeline

<a id='DISPLAY_OUTPUT-1'></a>
##### <font color = '#76b900'>Display Output</font>
---
Let's look at our video output to see the results.

In [18]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="DeepStream_Release/sources/apps/deepstream-test2/out_test2_app.mp4" type="video/mp4">
    </video>
""".format())

By using the secondary neural networks, we can classify cars into more specific categories than before. Notice that the `Person` category doesn't have the additional metadata, while the `Vehicle` category does. Let's dive into the details of handling metadata to see how we made this happen. 

<a id='access-meta'></a>
### 5.4 Accessing Metadata

Similar to the previous section, in the callback function, we access the metadata attached to buffer. Here, in this callback, we access the metadata added by the first classifier to get the color of the car. We can find the car make and the car type which are the outputs from the second and the third classifier. You can try it on your own and see the result on the console.

```c
  /* Lets add probe to get informed of the meta data generated, we add probe to
   * the sink pad of the osd element, since by that time, the buffer would have
   * had got all the metadata. */
  osd_sink_pad = gst_element_get_static_pad (nvosd, "sink");
  if (!osd_sink_pad)
    g_print ("Unable to get sink pad\n");
  else
    osd_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER,
        osd_sink_pad_buffer_probe, NULL, NULL);
```

__And the callback function is defined as:__


```c
static GstPadProbeReturn
osd_sink_pad_buffer_probe (GstPad * pad, GstPadProbeInfo * info,
    gpointer u_data)
{
...  
  while ((gst_meta = gst_buffer_iterate_meta (buf, &state))) {
    if (gst_meta_api_type_has_tag (gst_meta->info->api, _nvdsmeta_quark)) {

      nvdsmeta = (NvDsMeta *) gst_meta;
        frame_meta->num_strings = 0;

        num_rects = frame_meta->num_rects;
        /* This means we have num_rects in frame_meta->obj_params,
         * now lets iterate through them */

        for (rect_index = 0; rect_index < num_rects; rect_index++) {
 ...
        }

      }
    }
  }
```


Our metadata handling is governed by two files: __gstnvdsmeta.h__ and __nvosd.h__. 

gstnvdsmeta.h defines the NVIDIA DeepStream Metadata structures used to describe metadata objects and nvosd.h defines the NvOSD library to be used to draw rectangles and text over the video frame for given parameters.  

Open gstnvdsmeta.h and review it. Pay attention to the following code snippet in the docstring: 

```c
gpointer state = NULL;
GstMeta *gst_meta;
NvDsMeta *nvdsmeta;
static GQuark _nvdsmeta_quark = 0;

if (!_nvdsmeta_quark)
    _nvdsmeta_quark = g_quark_from_static_string (NVDS_META_STRING);

  while ((gst_meta = gst_buffer_iterate_meta (buf, &state))) {
    if (gst_meta_api_type_has_tag (gst_meta->info->api, _nvdsmeta_quark)) {

      nvdsmeta = (NvDsMeta *) gst_meta;
      // Do something with this nvdsmeta
```

Because DeepStream metadata is attached to the buffer, we use a while loop to iterate through all the attached metadata. Within the loop, we write our business logic that determines what we display on the video output. Open deepstream_test2_app and scroll to line 92 to see the following code snippet:

```c
    /* We are interested only in intercepting Meta of type
       * "NVDS_META_FRAME_INFO" as they are from our infer elements. */
      if (nvdsmeta->meta_type == NVDS_META_FRAME_INFO) {
        frame_meta = (NvDsFrameMeta *) nvdsmeta->meta_data;
```

By intercepting the metadata from the __NvInfer__ element and storing it in `frame_meta`, we can access the results of our deep learning models.

Notice that you can also control the on-screen display parameters defined in __nvosd.h__. These `txt_params` also come from the `frame_meta`.

### Change the font size to 24 

* (line 203 in __deepstream_test2_app__)

In [ ]:
# re-make and run the deepstream test2 app
!make -C DeepStream_Release/sources/apps/deepstream-test2

! cd DeepStream_Release/sources/apps/deepstream-test2 && \
./deepstream-test2-app  ../../../samples/streams/sample_720p.h264

Now, let's see how the output video changed.

In [ ]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="DeepStream_Release/sources/apps/deepstream-test2/out_test2_app.mp4" type="video/mp4">
    </video>
""".format())

In this section, we learned how to set up a pipeline with multiple, cascaded deep learning classifiers. Configuration file parameters are an important way for us to control the behavior of our models in a DeepStream application. 

We also dove deeper into our callback function for handling metadata. We access all the metadata attached to the buffer by iterating through it one at a time. To access metadata and results from our deep neural networks, we perform our business logic on the metadata of type `NVDS_META_FRAME_INFO`. 


<a id='custom-parser'></a> 
## 6. Custom Parsers and Networks  

Up until now, we have only used the sample neural networks and parsers. 

In this section, we will see how to use the __NvInfer__ component to accommodate any __TensorRT__ compatible neural network for `detection`. With this, users can focus on developing their own neural networks and leverage DeepStream building blocks to quickly implement a solution around it for novel use cases. 

<a id='PIPELINE-3'></a>
### 6.1 Pipeline
Here, the pipeline architecture is the same first pipeline

<img src='images/Lab3_pipeline.png' style='width:80%'/>
<p style="text-align: center;color:gray">Figure 15. The custom parser pipeline</p>


<a id='custom-parsers-6'></a>
### 6.2 Using Custom Parsers 

 In the DeepStream package, we provide an example of a custom parser (inside the `nvparsebbox` directory). This sample parser function is for a ResNet10 based detector. For this exercise, we will use this plugin as a bounding box parser function of the custom model created by a developer. For now, we will use the primary detector in the package as our custom model, but you could always supply a new model via the configuration files as described previously. 

 To use this parser, we first need to generate a library containing this parser function and set the configuration parameters mentioned in the previous cell. It's also important to make sure you are setting the correct network parameters when you are using custom parsers, but we will get to that in a bit. 

### NVDSPARSEBBOX

Open nvdsparsebbox.cpp and review the example model. There's a couple of key items to point out here. We will need to keep track of our function's name, `parse_bbox_custom_resnet`, so we can use it in the configuration file. We also need to fill in the if statement on line 20: 

```c
if(framenum == 0)
  {
    printf("Custom parser used by Deepstream");
  }


In [19]:
import sys,os,os.path
os.environ['LD_LIBRARY_PATH']='/usr/local/lib/x86_64-linux-gnu:/usr/local/lib/i386-linux-gnu:/usr/lib/x86_64-linux-gnu:/usr/lib/i386-linux-gnu:/tensorrt/include'

In [20]:

!echo $LD_LIBRARY_PATH

# clean up before building
!make -C DeepStream_Release/sources/libs/nvdsparsebbox2 clean

# build the library
!make -C DeepStream_Release/sources/libs/nvdsparsebbox2

/usr/local/lib/x86_64-linux-gnu:/usr/local/lib/i386-linux-gnu:/usr/lib/x86_64-linux-gnu:/usr/lib/i386-linux-gnu:/tensorrt/include
make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/libs/nvdsparsebbox2'
rm -rf libnvdsparsebbox.so
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/libs/nvdsparsebbox2'
make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/libs/nvdsparsebbox2'
g++ -o libnvdsparsebbox.so nvdsparsebbox.cpp -Wall -std=c++11 -shared -fPIC -I ../../includes -I /tensorrt/include/ -Wl,--start-group `pkg-config --libs gstreamer-1.0` -L/usr/local/deepstream/ -lnvdsgst_meta -lrt -Wl,-rpath,/usr/local/deepstream -Wl,--end-group
nvdsparsebbox.cpp: In function 'bool NvDsInferParseCustomResnet(const std::vector<NvDsInferLayerInfo>&, const NvDsInferNetworkInfo&, const NvDsInferParseDetectionParams&, std::vector<NvDsInferParseObjectInfo>&)':
nvdsparsebbox.cpp:75:24: warning: comparison between signed and unsigned in

With the library built, there's one more step. 
We need tell DeepStream to use this function and library for parsing. To start, open dstest1_pgie_config.txt and review the configuration file. To use a custom parser, we need to add three additional parameters for the NvInfer component: 

- __parse-bbox-func-name__ 
    - The name of the bounding box parser function of the detector 
- __custom-lib-path__ 
    - The library that contains the parser function 
- __parse-func__ 
    - Setting this equal to 0 indicates that we are using a detection algorithm. 
 Example parameters are listed below. 

``` 
parse-func=0 
parse-bbox-func-name=parse_bbox_custom_resnet 
custom-lib-path=/dli/tasks/l-iv-04/task/DeepStream_Release/sources/libs/nvdsparsebbox2/libnvdsparsebbox.so
```  

Make sure that the parameter `parse-bbox-func-name` is set to be equal to the name of the function you defined in nvdsparsebbox.cpp

#### dstest1_pgie_config.txt 

In [ ]:
"""
[property]
gpu-id=0
net-scale-factor=0.0039215697906911373
model-file=../../../samples/models/Primary_Detector/resnet10.caffemodel
proto-file=../../../samples/models/Primary_Detector/resnet10.prototxt
labelfile-path=../../../samples/models/Primary_Detector/labels.txt
int8-calib-file=../../../samples/models/Primary_Detector/cal_trt4.bin
batch-size=1
network-mode=1
num-detected-classes=4
interval=0
gie-unique-id=1
parse-func=4
output-blob-names=conv2d_bbox;conv2d_cov/Sigmoid
parse-func=0
parse-bbox-func-name=NvDsInferParseCustomResnet
custom-lib-path=/dli/tasks/l-iv-04/task/DeepStream_Release/sources/libs/nvdsparsebbox2/libnvdsparsebbox.so

[class-attrs-all]
threshold=0.2
eps=0.2
group-threshold=1

"""

#### Build and Run the Application

With the library built and configuration set, we are ready to build and run the application.

In [21]:
!rm -rf $HOME/.cache/gstreamer-1.0/ && \
cd DeepStream_Release/sources/apps/deepstream-test3 && \
make && \
./deepstream-test3-app  ../../../samples/streams/sample_720p.h264

cc -I../../includes `pkg-config --cflags gstreamer-1.0`   -c -o deepstream_test3_app.o deepstream_test3_app.c
cc -o deepstream-test3-app deepstream_test3_app.o `pkg-config --libs gstreamer-1.0`
Now playing: ../../../samples/streams/sample_720p.h264
>>> Generating new TRT model engine
Using INT8 data type.

 ***** Storing serialized engine file as /dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test3/../../../samples/models/Primary_Detector/resnet10.caffemodel_b1_int8.engine batchsize = 1 *****

Running...
Custom parser used by DeepstreamFrame Number = 0 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 2 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 3 Number of objects = 6 Vehicle Count = 3 Person Count = 3
Frame Number = 4 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 5 Number of objects = 5 Vehicle Count = 3 Person Coun

Frame Number = 103 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 104 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 105 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 106 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 107 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 108 Number of objects = 9 Vehicle Count = 5 Person Count = 4
Frame Number = 109 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Frame Number = 110 Number of objects = 9 Vehicle Count = 4 Person Count = 5
Frame Number = 111 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 112 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 113 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 114 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 115 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame N

Frame Number = 212 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 213 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 214 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 215 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 216 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 217 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 218 Number of objects = 10 Vehicle Count = 7 Person Count = 2
Frame Number = 219 Number of objects = 9 Vehicle Count = 6 Person Count = 2
Frame Number = 220 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 221 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 222 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 223 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 224 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Fram

Frame Number = 324 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 325 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 326 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 327 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 328 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Frame Number = 329 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 330 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 331 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 332 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 333 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 334 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 335 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 336 Number of objects = 14 Vehicle Count = 10 Person Count = 4


Frame Number = 432 Number of objects = 13 Vehicle Count = 7 Person Count = 6
Frame Number = 433 Number of objects = 13 Vehicle Count = 7 Person Count = 4
Frame Number = 434 Number of objects = 13 Vehicle Count = 7 Person Count = 5
Frame Number = 435 Number of objects = 12 Vehicle Count = 7 Person Count = 4
Frame Number = 436 Number of objects = 11 Vehicle Count = 6 Person Count = 4
Frame Number = 437 Number of objects = 13 Vehicle Count = 8 Person Count = 4
Frame Number = 438 Number of objects = 12 Vehicle Count = 7 Person Count = 4
Frame Number = 439 Number of objects = 14 Vehicle Count = 8 Person Count = 5
Frame Number = 440 Number of objects = 11 Vehicle Count = 7 Person Count = 3
Frame Number = 441 Number of objects = 13 Vehicle Count = 9 Person Count = 3
Frame Number = 442 Number of objects = 9 Vehicle Count = 6 Person Count = 2
Frame Number = 443 Number of objects = 7 Vehicle Count = 4 Person Count = 2
Frame Number = 444 Number of objects = 8 Vehicle Count = 6 Person Count = 1
Fr

...

Frame Number = 976 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 977 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 978 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 979 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 980 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 981 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 982 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 983 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 984 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 985 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 986 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 987 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 988 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame

Frame Number = 1083 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1084 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1085 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1086 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1087 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1088 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1089 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1090 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1091 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1092 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1093 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1094 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1095 Number of objects = 8 Vehicle Count = 5 Person 

Frame Number = 1193 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1194 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1195 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1196 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1197 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1198 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1199 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1200 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1201 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1202 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1203 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1204 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1205 Number of objects = 5 Vehicle Count = 3 Person Count = 2

Frame Number = 1300 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1301 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1302 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1303 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1304 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1305 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1306 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1307 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1308 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1309 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1310 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1311 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1312 Number of objects = 5 Vehicle Count = 3 Person Count = 2

Frame Number = 1407 Number of objects = 8 Vehicle Count = 7 Person Count = 1
Frame Number = 1408 Number of objects = 5 Vehicle Count = 5 Person Count = 0
Frame Number = 1409 Number of objects = 6 Vehicle Count = 5 Person Count = 1
Frame Number = 1410 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1411 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1412 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1413 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1414 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1415 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1416 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1417 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1418 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1419 Number of objects = 8 Vehicle Count = 6 Person Count = 2

Notice that, after the first frame, our custom parser printed out a message. DeepStream is using this parser on every frame. We can look at the output video and see the results of our parser. 

In [22]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="DeepStream_Release/sources/apps/deepstream-test3/out_test3_app.mp4" type="video/mp4">
    </video>
""".format())


<a id='CONSOLE_OUTPUT-2'></a>
##### <font color = '#76b900'>Console Output</font>
---

    ...
    #your_flag: Text inside the printf call
    Frame Number = 0 Number of objects = 5 Vehicle Count = 3 Person Count = 2
    ....
    Frame Number = 1428 Number of objects = 4 Vehicle Count = 4 Person Count = 0
    Frame Number = 1429 Number of objects = 5 Vehicle Count = 5 Person Count = 0
    Frame Number = 1430 Number of objects = 5 Vehicle Count = 5 Person Count = 0
    Frame Number = 1431 Number of objects = 3 Vehicle Count = 3 Person Count = 0
    Frame Number = 1432 Number of objects = 4 Vehicle Count = 4 Person Count = 0
    Frame Number = 1433 Number of objects = 5 Vehicle Count = 5 Person Count = 0
    Frame Number = 1434 Number of objects = 6 Vehicle Count = 6 Person Count = 0
    Frame Number = 1435 Number of objects = 5 Vehicle Count = 5 Person Count = 0
    Frame Number = 1436 Number of objects = 5 Vehicle Count = 5 Person Count = 0
    Frame Number = 1437 Number of objects = 6 Vehicle Count = 6 Person Count = 0
    Frame Number = 1438 Number of objects = 5 Vehicle Count = 5 Person Count = 0
    End of stream
    Returned, stopping playback
    #your_flag: parse_bbox_custom_resnet is called
    Deleting pipeline


We know how to incorporate a custom parser into a DeepStream pipeline by leveraging the __NvInfer__ plugin. __NvInfer__ makes it easy to utilize custom neural networks and neural network parsers. When we do this, we need to make sure that we update our configuration file parameters with the relevant parameters.

----

<a id='custom-plugins'></a>
## 7. Custom Plugins and OpenCV based Detection 

Here we will see how to incorporate a custom plugin into DeepStream pipeline. We will use the custom plugin __DsExample__ to use OpenCV (a commonly used computer vision library) to detect a moving car in a video stream. 

OpenCV 3 is a pre-requisite for Deepstream so it's already at your disposal. The DsExample Makefile already includes necessary linking instructions for the OpenCV modules typically used for real-time processing. If you base your future custom plugins on this reference plugin, and you need other modules, you should include them in the Makefile. 

**We will notice that we are building our library in C++ as opposed to C, which is necessary to use OpenCV.**

<a id='building-pipeline-7'></a>
### 7.1 Building Pipelines at the Command Line 

 Also, we will be composing our pipeline at the command line, which makes it easy for us to prototype. 

 In order to run the pipeline on the command line we are using a native Gstreamer program called `gst-launch-1.0` which builds and runs the pipeline and is called using the following parameter list: 

``` 
gst-launch-1.0 [OPTIONS] PIPELINE-DESCRIPTION 
``` 

Here, `description` is the list of pipeline elements and their corresponding properties. These elements are separated by exclamation marks.  

When we compose pipelines on the command line instead of building them into applications, we sacrifice flexibility and advanced usage for ease of prototyping. For production usage, we would compose the pipeline in our application, as we have done in the previous three sections. For prototyping and learning, building the pipeline at the command line and visualizing can help us get a sense of what's happening.

<a id='PIPELINE-7'></a> 
### 7.2 Pipeline Architecture 

<img src='images/Lab4_pipeline.png' style='width:80%'/> 
<p style="text-align: center;color:gray">Figure 16. The custom plugin architecture</p>     

The key difference between this pipeline and previous one is that here we are building a pipeline that uses __DsExample__ instead of __NvInfer__ to perform the object detection. As with deepstream-test1 the metadata produced now by our inference/detection plugin is rendered by `nvosd` and later, displayed by the video `sink`. 

<a id='custom-plugin-lib'></a>
### 7.3 Custom Plugin Library Structure 

DsExample supports the DeepStream metadata for inter-plugin operability, which inputs uncompressed frames and outputs ROI metadata. The implementation of DsExample a could be useful as a proof of concept and experiments, as a template to start development and in order to shield your code form GStreamer specifics. 

The DsExample DeepStream filter consists of 2 parts:  

1. The custom library dsexample_lib_cpp that implements our custom detection algorithm.  

2. The code that implements all the necessary mechanics for the GStreamer filter gstdsexample.cpp and the associated header file) 

<a id='MD-CV'></a>
### 7.4 Motion Detection with OpenCV 

Our approach to motion detection is straightforward: We analyze the differences in consecutive frames and, if the difference is above a threshold, consider that [contour](https://docs.opencv.org/3.3.1/d4/d73/tutorial_py_contours_begin.html) to be moving. Once we have identified moving contours, we identify the bounding boxes for the contour and return that metadata attached to a `DsExampleOutput` object. 

Please review the library code by opening dsexample_lib.cpp and the header file. Pay particular attention to the function `DsExampleProcess`, which has a return type of `DsExampleOutput` in the `dsexample_lib.cpp`. This is where we are implementing the details of OpenCV based detection algorithm and calculating bounding boxes. 

<a id='gs-plug'></a>
### 7.5 GStreamer Plugin Mechanics 

Going through the low-level details of warping the library into a GStreamer plugin is little more complicate. Some of the core functionality we implement include: 

- Initializing and setting properties of our element 

- Starting and stopping the output thread 

- Wrapping around our custom library to execute when this element receives an input buffer from an upstream element 

- Attaching resulting metadata to the frame 

We encourage you to look through gstdsexample.cpp and gstdsexample.h and take note of the core components.

With this background, we are ready to build the plugin and run our pipeline. 

* gstdsexample.cpp 

In [ ]:
"""
/**
 * Copyright (c) 2017-2018, NVIDIA CORPORATION.  All rights reserved.
 *
 * NVIDIA Corporation and its licensors retain all intellectual property
 * and proprietary rights in and to this software, related documentation
 * and any modifications thereto.  Any use, reproduction, disclosure or
 * distribution of this software and related documentation without an express
 * license agreement from NVIDIA Corporation is strictly prohibited.
 *
 */

#include <string.h>
#include <string>
#include <sstream>
#include <iostream>
#include <ostream>
#include <fstream>
#include "gstdsexample.h"
#include <npp.h>
#include <sys/time.h>
GST_DEBUG_CATEGORY_STATIC (gst_dsexample_debug);
#define GST_CAT_DEFAULT gst_dsexample_debug

static GQuark _dsmeta_quark = 0;

/* Enum to identify properties */
enum
{
  PROP_0,
  PROP_UNIQUE_ID,
  PROP_PROCESSING_WIDTH,
  PROP_PROCESSING_HEIGHT,
  PROP_PROCESS_FULL_FRAME,
  PROP_GPU_DEVICE_ID
};

/* Default values for properties */
#define DEFAULT_UNIQUE_ID 15
#define DEFAULT_PROCESSING_WIDTH 640
#define DEFAULT_PROCESSING_HEIGHT 480
#define DEFAULT_PROCESS_FULL_FRAME TRUE
#define DEFAULT_GPU_ID 0

#define RGB_BYTES_PER_PIXEL 3
#define RGBA_BYTES_PER_PIXEL 4
#define Y_BYTES_PER_PIXEL 1
#define UV_BYTES_PER_PIXEL 2

#define CHECK_NPP_STATUS(npp_status,error_str) do { \
  if ((npp_status) != NPP_SUCCESS) { \
    g_print ("Error: %s in %s at line %d: NPP Error %d\n", \
        error_str, __FILE__, __LINE__, npp_status); \
    goto error; \
  } \
} while (0)

#define CHECK_CUDA_STATUS(cuda_status,error_str) do { \
  if ((cuda_status) != cudaSuccess) { \
    g_print ("Error: %s in %s at line %d (%s)\n", \
        error_str, __FILE__, __LINE__, cudaGetErrorName(cuda_status)); \
    goto error; \
  } \
} while (0)

/* By default NVIDIA Hardware allocated memory flows through the pipeline. We
 * will be processing on this type of memory only. */
#define GST_CAPS_FEATURE_MEMORY_NVMM "memory:NVMM"
static GstStaticPadTemplate gst_dsexample_sink_template =
GST_STATIC_PAD_TEMPLATE ("sink",
    GST_PAD_SINK,
    GST_PAD_ALWAYS,
    GST_STATIC_CAPS (GST_VIDEO_CAPS_MAKE_WITH_FEATURES
        (GST_CAPS_FEATURE_MEMORY_NVMM,
            "{ NV12, RGBA }")));

static GstStaticPadTemplate gst_dsexample_src_template =
GST_STATIC_PAD_TEMPLATE ("src",
    GST_PAD_SRC,
    GST_PAD_ALWAYS,
    GST_STATIC_CAPS (GST_VIDEO_CAPS_MAKE_WITH_FEATURES
        (GST_CAPS_FEATURE_MEMORY_NVMM,
            "{ NV12, RGBA }")));

/* Define our element type. Standard GObject/GStreamer boilerplate stuff */
#define gst_dsexample_parent_class parent_class
G_DEFINE_TYPE (GstDsExample, gst_dsexample, GST_TYPE_BASE_TRANSFORM);

static void gst_dsexample_set_property (GObject * object, guint prop_id,
    const GValue * value, GParamSpec * pspec);
static void gst_dsexample_get_property (GObject * object, guint prop_id,
    GValue * value, GParamSpec * pspec);

static gboolean gst_dsexample_set_caps (GstBaseTransform * btrans,
    GstCaps * incaps, GstCaps * outcaps);
static gboolean gst_dsexample_start (GstBaseTransform * btrans);
static gboolean gst_dsexample_stop (GstBaseTransform * btrans);

static GstFlowReturn gst_dsexample_transform_ip (GstBaseTransform *
    btrans, GstBuffer * inbuf);

static void
attach_metadata_full_frame (GstDsExample * dsexample, GstBuffer * inbuf,
    gdouble scale_ratio, DsExampleOutput * output, guint batch_id);
static void attach_metadata_object (GstDsExample * dsexample,
    NvDsObjectParams * obj_param, DsExampleOutput * output);

/* Install properties, set sink and src pad capabilities, override the required
 * functions of the base class, These are common to all instances of the
 * element.
 */
static void
gst_dsexample_class_init (GstDsExampleClass * klass)
{
  GObjectClass *gobject_class;
  GstElementClass *gstelement_class;
  GstBaseTransformClass *gstbasetransform_class;

  gobject_class = (GObjectClass *) klass;
  gstelement_class = (GstElementClass *) klass;
  gstbasetransform_class = (GstBaseTransformClass *) klass;

  /* Overide base class functions */
  gobject_class->set_property = GST_DEBUG_FUNCPTR (gst_dsexample_set_property);
  gobject_class->get_property = GST_DEBUG_FUNCPTR (gst_dsexample_get_property);

  gstbasetransform_class->set_caps = GST_DEBUG_FUNCPTR (gst_dsexample_set_caps);
  gstbasetransform_class->start = GST_DEBUG_FUNCPTR (gst_dsexample_start);
  gstbasetransform_class->stop = GST_DEBUG_FUNCPTR (gst_dsexample_stop);

  gstbasetransform_class->transform_ip =
      GST_DEBUG_FUNCPTR (gst_dsexample_transform_ip);

  /* Install properties */
  g_object_class_install_property (gobject_class, PROP_UNIQUE_ID,
      g_param_spec_uint ("unique-id",
          "Unique ID",
          "Unique ID for the element. Can be used to identify output of the"
          " element", 0, G_MAXUINT, DEFAULT_UNIQUE_ID, (GParamFlags)
          (G_PARAM_READWRITE | G_PARAM_STATIC_STRINGS)));

  g_object_class_install_property (gobject_class, PROP_PROCESSING_WIDTH,
      g_param_spec_int ("processing-width",
          "Processing Width",
          "Width of the input buffer to algorithm",
          1, G_MAXINT, DEFAULT_PROCESSING_WIDTH, (GParamFlags)
          (G_PARAM_READWRITE | G_PARAM_STATIC_STRINGS)));

  g_object_class_install_property (gobject_class, PROP_PROCESSING_HEIGHT,
      g_param_spec_int ("processing-height",
          "Processing Height",
          "Height of the input buffer to algorithm",
          1, G_MAXINT, DEFAULT_PROCESSING_HEIGHT, (GParamFlags)
          (G_PARAM_READWRITE | G_PARAM_STATIC_STRINGS)));

  g_object_class_install_property (gobject_class, PROP_PROCESS_FULL_FRAME,
      g_param_spec_boolean ("full-frame",
          "Full frame",
          "Enable to process full frame or disable to process objects detected"
          "by primary detector", DEFAULT_PROCESS_FULL_FRAME, (GParamFlags)
          (G_PARAM_READWRITE | G_PARAM_STATIC_STRINGS)));

  g_object_class_install_property (gobject_class, PROP_GPU_DEVICE_ID,
      g_param_spec_uint ("gpu-id",
          "Set GPU Device ID",
          "Set GPU Device ID", 0,
          G_MAXUINT, 0,
          GParamFlags
          (G_PARAM_READWRITE |
              G_PARAM_STATIC_STRINGS | GST_PARAM_MUTABLE_READY)));
  /* Set sink and src pad capabilities */
  gst_element_class_add_pad_template (gstelement_class,
      gst_static_pad_template_get (&gst_dsexample_src_template));
  gst_element_class_add_pad_template (gstelement_class,
      gst_static_pad_template_get (&gst_dsexample_sink_template));

  /* Set metadata describing the element */
  gst_element_class_set_details_simple (gstelement_class,
      "DsExample plugin",
      "DsExample Plugin",
      "Process a 3rdparty example algorithm on objects / full frame",
      "NVIDIA Corporation. Post on Deepstream for Tesla forum for any queries "
      "@ https://devtalk.nvidia.com/default/board/209/");
}

static void
gst_dsexample_init (GstDsExample * dsexample)
{
  GstBaseTransform *btrans = GST_BASE_TRANSFORM (dsexample);

  /* We will not be generating a new buffer. Just adding / updating
   * metadata. */
  gst_base_transform_set_in_place (GST_BASE_TRANSFORM (btrans), TRUE);
  /* We do not want to change the input caps. Set to passthrough. transform_ip
   * is still called. */
  gst_base_transform_set_passthrough (GST_BASE_TRANSFORM (btrans), TRUE);

  /* Initialize all property variables to default values */
  dsexample->unique_id = DEFAULT_UNIQUE_ID;
  dsexample->processing_width = DEFAULT_PROCESSING_WIDTH;
  dsexample->processing_height = DEFAULT_PROCESSING_HEIGHT;
  dsexample->process_full_frame = DEFAULT_PROCESS_FULL_FRAME;
  dsexample->gpu_id = DEFAULT_GPU_ID;
  /* This quark is required to identify NvDsMeta when iterating through
   * the buffer metadatas */
  if (!_dsmeta_quark)
    _dsmeta_quark = g_quark_from_static_string (NVDS_META_STRING);
}

/* Function called when a property of the element is set. Standard boilerplate.
 */
static void
gst_dsexample_set_property (GObject * object, guint prop_id,
    const GValue * value, GParamSpec * pspec)
{
  GstDsExample *dsexample = GST_DSEXAMPLE (object);
  switch (prop_id) {
    case PROP_UNIQUE_ID:
      dsexample->unique_id = g_value_get_uint (value);
      break;
    case PROP_PROCESSING_WIDTH:
      dsexample->processing_width = g_value_get_int (value);
      break;
    case PROP_PROCESSING_HEIGHT:
      dsexample->processing_height = g_value_get_int (value);
      break;
    case PROP_PROCESS_FULL_FRAME:
      dsexample->process_full_frame = g_value_get_boolean (value);
      break;
    case PROP_GPU_DEVICE_ID:
      dsexample->gpu_id = g_value_get_uint (value);
      break;
    default:
      G_OBJECT_WARN_INVALID_PROPERTY_ID (object, prop_id, pspec);
      break;
  }
}

/* Function called when a property of the element is requested. Standard
 * boilerplate.
 */
static void
gst_dsexample_get_property (GObject * object, guint prop_id,
    GValue * value, GParamSpec * pspec)
{
  GstDsExample *dsexample = GST_DSEXAMPLE (object);

  switch (prop_id) {
    case PROP_UNIQUE_ID:
      g_value_set_uint (value, dsexample->unique_id);
      break;
    case PROP_PROCESSING_WIDTH:
      g_value_set_int (value, dsexample->processing_width);
      break;
    case PROP_PROCESSING_HEIGHT:
      g_value_set_int (value, dsexample->processing_height);
      break;
    case PROP_PROCESS_FULL_FRAME:
      g_value_set_boolean (value, dsexample->process_full_frame);
      break;
    case PROP_GPU_DEVICE_ID:
      g_value_set_uint (value, dsexample->gpu_id);
      break;
    default:
      G_OBJECT_WARN_INVALID_PROPERTY_ID (object, prop_id, pspec);
      break;
  }
}

/**
 * Initialize all resources and start the output thread
 */
static gboolean
gst_dsexample_start (GstBaseTransform * btrans)
{
  GstDsExample *dsexample = GST_DSEXAMPLE (btrans);
  DsExampleInitParams init_params =
      { dsexample->processing_width, dsexample->processing_height,
    dsexample->process_full_frame
  };

  GstQuery *queryparams = NULL;
  guint batch_size = 1;

  /* Algorithm specific initializations and resource allocation. */
  dsexample->dsexamplelib_ctx = DsExampleCtxInit (&init_params);

  GST_DEBUG_OBJECT (dsexample, "ctx lib %p \n", dsexample->dsexamplelib_ctx);

  CHECK_CUDA_STATUS (cudaSetDevice (dsexample->gpu_id),
      "Unable to set cuda device");

  dsexample->batch_size = 1;
  queryparams = gst_nvquery_batch_size_new ();
  if (gst_pad_peer_query (GST_BASE_TRANSFORM_SINK_PAD (btrans), queryparams)
      || gst_pad_peer_query (GST_BASE_TRANSFORM_SRC_PAD (btrans), queryparams)) {
    if (gst_nvquery_batch_size_parse (queryparams, &batch_size)) {
      dsexample->batch_size = batch_size;
    }
  }
  GST_DEBUG_OBJECT (dsexample, "Setting batch-size %d \n",
      dsexample->batch_size);
  gst_query_unref (queryparams);

  CHECK_CUDA_STATUS (cudaStreamCreate (&dsexample->npp_stream),
      "Could not create cuda stream");

  // Create host memory for storing converted/scaled interleaved RGB data
  CHECK_CUDA_STATUS (cudaMallocHost (&dsexample->host_rgb_buf,
          dsexample->processing_width * dsexample->processing_height *
          RGB_BYTES_PER_PIXEL), "Could not allocate cuda host buffer");

  GST_DEBUG_OBJECT (dsexample, "allocated cuda buffer %p \n",
      dsexample->host_rgb_buf);

  // CV Mat containing interleaved RGB data. This call does not allocate memory.
  // It uses host_rgb_buf as data.
  dsexample->cvmat =
      new cv::Mat (dsexample->processing_height, dsexample->processing_width,
      CV_8UC3, dsexample->host_rgb_buf,
      dsexample->processing_width * RGB_BYTES_PER_PIXEL);

  if (!dsexample->cvmat)
    goto error;

  GST_DEBUG_OBJECT (dsexample, "created CV Mat\n");

  return TRUE;
error:
  if (dsexample->host_rgb_buf) {
    cudaFreeHost (dsexample->host_rgb_buf);
    dsexample->host_rgb_buf = NULL;
  }

  if (dsexample->npp_stream) {
    cudaStreamDestroy (dsexample->npp_stream);
    dsexample->npp_stream = NULL;
  }
  if (dsexample->dsexamplelib_ctx)
    DsExampleCtxDeinit (dsexample->dsexamplelib_ctx);
  return FALSE;
}

/**
 * Stop the output thread and free up all the resources
 */
static gboolean
gst_dsexample_stop (GstBaseTransform * btrans)
{
  GstDsExample *dsexample = GST_DSEXAMPLE (btrans);

  if (dsexample->inter_buf)
    cudaFree (dsexample->inter_buf);
  dsexample->inter_buf = NULL;

  if (dsexample->host_rgb_buf)
    cudaFreeHost (dsexample->host_rgb_buf);
  dsexample->host_rgb_buf = NULL;

  if (dsexample->npp_stream)
    cudaStreamDestroy (dsexample->npp_stream);
  dsexample->npp_stream = NULL;

  delete dsexample->cvmat;
  dsexample->cvmat = NULL;

  GST_DEBUG_OBJECT (dsexample, "deleted CV Mat \n");

  // Deinit the algorithm library
  DsExampleCtxDeinit (dsexample->dsexamplelib_ctx);
  dsexample->dsexamplelib_ctx = NULL;

  GST_DEBUG_OBJECT (dsexample, "ctx lib released \n");

  return TRUE;
}

/**
 * Called when source / sink pad capabilities have been negotiated.
 */
static gboolean
gst_dsexample_set_caps (GstBaseTransform * btrans, GstCaps * incaps,
    GstCaps * outcaps)
{
  GstDsExample *dsexample = GST_DSEXAMPLE (btrans);

  /* Save the input video information, since this will be required later. */
  gst_video_info_from_caps (&dsexample->video_info, incaps);

  CHECK_CUDA_STATUS (cudaSetDevice (dsexample->gpu_id),
      "Unable to set cuda device");

  if (dsexample->inter_buf)
    cudaFree (dsexample->inter_buf);
  dsexample->inter_buf = NULL;

  /* An intermediate buffer for NV12/RGBA to RGB conversion  will be
   * required. Can be skipped if custom algorithm can work directly on NV12/RGBA. */
  CHECK_CUDA_STATUS (cudaMalloc (&dsexample->inter_buf,
          dsexample->video_info.width * dsexample->video_info.height *
          RGB_BYTES_PER_PIXEL), "Failed to allocate cuda buffer");

  return TRUE;

error:
  return FALSE;
}

/**
 * Scale the entire frame to the processing resolution maintaining aspect ratio.
 * Or crop and scale objects to the processing resolution maintaining the aspect
 * ratio. Remove the padding required by hardware and convert from RGBA to RGB
 * using openCV. These steps can be skipped if the algorithm can work with
 * padded data and/or can work with RGBA.
 */
static GstFlowReturn
get_converted_mat_dgpu (GstDsExample * dsexample, void *input_buf,
    NvOSD_RectParams * crop_rect_params, gdouble & ratio, gint input_width,
    gint input_height)
{
  gint src_left = (crop_rect_params->left);
  gint src_top = (crop_rect_params->top);
  gint src_width = (crop_rect_params->width);
  gint src_height = (crop_rect_params->height);

  // source ROI
  NppiRect oSrcROI = { (gint) 0,
    (gint) 0,
    (gint) src_width,
    (gint) src_height
  };
  NppiSize oSrcCropSize = { src_width, src_height };

  // Destination ROI
  NppiRect DstROI = { 0, 0, (gint) dsexample->processing_width,
    (gint) dsexample->processing_height
  };

  GST_DEBUG_OBJECT (dsexample, "Scaling and converting input buffer\n");

  // Calculate scaling ratio while maintaining aspect ratio
  ratio = MIN (1.0 * dsexample->processing_width / crop_rect_params->width,
      1.0 * dsexample->processing_height / crop_rect_params->height);

  if ((crop_rect_params->width == 0) || (crop_rect_params->height == 0)) {
    return GST_FLOW_ERROR;
  }

  nppSetStream (dsexample->npp_stream);

  // Memset the memory
  CHECK_CUDA_STATUS (cudaMemsetAsync (dsexample->host_rgb_buf, 0,
          dsexample->processing_width * dsexample->processing_height *
          RGB_BYTES_PER_PIXEL, dsexample->npp_stream),
      "Failed to memset cuda buffer");

  /* We will first convert only the Region of Interest (the entire frame or the
   * object bounding box) to RGB and then scale the converted RGB frame to
   * processing resolution. */

  if (dsexample->video_info.finfo->format == GST_VIDEO_FORMAT_RGBA) {
    /* Input is packed RGBA. First convert to packed RGB */

    /* Calculate the pointer to the top left corner pixel of the object crop /
     * frame. */
    const Npp8u *ptr_top_left_pixel =
        (Npp8u *) input_buf + (src_left +
        src_top * input_width) * RGBA_BYTES_PER_PIXEL;
    const int aDstOrder[3] = { 0, 1, 2 };       // {R, G, B}

    /* Convert ROI to RGB. */
    CHECK_NPP_STATUS (nppiSwapChannels_8u_C4C3R (ptr_top_left_pixel,
            input_width * RGBA_BYTES_PER_PIXEL, (Npp8u *) dsexample->inter_buf,
            src_width * RGB_BYTES_PER_PIXEL, oSrcCropSize, aDstOrder),
        "Failed to convert RGBA to RGB");
  } else {
    /* Input is NV12. First convert to packed RGB */

    /* Calculate the pointers to the top left corner pixel of the object crop or
     * frame. */
    const Npp8u *ptr_top_left_pixel_Y =
        (Npp8u *) input_buf + (src_top * input_width +
        src_left) * Y_BYTES_PER_PIXEL;
    const Npp8u *ptr_top_left_pixel_UV =
        (Npp8u *) input_buf + (input_width * input_height) +
        (((src_top / 2) * (input_width / 2)) +
        (src_left / 2)) * UV_BYTES_PER_PIXEL;
    const Npp8u *const ptr_top_left_pixel[2] =
        { ptr_top_left_pixel_Y, ptr_top_left_pixel_UV };


    /* Convert ROI to RGB. */
    CHECK_NPP_STATUS (nppiNV12ToRGB_8u_P2C3R (ptr_top_left_pixel, input_width,
            (Npp8u *) dsexample->inter_buf, src_width * RGB_BYTES_PER_PIXEL,
            oSrcCropSize), "Failed to convert NV12 to RGB");
  }

  /* Scale RGB to processing resolution. */
  CHECK_NPP_STATUS (nppiResizeSqrPixel_8u_C3R ((const Npp8u *)
          dsexample->inter_buf, oSrcCropSize, src_width * RGB_BYTES_PER_PIXEL,
          oSrcROI, (Npp8u *) dsexample->host_rgb_buf,
          dsexample->processing_width * RGB_BYTES_PER_PIXEL, DstROI, ratio,
          ratio, 0, 0, NPPI_INTER_LINEAR), "Failed to scale RGB frame");

  CHECK_CUDA_STATUS (cudaStreamSynchronize (dsexample->npp_stream),
      "Failed to synchronize cuda stream");

  return GST_FLOW_OK;

error:
  return GST_FLOW_ERROR;
}

/**
 * Called when element recieves an input buffer from upstream element.
 */
static GstFlowReturn
gst_dsexample_transform_ip (GstBaseTransform * btrans, GstBuffer * inbuf)
{
  GstDsExample *dsexample = GST_DSEXAMPLE (btrans);
  GstMapInfo in_map_info;
  GstFlowReturn flow_ret = GST_FLOW_ERROR;
  gdouble scale_ratio;
  DsExampleOutput *output;

  NvBufSurface *surface = NULL;
  guint batch_size = 1;
  GstNvStreamMeta *streamMeta = NULL;

  dsexample->frame_num++;
  CHECK_CUDA_STATUS (cudaSetDevice (dsexample->gpu_id),
      "Unable to set cuda device");

  memset (&in_map_info, 0, sizeof (in_map_info));
  if (!gst_buffer_map (inbuf, &in_map_info, GST_MAP_READ)) {
    g_print ("Error: Failed to map gst buffer\n");
    goto error;
  }

  surface = (NvBufSurface *) in_map_info.data;
  GST_DEBUG_OBJECT (dsexample,
      "Processing Frame %" G_GUINT64_FORMAT " Surface %p\n",
      dsexample->frame_num, surface);

  if (CHECK_NVDS_MEMORY_AND_GPUID (dsexample, surface))
    goto error;

  /* Stream meta for batched mode */
  streamMeta = gst_buffer_get_nvstream_meta (inbuf);
  if (streamMeta) {
    batch_size = MIN (streamMeta->num_filled, dsexample->batch_size);
  }

  if (dsexample->process_full_frame) {
    for (guint i = 0; i < batch_size; i++) {
      NvOSD_RectParams rect_params;

      // Scale the entire frame to processing resolution
      rect_params.left = 0;
      rect_params.top = 0;
      rect_params.width = dsexample->video_info.width;
      rect_params.height = dsexample->video_info.height;

      // Scale and convert the frame
      if (get_converted_mat_dgpu (dsexample, surface->buf_data[i], &rect_params,
              scale_ratio, dsexample->video_info.width,
              dsexample->video_info.height) != GST_FLOW_OK) {
        goto error;
      }
      // Process to get the output
      output =
          DsExampleProcess (dsexample->dsexamplelib_ctx,
          dsexample->cvmat->data);
      // Attach the metadata for the full frame
      attach_metadata_full_frame (dsexample, inbuf, scale_ratio, output, i);
      free (output);
    }

  } else {
    // Using object crops as input to the algorithm. The objects are detected by
    // the primary detector
    GstMeta *gst_meta;
    NvDsMeta *dsmeta;
    // NOTE: Initializing state to NULL is essential
    gpointer state = NULL;
    NvDsFrameMeta *bbparams;

    // Standard way of iterating through buffer metadata
    while ((gst_meta = gst_buffer_iterate_meta (inbuf, &state)) != NULL) {
      // Check if this metadata is of NvDsMeta type
      if (!gst_meta_api_type_has_tag (gst_meta->info->api, _dsmeta_quark))
        continue;

      dsmeta = (NvDsMeta *) gst_meta;
      // Check if the metadata of NvDsMeta contains object bounding boxes
      if (dsmeta->meta_type != NVDS_META_FRAME_INFO)
        continue;

      bbparams = (NvDsFrameMeta *) dsmeta->meta_data;
      // Check if these parameters have been set by the primary detector /
      // tracker
      if (bbparams->gie_type != 1) {
        continue;
      }
      // Iterate through all the objects
      for (guint i = 0; i < bbparams->num_rects; i++) {
        NvDsObjectParams *obj_param = &bbparams->obj_params[i];

        // Crop and scale the object
        if (get_converted_mat_dgpu (dsexample,
                surface->buf_data[bbparams->batch_id], &obj_param->rect_params,
                scale_ratio, dsexample->video_info.width,
                dsexample->video_info.height) != GST_FLOW_OK) {
          goto error;
        }
        // Process the object crop to obtain label
        output = DsExampleProcess (dsexample->dsexamplelib_ctx,
            dsexample->cvmat->data);

        if (!obj_param->text_params.display_text) {
          bbparams->num_strings++;
        }
        // Attach labels for the object
        attach_metadata_object (dsexample, obj_param, output);

        free (output);
      }
    }
  }

  flow_ret = GST_FLOW_OK;

error:
  gst_buffer_unmap (inbuf, &in_map_info);
  return flow_ret;
}

/**
 * Free the metadata allocated in attach_metadata_full_frame
 */
static void
free_ds_meta (gpointer meta_data)
{
  NvDsFrameMeta *params = (NvDsFrameMeta *) meta_data;
  for (guint i = 0; i < params->num_rects; i++) {
    g_free (params->obj_params[i].text_params.display_text);
  }
  g_free (params->obj_params);
  g_free (params);
}

/**
 * Attach metadata for the full frame. We will be adding a new metadata.
 */
static void
attach_metadata_full_frame (GstDsExample * dsexample, GstBuffer * inbuf,
    gdouble scale_ratio, DsExampleOutput * output, guint batch_id)
{
  NvDsMeta *dsmeta;
  NvDsFrameMeta *bbparams = (NvDsFrameMeta *) g_malloc0 (sizeof (NvDsFrameMeta));
  // Allocate an array of size equal to the number of objects detected
  bbparams->obj_params =
      (NvDsObjectParams *) g_malloc0 (sizeof (NvDsObjectParams) *
      output->numObjects);
  // Should be set to 3 for custom elements
  bbparams->gie_type = 3;
  // Use HW for overlaying boxes
  bbparams->nvosd_mode = NV_OSD_MODE_GPU;
  bbparams->batch_id = batch_id;
  // Font to be used for label text
  static gchar font_name[] = "Arial";
  GST_DEBUG_OBJECT (dsexample, "Attaching metadata %d\n", output->numObjects);
  for (gint i = 0; i < output->numObjects; i++) {
    DsExampleObject *obj = &output->object[i];
    NvDsObjectParams *obj_param = &bbparams->obj_params[i];
    NvOSD_RectParams & rect_params = obj_param->rect_params;
    NvOSD_TextParams & text_params = obj_param->text_params;

    // Assign bounding box coordinates
    rect_params.left = obj->left;
    rect_params.top = obj->top;
    rect_params.width = obj->width;
    rect_params.height = obj->height;

    // Semi-transparent yellow background
    rect_params.has_bg_color = 0;
    rect_params.bg_color = (NvOSD_ColorParams) {
    1, 1, 0, 0.4};
    // Red border of width 6
    rect_params.border_width = 1;
    rect_params.border_color = (NvOSD_ColorParams) {
    1, 0, 0, 1};

    // Scale the bounding boxes proportionally based on how the object/frame was
    // scaled during input
    rect_params.left /= scale_ratio;
    rect_params.top /= scale_ratio;
    rect_params.width /= scale_ratio;
    rect_params.height /= scale_ratio;
    GST_DEBUG_OBJECT (dsexample, "Attaching rect%d of batch%u"
        "  left->%u top->%u width->%u"
        " height->%u label->%s\n", i, batch_id, rect_params.left,
        rect_params.top, rect_params.width, rect_params.height, obj->label);
    bbparams->num_rects++;

    // has_new_info should be set to TRUE whenever adding new/updating
    // information to NvDsAttrInfo
    obj_param->has_new_info = TRUE;
    // Update the approriate element of the attr_info array. Application knows
    // that output of this element is available at index "unique_id".
    strcpy (obj_param->attr_info[dsexample->unique_id].attr_label,
        obj->label);
    // is_attr_label should be set to TRUE indicating that above attr_label field is
    // valid
    obj_param->attr_info[dsexample->unique_id].is_attr_label = 1;
    // Obj not yet tracked
    obj_param->tracking_id = -1;

    // display_text required heap allocated memory
    text_params.display_text = g_strdup (obj->label);
    // Display text above the left top corner of the object
    text_params.x_offset = rect_params.left;
    text_params.y_offset = rect_params.top - 10;
    // Set black background for the text
    text_params.set_bg_clr = 1;
    text_params.text_bg_clr = (NvOSD_ColorParams) {
    0, 0, 0, 1};
    // Font face, size and color
    text_params.font_params.font_name = font_name;
    text_params.font_params.font_size = 11;
    text_params.font_params.font_color = (NvOSD_ColorParams) {
    1, 1, 1, 1};
    bbparams->num_strings++;
  }

  // Attach the NvDsFrameMeta structure as NvDsMeta to the buffer. Pass the
  // function to be called when freeing the meta_data
  dsmeta = gst_buffer_add_nvds_meta (inbuf, bbparams, free_ds_meta);
  dsmeta->meta_type = NVDS_META_FRAME_INFO;
}

/**
 * Only update string label in an existing object metadata. No bounding boxes.
 * We assume only one label per object is generated
 */
static void
attach_metadata_object (GstDsExample * dsexample, NvDsObjectParams * obj_param,
    DsExampleOutput * output)
{
  if (output->numObjects == 0)
    return;
  NvOSD_TextParams & text_params = obj_param->text_params;
  NvOSD_RectParams & rect_params = obj_param->rect_params;

  // has_new_info should be set to TRUE whenever adding new/updating
  // information to NvDsAttrInfo
  obj_param->has_new_info = TRUE;
  // Update the approriate element of the attr_info array. Application knows
  // that output of this element is available at index "unique_id".
  strcpy (obj_param->attr_info[dsexample->unique_id].attr_label,
      output->object[0].label);
  // is_attr_label should be set to TRUE indicating that above attr_label field is
  // valid
  obj_param->attr_info[dsexample->unique_id].is_attr_label = 1;
  // Set black background for the text
  // display_text required heap allocated memory
  if (text_params.display_text) {
    gchar *conc_string = g_strconcat (text_params.display_text, " ",
        output->object[0].label, NULL);
    g_free (text_params.display_text);
    text_params.display_text = conc_string;
  } else {
    // Display text above the left top corner of the object
    text_params.x_offset = rect_params.left;
    text_params.y_offset = rect_params.top - 10;
    text_params.display_text = g_strdup (output->object[0].label);
    // Font face, size and color
    text_params.font_params.font_name = "Arial";
    text_params.font_params.font_size = 11;
    text_params.font_params.font_color = (NvOSD_ColorParams) {
    1, 1, 1, 1};
    // Set black background for the text
    text_params.set_bg_clr = 1;
    text_params.text_bg_clr = (NvOSD_ColorParams) {
    0, 0, 0, 1};
  }

}

/**
 * Boiler plate for registering a plugin and an element.
 */
static gboolean
dsexample_plugin_init (GstPlugin * plugin)
{
  GST_DEBUG_CATEGORY_INIT (gst_dsexample_debug, "dsexample", 0,
      "dsexample plugin");

  return gst_element_register (plugin, "dsexample", GST_RANK_PRIMARY,
      GST_TYPE_DSEXAMPLE);
}

GST_PLUGIN_DEFINE (GST_VERSION_MAJOR,
    GST_VERSION_MINOR,
    dsexample,
    DESCRIPTION, dsexample_plugin_init, "3.0", LICENSE, BINARY_PACKAGE, URL)

"""

* Header file : dsexample_lib.h 

In [ ]:
"""#ifndef __DSEXAMPLE_LIB__
#define __DSEXAMPLE_LIB__

#ifdef __cplusplus
extern "C" {
#endif

typedef struct DsExampleCtx DsExampleCtx;

// Init parameters structure as input, required for instantiating dsexample_lib
typedef struct
{
  // Width at which frame/object will be scaled
  int processingWidth;
  // height at which frame/object will be scaled
  int processingHeight;
  // Flag to indicate whether operating on crops of full frame
  int fullFrame;
} DsExampleInitParams;

// Detected/Labelled object structure, stores bounding box info along with label
typedef struct
{
  int left;
  int top;
  int width;
  int height;
  char label[64];
} DsExampleObject;

// Output data returned after processing
typedef struct
{
  int numObjects;
  DsExampleObject object[4];
} DsExampleOutput;

// Initialize library context
DsExampleCtx * DsExampleCtxInit (DsExampleInitParams *init_params);

// Dequeue processed output
DsExampleOutput *DsExampleProcess (DsExampleCtx *ctx, unsigned char *data);

// Deinitialize library context
void DsExampleCtxDeinit (DsExampleCtx *ctx);

#ifdef __cplusplus
}
#endif

#endif
"""

* gstdsexample.h

In [ ]:
"""/**
 * Copyright (c) 2017-2018, NVIDIA CORPORATION.  All rights reserved.
 *
 * NVIDIA Corporation and its licensors retain all intellectual property
 * and proprietary rights in and to this software, related documentation
 * and any modifications thereto.  Any use, reproduction, disclosure or
 * distribution of this software and related documentation without an express
 * license agreement from NVIDIA Corporation is strictly prohibited.
 *
 */

#ifndef __GST_DSEXAMPLE_H__
#define __GST_DSEXAMPLE_H__

#include <gst/base/gstbasetransform.h>
#include <gst/video/video.h>

/* Open CV headers */
#include "opencv2/imgproc/imgproc.hpp"
#include "opencv2/highgui/highgui.hpp"

#include <cuda.h>
#include <cuda_runtime.h>
#include "nvbuffer.h"
#include "gst-nvquery.h"
#include "gstnvstreammeta.h"
#include "gstnvdsmeta.h"
#include "dsexample_lib_cpp/dsexample_lib.h"

/* Package and library details required for plugin_init */
#define PACKAGE "dsexample"
#define VERSION "1.0"
#define LICENSE "Proprietary"
#define DESCRIPTION "NVIDIA example plugin for integration with DeepStream on DGPU"
#define BINARY_PACKAGE "NVIDIA DeepStream 3rdparty IP integration example plugin"
#define URL "http://nvidia.com/"


G_BEGIN_DECLS
/* Standard boilerplate stuff */
typedef struct _GstDsExample GstDsExample;
typedef struct _GstDsExampleClass GstDsExampleClass;

/* Standard boilerplate stuff */
#define GST_TYPE_DSEXAMPLE (gst_dsexample_get_type())
#define GST_DSEXAMPLE(obj) (G_TYPE_CHECK_INSTANCE_CAST((obj),GST_TYPE_DSEXAMPLE,GstDsExample))
#define GST_DSEXAMPLE_CLASS(klass) (G_TYPE_CHECK_CLASS_CAST((klass),GST_TYPE_DSEXAMPLE,GstDsExampleClass))
#define GST_DSEXAMPLE_GET_CLASS(obj) (G_TYPE_INSTANCE_GET_CLASS((obj), GST_TYPE_DSEXAMPLE, GstDsExampleClass))
#define GST_IS_DSEXAMPLE(obj) (G_TYPE_CHECK_INSTANCE_TYPE((obj),GST_TYPE_DSEXAMPLE))
#define GST_IS_DSEXAMPLE_CLASS(klass) (G_TYPE_CHECK_CLASS_TYPE((klass),GST_TYPE_DSEXAMPLE))
#define GST_DSEXAMPLE_CAST(obj)  ((GstDsExample *)(obj))

struct _GstDsExample
{
  GstBaseTransform base_trans;

  // Context of the custom algorithm library
  DsExampleCtx *dsexamplelib_ctx;

  // Unique ID of the element. The labels generated by the element will be
  // updated at index `unique_id` of attr_info array in NvDsObjectParams.
  guint unique_id;

  // Frame number of the current input buffer
  guint64 frame_num;

  // NPP Stream used for allocating the CUDA task
  cudaStream_t npp_stream;

  // Host buffer to store RGB data for use by algorithm
  void *host_rgb_buf;

  // the intermediate scratch buffer for conversions
  void *inter_buf;

  // OpenCV mat containing RGB data
  cv::Mat *cvmat;

  // Input video info (resolution, color format, framerate, etc)
  GstVideoInfo video_info;

  // Resolution at which frames/objects should be processed
  gint processing_width;
  gint processing_height;

  // Amount of objects processed in single call to algorithm
  guint batch_size;

  // GPU ID on which we expect to execute the task
  guint gpu_id;

  // Boolean indicating if entire frame or cropped objects should be processed
  gboolean process_full_frame;
};

// Boiler plate stuff
struct _GstDsExampleClass
{
  GstBaseTransformClass parent_class;
};

GType gst_dsexample_get_type (void);

G_END_DECLS
#endif /* __GST_DSEXAMPLE_H__ */
"""

<a id='comp-run-7'></a>
### 7.6 Compile and Run

In [23]:
!rm -f DeepStream_Release/sources/gst-plugins/gst-dsexample/libgstnvdsexample.so && \
make -C DeepStream_Release/sources/gst-plugins/gst-dsexample -f Makefile_cpp

make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/gst-plugins/gst-dsexample'
-fPIC -I /usr/include/include -I /usr/local/cuda-10.0/include -I ../../includes -pthread -I/usr/include/gstreamer-1.0 -I/usr/lib/x86_64-linux-gnu/gstreamer-1.0/include -I/usr/include/glib-2.0 -I/usr/lib/x86_64-linux-gnu/glib-2.0/include -I/usr/include/opencv
g++ -std=c++11 -c -o gstdsexample.o -fPIC -I /usr/include/include -I /usr/local/cuda-10.0/include -I ../../includes -pthread -I/usr/include/gstreamer-1.0 -I/usr/lib/x86_64-linux-gnu/gstreamer-1.0/include -I/usr/include/glib-2.0 -I/usr/lib/x86_64-linux-gnu/glib-2.0/include -I/usr/include/opencv gstdsexample.cpp
-fPIC -I /usr/include/include -I /usr/local/cuda-10.0/include -I ../../includes -pthread -I/usr/include/gstreamer-1.0 -I/usr/lib/x86_64-linux-gnu/gstreamer-1.0/include -I/usr/include/glib-2.0 -I/usr/lib/x86_64-linux-gnu/glib-2.0/include -I/usr/include/opencv
g++ -o libgstnvdsexample.so gstdsexample.o -shared -Wl,-no-undefin

We also need to copy the built library to the gstreamer directory and clear our cache. Once we have done that, we are ready to run the pipeline.

In [24]:
!cp DeepStream_Release/sources/gst-plugins/gst-dsexample/libgstnvdsexample.so /usr/lib/x86_64-linux-gnu/gstreamer-1.0/

In [25]:
!rm $HOME/.cache/gstreamer-1.0/registry.x86_64.bin

In [26]:
# Run the pipeline

!GST_DEBUG_DUMP_DOT_DIR=./ gst-launch-1.0 filesrc location=DeepStream_Release/samples/streams/car1.mp4 ! decodebin ! \
  nvvidconv ! "video/x-raw(memory:NVMM), format=(string)RGBA" ! \
  dsexample processing-width=160 processing-height=120 ! nvosd ! queue ! \
  nvvidconv ! "video/x-raw, format=(string)RGBA" ! videoconvert ! x264enc ! qtmux ! filesink location=out_dsmotion.mp4

Setting pipeline to PAUSED ...
Pipeline is PREROLLING ...
Redistribute latency...
Pipeline is PREROLLED ...
Setting pipeline to PLAYING ...
New clock: GstSystemClock
Got EOS from element "pipeline0".
Execution ended after 0:00:22.463550191
Setting pipeline to PAUSED ...
Setting pipeline to READY ...
Setting pipeline to NULL ...
Freeing pipeline ...


<a id='vis-pipeline'></a>
### 7.7 Visualizing the Pipeline

When the pipeline is finished, we can visualize it to get a better understanding of the data flow. By setting `GST_DEBUG_DUMP_DOT_DIR` before running the pipeline, DeepStream will create pipeline diagrams (graphs) to visualize the pipeline in different states. 

The `dot` command comes from [graphviz](https://www.graphviz.org/), and it lets us convert `.dot` files into standard image formats. 

In [27]:
!ls ./ | grep PLAYING_PAUSED

0.00.24.423156160-gst-launch.PLAYING_PAUSED.dot


In [30]:
!dot -Tpng ./0.00.24.423156160-gst-launch.PLAYING_PAUSED.dot > ./pipeline_custom_plugin1_opencvbased.png

 Each block corresponds to an element in our pipeline, and the arrows indicate the flow of data (from left to right). The first block on the left is the __filesrc block__. This is the beginning of our pipeline. Data flows from here into the large __decodebin__ block, which contains multiple sub-blocks corresponding to different elements in our pipeline. 

You may have noticed that there is a __Caps filter__ (in fact, there are several throughout the pipeline). We have seen these in pipelines before (in our DeepStream application code), and briefly discussed Caps in the beginning of the lab. 

When an element has more than one output pad, it might not be clear which one should be used. An example of this would be when an element outputs both audio and video, and the next element could operate on either of them. In this situation, GStreamer effectively chooses a pad randomly. This isn't what we want. __Caps filters__ are our solution. They are essentially pass-through elements which only accepts media with the given capabilities, effectively resolving the ambiguity.  

<a id='ev-output'></a>
### 7.8 Evaluate the Output

We can now look at our output. Note that our motion detection algorithm was relatively successful. The bounding boxes generally follow the moving car, though not perfectly. The motion of the camera itself appears to be causing some issues.  

In [31]:
from IPython.display import HTML
HTML("""
<video width="640" height="480" controls>
  <source src="out_dsmotion.mp4" type="video/mp4">
</video>
""".format())

We learned that DeepStream supports custom plugins, and that we can use custom plugins in addition to or instead of existing plugins like __NvInfer__. We learned how to compose pipelines at the command line, and how that can help us in prototyping and rapidly visualizing our pipeline. We also learned how the basics of how a motion detection algorithm could work, and saw a simple implementation using OpenCV. 

When we implement custom plugins though, we also must implement the code that handles all the necessary mechanics to treat it as a GStreamer plugin. Because of that, we covered the necessary functionality at a high level and downloaded the example implementation for future reference. 

<a id='od-multiple'></a>
## 8. Object Detection on Multiple Input Streams 

Up until now, we have looked at one video stream at a time. In some circumstances, though, we may want to use the same model to detect objects from multiple video streams. In this exercise, we will build a pipeline that accepts multiple input files and runs our object detection neural network on them. Like before, we will be building a pipeline at the command line for ease of explanation. 

<a id='batch-input'></a>
 ### 8.1 Batching Input Streams 

DeepStream provides the plugins, __nvstreammux__ and __nvstreamdemux__, to streamline processing multiple input streams. The video aggregator plugin (__nvstreammux__) forms a batch of buffers from the input sources and creates the necessary metadata to differentiate between the buffers of different source files. Once the batch is created, the DeepStream pipeline continues as expected. For example, in our pipeline, we will do object detection using a TensorRT optimized neural network via the NvInfer plugin to detect objects in the batch of frames.  

<img src='images/multiple_input_batching.png' style='width:80%'/> 

<p style="text-align: center;color:gray">Figure 17. Multiple input pipeline</p>     

When we have finished inferencing, we need to separate the buffers so we can create output files for each of the input streams. We use the plugin __nvstreamdemux__ to go from 1 batch to N separate streams. Because our DeepStream pipeline keeps track of the metadata, this process is simple and completely painless. 

<a id='compose-pipline'></a>
### 8.2 Composing a Pipeline 

We are ready to compose a pipeline that runs detection on two video streams. Our pipeline is going to look a lot like the one in the previous exercise. But there will be three key differences: 

1. Because we are operating on multiple inputs, we need to create video parsing, decoding, conversion, and sink elements for each input. We do them separately to allow for inputs that require different types of processing 

2. We include __nvstreammux__ and its `name` property, to batch the input streams 

3. We include __nvstreamdemux__ and its `name` property, to separate the batched frames 

We use the value supplied to the `name` property to easily access information in these two elements. When we want to access the first input stream from our batch, we do that with the notation `name.src_0`. In the same way, when we want to `sink` the first input stream from our batch, we can do that with the notation `name.sink_0`. 


In [43]:
!gst-launch-1.0 nvstreammux name=mux batch-size=1 width=1280 height=720 ! nvinfer config-file-path=./DeepStream_Release/samples/configs/deepstream-app/config_infer_primary.txt ! nvstreamdemux name=demux \
filesrc location=./DeepStream_Release/samples/streams/1.264 ! h264parse ! nvdec_h264 ! queue ! mux.sink_0 \
filesrc location=./DeepStream_Release/samples/streams/2.264 ! decodebin ! queue ! mux.sink_1 \
demux.src_0 ! "video/x-raw(memory:NVMM), format=NV12" ! queue ! nvvidconv ! "video/x-raw(memory:NVMM), format=RGBA" ! nvosd font-size=15 ! nvvidconv ! "video/x-raw, format=RGBA" ! videoconvert ! "video/x-raw, format=NV12" ! x264enc ! qtmux ! filesink location=./out3.mp4 \
demux.src_1 ! "video/x-raw(memory:NVMM), format=NV12" ! queue ! nvvidconv ! "video/x-raw(memory:NVMM), format=RGBA" ! nvosd font-size=15 ! nvvidconv ! "video/x-raw, format=RGBA" ! videoconvert ! "video/x-raw, format=NV12" ! x264enc ! qtmux ! filesink location=./out4.mp4 

Setting pipeline to PAUSED ...
>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Primary_Detector/resnet10.caffemodel_b30_int8.engine crypto flags(0)
Pipeline is PREROLLING ...
Redistribute latency...
Pipeline is PREROLLED ...
Setting pipeline to PLAYING ...
New clock: GstSystemClock
Got EOS from element "pipeline0".
Execution ended after 0:00:07.912238049
Setting pipeline to PAUSED ...
Setting pipeline to READY ...
Setting pipeline to NULL ...
Freeing pipeline ...


If the pipeline was successful, you should see the printed output that looks like:

<br></br>

```
Setting pipeline to PAUSED ...
>>> Using TRT model serialized engine /dli/dl-deepstream-deployment/English/notebooks/DeepStream_Release/samples/configs/deepstream-app/../../models/Primary_Detector/resnet10.caffemodel_b30_int8.engine crypto flags(0)
Pipeline is PREROLLING ...
Redistribute latency...
Redistribute latency...
Redistribute latency...
Pipeline is PREROLLED ...
Setting pipeline to PLAYING ...
New clock: GstSystemClock
Got EOS from element "pipeline0".
Execution ended after 0:00:25.710410137
Setting pipeline to PAUSED ...
Setting pipeline to READY ...
Setting pipeline to NULL ...
Freeing pipeline ...
```

If your output looks like this, you are ready to look at the results!


In [44]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="./out3.mp4" type="video/mp4">
    </video>
""".format())

In [ ]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="./out4.mp4" type="video/mp4">
    </video>
""".format())

Notice that one video is much longer than the other (in fact, one is a 19 second clip taken from the other), yet DeepStream was able to process both at the same time! 

In this section, we learned how DeepStream makes it easy to handle multiple video streams at once. Using nvstreammux and nvstreamdemux, we can batch and separate video streams for efficient processing and analysis. 

<a id='dewarp'></a>
## 9. Dewarping 360° camera streams

All the video files we have examined so far, had flat rectangular frames, making the inference process immediate and straightforward.  360° camera feeds (also known as omnidirectional cameras) however, are growing in demand and consequently rapid pre-processing and _dewarping_ become vital tasks. 

You can view omnidirectional video by executing the following cell:

In [35]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="./DeepStream_Release/sources/apps/deepstream-test5/sample_cam6.mp4" type="video/mp4">
    </video>
""".format())

The 360° camera's field of view covers the entire sphere (or a full circle of view) and provides a wide visual field coverage. these raw camera feeds are not useful for inference unless we `dewarp` them into flat video feeds and process them separately. `Dewarping` is a technique that mathematically corrects the deformed (warped) camera feeds so that all the curved lines turn back into straight lines. This process is computationally expensive and delays the inference by expanding the preprocess step, resulting in significant delays 

<br /> 
<img src='images/dewarp.jpg'/> 

<p style="text-align: center;color:gray">Figure 18. Dewarp process, left: 360° camera feed - right: 4 dewarped surfaces</p> 
<br /> 

In this section, we will work with the GPU-accelerated `gst-nvdewarper` plugin for dewarping camera feeds. The gst-nvdewarper plugin included in the SDK provides hardware-accelerated solutions to dewarp and transform an image to a planar projection. Reducing distortion makes these images more suitable for viewing and processing with existing deep learning models. The current plugin supports `pushbroom` and `vertically panned radical cylinder` projections. 
<br /> 

<img src='images/dewarp_plugin.jpg'/> 
<p style="text-align: center;color:gray">Figure 19. The Gst-nvdewarper plugin</p> 
<br /> 

In addition, the dewarper plugin requires a `config-file` which specifies the camera specs and the output videos properties. Configuration file paramters; 

- __projection-type__: Selects projection type. Supported projection types are:1 = PushBroom, 2 = VertRadCyl 
- __surface-index__:   An index that distinguishes surfaces of the same projection type 
- __width__:           Dewarped surface width 
- __height__:          Dewarped surface height 
- __top-angle__:       Top field of view angle, in degrees 
- __bottom-angle__:    Bottom field of view angle, in degrees 
- __pitch__:           Viewing parameter pitch in degrees 
- __yaw__:             Viewing parameter yaw in degrees 
- __roll__:            Viewing parameter roll in degrees 
- __focal-length__:    Focal length of camera lens, in pixels per radian  

The following pipeline takes a 360° camera feed and after decoding, the `nvdewarper` plugin dewarps the feed into four surfaces. We do not apply any inference for brevity and only save one of the surfaces as output: 

* configuration files

In [ ]:
"""
[property]
#scale dewarped surfaces to specified output width and height
output-width=960
output-height=752
# 0 - pinned, 1 - device, 2 -unified
cuda-memory-type=1
#dewarp-dump-frames=10

#########################################
# Note - Max 4 surfaces are supported
#########################################

[surface0]
# 1=PushBroom, 2=VertRadCyl
projection-type=2
surface-index=0
#dewarped surface parameters
width=1902
height=1500
top-angle=90.3
bottom-angle=0.3
pitch=0
yaw=0
roll=278
focal-length=437

[surface1]
# 1=PushBroom, 2=VertRadCyl
projection-type=2
surface-index=1
#dewarped surface parameters
width=1902
height=1500
top-angle=90.3
bottom-angle=0.3
pitch=0
yaw=0
roll=98
focal-length=437

[surface2]
# 1=PushBroom, 2=VertRadCyl
projection-type=1
surface-index=0
#dewarped surface parameters
width=3886
height=666
top-angle=0
bottom-angle=-35
pitch=90
yaw=0
roll=0
focal-length=437

[surface3]
# 1=PushBroom, 2=VertRadCyl
projection-type=1
surface-index=1
#dewarped surface parameters
width=3886
height=666
top-angle=0
bottom-angle=-35
pitch=90
yaw=0
roll=180
focal-length=437
"""

In [45]:
!gst-launch-1.0 filesrc location=DeepStream_Release/sources/apps/deepstream-test5/sample_cam6.mp4 ! \
qtdemux ! h264parse ! nvdec_h264 ! nvvidconv ! nvdewarper config-file=DeepStream_Release/sources/apps/deepstream-test5/config_dewarper.txt ! \
m.sink_0 nvstreammux name=m width=960 height=752 batch-size=4 ! \
nvvidconv ! capsfilter caps="video/x-raw, format=RGBA" ! videoconvert ! capsfilter caps="video/x-raw, format=NV12" ! \
x264enc ! qtmux ! filesink location=DeepStream_Release/sources/apps/deepstream-test5/out.mp4

Setting pipeline to PAUSED ...
Pipeline is PREROLLING ...
Redistribute latency...
Pipeline is PREROLLED ...
Setting pipeline to PLAYING ...
New clock: GstSystemClock
Got EOS from element "pipeline0".
Execution ended after 0:00:02.799222849
Setting pipeline to PAUSED ...
Setting pipeline to READY ...
Setting pipeline to NULL ...
Freeing pipeline ...


You may view the resulting video by executing the following cell:

In [46]:
from IPython.display import HTML
HTML("""
    <video width="640" height="480" controls>
      <source src="./DeepStream_Release/sources/apps/deepstream-test5/out.mp4" type="video/mp4">
    </video>
""".format())

---

<a id='msgconv'></a>
## 10. Using "nvmsgconv" and "nvmsgbroker" plugins in the pipeline

An important capability of DeepStream which is added in version 3.0, is to encapsulate the generated metadata (tracks, bounding boxes, etc.) as messages and sending them for further analysis. These data could be used for a variety of tasks including anomaly detection, building long-term trends on location and movement and providing information dashboards for remote viewing, and more. 

Let's consider the metadata generated by DeepStream first. At the end of the pipeline, the generated metadata represents the complete set of information extracted from the elements of the pipeline. We need to make this information accessible to the external consumers as part of a message for further analysis or long term archival. 

<a id='gst-nvmsgconv'></a>
### 10.1 The  gst-nvmsgconv plugin

The  `gst-nvmsgconv` plugin accepts a metadata structure of `NvDsEventMsgMeta` type and generates the corresponding __message payload__.  this plugin provides a comprehensive JSON-based schema description has been defined that specifies events based on associated objects, location and time of occurrence, and underlying sensor information while specifying attributes for each of these event properties. 

By default, the `NvDsEventMsgMeta` plugin generates messages based on the DeepStream schema description. However, it also allows the user to register their own metadata-to-payload converter functions for additional customizability. Using custom metadata descriptions in combination with user-defined conversion functions gives the user the ability to implement a fully custom event description and messaging capability that perfectly meets their needs. 

<a id='gst-nvmsgbroker'></a>
### 10.2 The  gst-nvmsgbroker plugin

 After generating the augmented message with user data, the `gst-nvmsgbroker` plugin provides a message delivery mechanism using the __Apache Kafka__ protocol to Kafka message brokers. Kafka serves as a conduit into a backend event analysis system, including those executing in the cloud. The high message throughput support, combined with reliability offered by the Kafka framework, enables the backend architecture to scale to support numerous DeepStream applications continuously sending messages. 

The `gst-nvmsgbroker` plugin is implemented in a protocol agnostic manner and leverages protocol adapters in the form of shared libraries. These can be modified to support any user defined protocol.

**As we do not utilize a kafka instance, we are going to make a customized gst-nvmsgbroker plugin that dumps the metadata inside a text file instead of connecting to the kafka sever.**

 <br /> 
<img src='images/ts_broker.png'/> 

<p style="text-align: center;color:gray">Figure 20. message transformation and broker plugins working in combination to deliver messages encapsulating detected events to backend analysis systems</p> 
<br /> 

First, we are going to create a broker by implementing the `nvds_msgapi.h` API that removes all network communication codes and simply writes the metadata into a file. There are five main functions that this api implements:

- __nvds_msgapi_connect__: which connects to the broker and returns a message handler of type `NvDsMsgApiHandle`
- __nvds_msgapi_send__: for sending the payload string to the target synchronously
- __nvds_msgapi_send_async__: for sending the payload string to the target asynchronously
- __nvds_msgapi_disconnect__: terminating the connection and freeing up the resources
- __nvds_msgapi_getversion__: get the broker API version

Now let's build our broker and then we will see how to use this custom broker in our app.

* customized gst-nvmsgbroker plugin : broker/broker.cpp

In [ ]:
"""
#include "nvds_msgapi.h"
#include <iostream>
#include <fstream>
#define MAX_FIELD_LEN 255 //maximum topic length supported by kafka is 255
#define NVDS_MSGAPI_VERSION "1.0"

typedef struct {
  void *kh;
  char topic[MAX_FIELD_LEN];
} NvDsKafkaProtoConn;

void logit(std::string log)
{
  std::ofstream outfile;
  outfile.open("logs.txt", std::ios_base::app);
  outfile << std::endl << log << std::endl; 
  return;
}
void logit(const uint8_t *payload)
{
  std::ofstream outfile;
  outfile.open("logs.txt", std::ios_base::app);
  outfile << std::endl << payload << std::endl; 
  return;
}

NvDsMsgApiHandle nvds_msgapi_connect(char *connection_str, nvds_msgapi_connect_cb_t connect_cb, char *config_path)
{
    logit("Connecting");
    NvDsKafkaProtoConn *conn_ptr = (NvDsKafkaProtoConn *)malloc(sizeof(NvDsKafkaProtoConn));
    logit("Connected");
    return conn_ptr;
}
NvDsMsgApiErrorType nvds_msgapi_send(NvDsMsgApiHandle h_ptr, char *topic, const uint8_t *payload, size_t nbuf)
{
    logit(payload);
    return NVDS_MSGAPI_OK;
}
NvDsMsgApiErrorType nvds_msgapi_send_async(NvDsMsgApiHandle h_ptr, char  *topic, const uint8_t *payload, size_t nbuf, nvds_msgapi_send_cb_t send_callback, void *user_ptr)
{
   logit(payload);
   return NVDS_MSGAPI_OK;
}
void nvds_msgapi_do_work(NvDsMsgApiHandle h_ptr)
{
    //logit("nvds_msgapi_do_work call");
}
NvDsMsgApiErrorType nvds_msgapi_disconnect(NvDsMsgApiHandle h_ptr)
{
    logit("Disconnecting");
    return NVDS_MSGAPI_OK;
}
char *nvds_msgapi_getversion()
{
    logit("nvds_msgapi_getversion call");
    return (char *)NVDS_MSGAPI_VERSION;
}
"""

In [47]:
!rm DeepStream_Release/sources/apps/deepstream-test4/broker/*.so
!rm DeepStream_Release/sources/apps/deepstream-test4/logs.txt
!make -C DeepStream_Release/sources/apps/deepstream-test4/broker

rm: cannot remove 'DeepStream_Release/sources/apps/deepstream-test4/logs.txt': No such file or directory
make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test4/broker'
g++ -fPIC -std=c++11 -I /usr/include/include -I ../../../includes -I/usr/local/opencv-3.4.1/include -pthread -I/usr/include/gstreamer-1.0 -I/usr/lib/x86_64-linux-gnu/gstreamer-1.0/include -I/usr/include/glib-2.0 -I/usr/lib/x86_64-linux-gnu/glib-2.0/include -shared broker.cpp -o broker.so
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test4/broker'


This broker has a minimal implementation of the broker class, the deepstream SDK is shipped with the full kafka implementation of the broker.

<a id='example-10'></a>
### 10.3 The "nvmsgconv" and "nvmsgbroker" example application

How to utilize the "nvmsgconv" and "nvmsgbroker" plugins. This sample builds on top of the deepstream-test1 sample to demonstrate how to: 

* Use "nvmsgconv" and "nvmsgbroker" plugins in the pipeline. 
* Create NVDS_META_EVENT_MSG type of meta and attach to buffer. 
* Use NVDS_META_EVENT_MSG for different types of objects e.g. vehicle, person etc. 
* Provide copy / free functions if meta data is extended through "extMsg" field. 

First, we make elements of both plugins: 

```c 
  /* Create msg converter to generate payload from buffer metadata */ 
  msgconv = gst_element_factory_make ("nvmsgconv", "nvmsg-converter"); 
  /* Create msg broker to send payload to server */ 
  msgbroker = gst_element_factory_make ("nvmsgbroker", "nvmsg-broker"); 
``` 

The `nvmsgconv` plugin uses NVDS_META_EVENT_MSG type of metadata from the buffer and generates the "DeepStream Schema" payload in Json format. Static properties of schema are read from configuration file in the form of key-value pair. 

```c 
g_object_set (G_OBJECT(msgconv), "config", "dstest4_msgconv_config.txt", NULL); 

``` 

Check `dstest4_msgconv_config.txt` for reference. Generated payload is attached as `NVDS_META_PAYLOAD` type metadata to the buffer. Note that in addition to common fields provided in `NvDsEventMsgMeta` structure, user can also create custom objects and attach to buffer as `NVDS_META_EVENT_MSG` metadata. To do that `NvDsEventMsgMeta` provides "extMsg" and `extMsgSize` fields. User can 

create custom structure, fill that structure and assign the pointer of that structure as `extMsg` and set the `extMsgSize` accordingly. If custom object contains fields that can't be simply mem copied, then user should also provide function to copy and free those objects. 

Finally, `nvmsgbroker` plugin extracts `NVDS_META_PAYLOAD` type of metadata from the buffer and sends that payload to the server using protocol adaptor APIs. We use the library we built previously as the broker library: 

```c 
#define PROTOCOL_ADAPTOR_LIB  "broker/broker.so" 
... 
g_object_set (G_OBJECT(msgbroker), "proto-lib", PROTOCOL_ADAPTOR_LIB, 
              "conn-str", CONNECTION_STRING, "sync", FALSE, NULL); 
``` 

In [ ]:
"""
#include <gst/gst.h>
#include <glib.h>
#include <stdlib.h>
#include <string.h>
#include <time.h>
#include <sys/timeb.h>

#include "gstnvdsmeta.h"

#define MAX_DISPLAY_LEN 64
#define MAX_TIME_STAMP_LEN 32

#define PGIE_CLASS_ID_VEHICLE 0
#define PGIE_CLASS_ID_PERSON 2

#define PROTOCOL_ADAPTOR_LIB  "broker/broker.so"
#define CONNECTION_STRING "foo.bar.com;80;dsapp1"

gint frame_number = 0;
gchar pgie_classes_str[4][32] = { "Vehicle", "TwoWheeler", "Person",
  "Roadsign"
};

static void generate_ts_rfc3339 (char *buf, int buf_size)
{
  time_t tloc;
  struct timeb timeb_log;
  struct tm tm_log;
  struct timespec ts;
  char strmsec[6]; //.nnnZ\0

  clock_gettime(CLOCK_REALTIME,  &ts);
  memcpy(&tloc, (void *)(&ts.tv_sec), sizeof(time_t));
  gmtime_r(&tloc, &tm_log);
  strftime(buf, buf_size,"%Y-%m-%dT%H:%M:%S", &tm_log);
  int ms = ts.tv_nsec/1000000;
  g_snprintf(strmsec, sizeof(strmsec),".%.3dZ", ms);
  strncat(buf, strmsec, buf_size);
}

static gpointer meta_copy_func (gpointer data, gpointer user_data)
{
  NvDsEventMsgMeta *srcMeta = (NvDsEventMsgMeta *) data;
  NvDsEventMsgMeta *dstMeta = NULL;

  dstMeta = g_memdup (srcMeta, sizeof(NvDsEventMsgMeta));

  if (srcMeta->ts)
    dstMeta->ts = g_strdup (srcMeta->ts);

  if (srcMeta->objSignature.size > 0) {
    dstMeta->objSignature.signature = g_memdup (srcMeta->objSignature.signature,
                                                srcMeta->objSignature.size);
    dstMeta->objSignature.size = srcMeta->objSignature.size;
  }

  if (srcMeta->extMsgSize > 0) {
    if (srcMeta->objType == NVDS_OBJECT_TYPE_VEHICLE) {
      NvDsVehicleObject *srcObj = (NvDsVehicleObject *) srcMeta->extMsg;
      NvDsVehicleObject *obj = (NvDsVehicleObject *) g_malloc0 (sizeof (NvDsVehicleObject));
      if (srcObj->type)
        obj->type = g_strdup (srcObj->type);
      if (srcObj->make)
        obj->make = g_strdup (srcObj->make);
      if (srcObj->model)
        obj->model = g_strdup (srcObj->model);
      if (srcObj->color)
        obj->color = g_strdup (srcObj->color);
      if (srcObj->license)
        obj->license = g_strdup (srcObj->license);
      if (srcObj->region)
        obj->region = g_strdup (srcObj->region);

      dstMeta->extMsg = obj;
      dstMeta->extMsgSize = sizeof (NvDsVehicleObject);
    } else if (srcMeta->objType == NVDS_OBJECT_TYPE_PERSON) {
      NvDsPersonObject *srcObj = (NvDsPersonObject *) srcMeta->extMsg;
      NvDsPersonObject *obj = (NvDsPersonObject *) g_malloc0 (sizeof (NvDsPersonObject));

      obj->age = srcObj->age;

      if (srcObj->gender)
        obj->gender = g_strdup (srcObj->gender);
      if (srcObj->cap)
        obj->cap = g_strdup (srcObj->cap);
      if (srcObj->hair)
        obj->hair = g_strdup (srcObj->hair);
      if (srcObj->apparel)
        obj->apparel = g_strdup (srcObj->apparel);
    }
  }

  return dstMeta;
}

static void meta_free_func (gpointer data, gpointer user_data)
{
  NvDsEventMsgMeta *srcMeta = (NvDsEventMsgMeta *) data;

  if (srcMeta->ts)
    g_free (srcMeta->ts);

  if (srcMeta->objSignature.size > 0) {
    g_free (srcMeta->objSignature.signature);
    srcMeta->objSignature.size = 0;
  }

  if (srcMeta->extMsgSize > 0) {
    if (srcMeta->objType == NVDS_OBJECT_TYPE_VEHICLE) {
      NvDsVehicleObject *obj = (NvDsVehicleObject *) srcMeta->extMsg;
      if (obj->type)
        g_free (obj->type);
      if (obj->color)
        g_free (obj->color);
      if (obj->make)
        g_free (obj->make);
      if (obj->model)
        g_free (obj->model);
      if (obj->license)
        g_free (obj->license);
      if (obj->region)
        g_free (obj->region);
    } else if (srcMeta->objType == NVDS_OBJECT_TYPE_PERSON) {
      NvDsPersonObject *obj = (NvDsPersonObject *) srcMeta->extMsg;

      if (obj->gender)
        g_free (obj->gender);
      if (obj->cap)
        g_free (obj->cap);
      if (obj->hair)
        g_free (obj->hair);
      if (obj->apparel)
        g_free (obj->apparel);
    }
    g_free (srcMeta->extMsg);
    srcMeta->extMsgSize = 0;
  }
  g_free (data);
}

static void
generate_vehicle_meta (gpointer data)
{
  NvDsVehicleObject *obj = (NvDsVehicleObject *) data;

  obj->type = g_strdup ("sedan");
  obj->color = g_strdup ("blue");
  obj->make = g_strdup ("Bugatti");
  obj->model = g_strdup ("M");
  obj->license = g_strdup ("XX1234");
  obj->region = g_strdup ("CA");
}

static void
generate_person_meta (gpointer data)
{
  NvDsPersonObject *obj = (NvDsPersonObject *) data;
  obj->age = 45;
  obj->cap = g_strdup ("none");
  obj->hair = g_strdup ("black");
  obj->gender = g_strdup ("male");
  obj->apparel= g_strdup ("formal");
}

static void
generate_event_msg_meta (gpointer data, gint class_id)
{
  NvDsEventMsgMeta *meta = (NvDsEventMsgMeta *) data;
  meta->sensorId = 0;
  meta->placeId = 0;
  meta->moduleId = 0;

  meta->ts = (gchar *) g_malloc0 (MAX_TIME_STAMP_LEN + 1);

  generate_ts_rfc3339(meta->ts, MAX_TIME_STAMP_LEN);

  /*
   * This demonstrates how to attach custom objects.
   * Any custom object as per requirement can be generated and attached
   * like NvDsVehicleObject / NvDsPersonObject. Then that object should
   * be handled in gst-nvmsgconv component accordingly.
   */
  if (class_id == PGIE_CLASS_ID_VEHICLE) {
    meta->type = NVDS_EVENT_MOVING;
    meta->objType = NVDS_OBJECT_TYPE_VEHICLE;
    meta->objClassId = PGIE_CLASS_ID_VEHICLE;

    NvDsVehicleObject *obj = (NvDsVehicleObject *) g_malloc0 (sizeof (NvDsVehicleObject));
    generate_vehicle_meta (obj);

    meta->extMsg = obj;
    meta->extMsgSize = sizeof (NvDsVehicleObject);
  } else if (class_id == PGIE_CLASS_ID_PERSON) {
    meta->type = NVDS_EVENT_ENTRY;
    meta->objType = NVDS_OBJECT_TYPE_PERSON;
    meta->objClassId = PGIE_CLASS_ID_PERSON;

    NvDsPersonObject *obj = (NvDsPersonObject *) g_malloc0 (sizeof (NvDsPersonObject));
    generate_person_meta (obj);

    meta->extMsg = obj;
    meta->extMsgSize = sizeof (NvDsPersonObject);
  }
}

/* osd_sink_pad_buffer_probe  will extract metadata received on OSD sink pad
 * and update params for drawing rectangle, object information etc. */

static GstPadProbeReturn
osd_sink_pad_buffer_probe (GstPad * pad, GstPadProbeInfo * info,
    gpointer u_data)
{

  GstMeta *gst_meta = NULL;
  NvDsMeta *nvdsmeta = NULL;
  gpointer state = NULL;
  static GQuark _nvdsmeta_quark = 0;
  GstBuffer *buf = (GstBuffer *) info->data;
  NvDsFrameMeta *frame_meta = NULL;
  guint num_rects = 0, rect_index = 0, l_index = 0;
  NvDsObjectParams *obj_meta = NULL;
  guint i = 0;
  NvOSD_TextParams *txt_params = NULL;
  guint vehicle_count = 0;
  guint person_count = 0;
  gboolean is_first_rect = TRUE;

  if (!_nvdsmeta_quark)
    _nvdsmeta_quark = g_quark_from_static_string (NVDS_META_STRING);

  while ((gst_meta = gst_buffer_iterate_meta (buf, &state))) {
    if (gst_meta_api_type_has_tag (gst_meta->info->api, _nvdsmeta_quark)) {

      nvdsmeta = (NvDsMeta *) gst_meta;

      /* We are interested only in intercepting Meta of type
       * "NVDS_META_FRAME_INFO" as they are from our infer elements. */
      if (nvdsmeta->meta_type == NVDS_META_FRAME_INFO) {
        frame_meta = (NvDsFrameMeta *) nvdsmeta->meta_data;
        if (frame_meta == NULL) {
          g_print ("NvDS Meta contained NULL meta \n");
          return GST_PAD_PROBE_OK;
        }

        /* We reset the num_strings here as we plan to iterate through the
         *  the detected objects and form our own strings.
         *  The pipeline generated strings shall be discarded.
         */
        frame_meta->num_strings = 0;

        num_rects = frame_meta->num_rects;
        is_first_rect = TRUE;

        /* This means we have num_rects in frame_meta->obj_params,
         * now lets iterate through them */

        for (rect_index = 0; rect_index < num_rects; rect_index++) {
          /* Now using above information we need to form a text that should
           * be displayed on top of the bounding box, so lets form it here. */

          obj_meta = (NvDsObjectParams *) & frame_meta->obj_params[rect_index];

          txt_params = &(obj_meta->text_params);
          if (txt_params->display_text)
            g_free (txt_params->display_text);

          txt_params->display_text = g_malloc0 (MAX_DISPLAY_LEN);

          g_snprintf (txt_params->display_text, MAX_DISPLAY_LEN, "%s ",
              pgie_classes_str[obj_meta->class_id]);

          if (obj_meta->class_id == PGIE_CLASS_ID_VEHICLE)
            vehicle_count++;
          if (obj_meta->class_id == PGIE_CLASS_ID_PERSON)
            person_count++;

          /* Now set the offsets where the string should appear */
          txt_params->x_offset = obj_meta->rect_params.left;
          txt_params->y_offset = obj_meta->rect_params.top - 25;

          /* Font , font-color and font-size */
          txt_params->font_params.font_name = "Arial";
          txt_params->font_params.font_size = 10;
          txt_params->font_params.font_color.red = 1.0;
          txt_params->font_params.font_color.green = 1.0;
          txt_params->font_params.font_color.blue = 1.0;
          txt_params->font_params.font_color.alpha = 1.0;

          /* Text background color */
          txt_params->set_bg_clr = 1;
          txt_params->text_bg_clr.red = 0.0;
          txt_params->text_bg_clr.green = 0.0;
          txt_params->text_bg_clr.blue = 0.0;
          txt_params->text_bg_clr.alpha = 1.0;

          frame_meta->num_strings++;

          /*
           * Ideally NVDS_META_EVENT_MSG should be attached to buffer by the
           * component implementing detection / recognition logic.
           * Here it demonstrates how to use / attach that meta data.
           */
          if (is_first_rect && !(frame_number % 30)) {
            /* Frequency of messages to be send will be based on use case.
             * Here message is being sent for first object every 30 frames.
             */
            NvDsMeta *gst_event_meta = NULL;
            NvDsEventMsgMeta *msg_meta = (NvDsEventMsgMeta *) g_malloc0 (sizeof (NvDsEventMsgMeta));
            generate_event_msg_meta (msg_meta, obj_meta->class_id);
            gst_event_meta = gst_buffer_add_nvds_meta (buf, msg_meta, NULL);
            if (gst_event_meta) {
              gst_event_meta->meta_type = NVDS_META_EVENT_MSG;
              /*
               * Since generated event metadata has custom objects for
               * Vehicle / Person which are allocated dynamically, we are
               * setting copy and free function to handle those fields when
               * metadata copy happens between two components.
               */
              nvds_meta_set_copy_function_full(gst_event_meta, meta_copy_func, NULL, meta_free_func);
            } else {
              g_print ("Error in attaching event meta to buffer\n");
            }
            is_first_rect = FALSE;
          }
        }
      }
    }
  }
  g_print ("Frame Number = %d Number of objects = %d "
      "Vehicle Count = %d Person Count = %d\n",
      frame_number, num_rects, vehicle_count, person_count);
  frame_number++;

  return GST_PAD_PROBE_OK;
}

static gboolean
bus_call (GstBus * bus, GstMessage * msg, gpointer data)
{
  GMainLoop *loop = (GMainLoop *) data;
  switch (GST_MESSAGE_TYPE (msg)) {
    case GST_MESSAGE_EOS:
      g_print ("End of stream\n");
      g_main_loop_quit (loop);
      break;
    case GST_MESSAGE_ERROR:{
      gchar *debug;
      GError *error;
      gst_message_parse_error (msg, &error, &debug);
      g_printerr ("ERROR from element %s: %s\n",
          GST_OBJECT_NAME (msg->src), error->message);
      if (debug)
        g_printerr ("Error details: %s\n", debug);
      g_free (debug);
      g_error_free (error);
      g_main_loop_quit (loop);
      break;
    }
    default:
      break;
  }
  return TRUE;
}

int
main (int argc, char *argv[])
{
  GMainLoop *loop = NULL;
  GstElement *pipeline = NULL, *source = NULL, *h264parser = NULL,
      *decoder = NULL, *sink = NULL, *pgie = NULL, *nvvidconv = NULL,
      *nvosd = NULL, *filter1 = NULL, *filter2 = NULL;
  GstElement *msgconv = NULL, *msgbroker = NULL, *tee = NULL;
  GstElement *queue1 = NULL, *queue2 = NULL;
  GstBus *bus = NULL;
  guint bus_watch_id;
  gulong osd_probe_id = 0;
  GstPad *osd_sink_pad = NULL;
  GstPad *tee_render_pad = NULL;
  GstPad *tee_msg_pad = NULL;
  GstPad *sink_pad = NULL;
  GstCaps *caps1 = NULL, *caps2 = NULL;

  GstElement *nvvidconv1 = NULL;
  GstElement *filter3 = NULL;
  GstElement *videoconvert = NULL;
  GstElement *filter4 = NULL;
  GstElement *x264enc = NULL;
  GstElement *qtmux = NULL;
  GstCaps *caps3 = NULL, *caps4 = NULL;
    
  /* Check input arguments */
  if (argc != 2) {
    g_printerr ("Usage: %s <H264 filename>\n", argv[0]);
    return -1;
  }

  /* Standard GStreamer initialization */
  gst_init (&argc, &argv);
  loop = g_main_loop_new (NULL, FALSE);

  /* Create gstreamer elements */
  /* Create Pipeline element that will form a connection of other elements */
  pipeline = gst_pipeline_new ("dstest4-pipeline");

  /* Source element for reading from the file */
  source = gst_element_factory_make ("filesrc", "file-source");
    
  sink = gst_element_factory_make ("fakesink", "fakesink");

  /* Since the data format in the input file is elementary h264 stream,
   * we need a h264parser */
  h264parser = gst_element_factory_make ("h264parse", "h264-parser");

  /* Use nvdec_h264 for hardware accelerated decode on GPU */
  decoder = gst_element_factory_make ("nvdec_h264", "nvh264-decoder");

  /* Use nvinfer to run inferencing on decoder's output,
   * behaviour of inferencing is set through config file */
  pgie = gst_element_factory_make ("nvinfer", "primary-nvinference-engine");

  /* Use convertor to convert from NV12 to RGBA as required by nvosd */
  nvvidconv = gst_element_factory_make ("nvvidconv", "nvvideo-converter");

  /* Create OSD to draw on the converted RGBA buffer */
  nvosd = gst_element_factory_make ("nvosd", "nv-onscreendisplay");
    
  nvvidconv1 = gst_element_factory_make("nvvidconv", "nvvideo-converter1");
  videoconvert = gst_element_factory_make("videoconvert", "converter");
  x264enc = gst_element_factory_make("x264enc", "h264 encoder");
  qtmux = gst_element_factory_make("qtmux", "muxer");

  /* Create msg converter to generate payload from buffer metadata */
  msgconv = gst_element_factory_make ("nvmsgconv", "nvmsg-converter");

  /* Create msg broker to send payload to server */
  msgbroker = gst_element_factory_make ("nvmsgbroker", "nvmsg-broker");

  /* Create tee to render buffer and send message simultaneously*/
  tee = gst_element_factory_make ("tee", "nvsink-tee");

  /* Create queues */
  queue1 = gst_element_factory_make ("queue", "nvtee-que1");
  queue2 = gst_element_factory_make ("queue", "nvtee-que2");
    
    
  /* caps filter for nvvidconv to convert NV12 to RGBA as nvosd expects input
  * in RGBA format */
  filter1 = gst_element_factory_make ("capsfilter", "filter1");
  filter2 = gst_element_factory_make ("capsfilter", "filter2");
  filter3 = gst_element_factory_make ("capsfilter", "filter3");
  filter4 = gst_element_factory_make ("capsfilter", "filter4");

  /* Finally render the osd output */
  //sink = gst_element_factory_make ("nveglglessink", "nvvideo-renderer");

  if (!pipeline || !source || !h264parser || !decoder || !pgie
      || !nvvidconv || !nvosd || !msgconv || !msgbroker || !tee
      || !queue1 || !queue2 || !sink) {
    g_printerr ("One element could not be created. Exiting.\n");
    return -1;
  }
  if (!nvvidconv1 || !x264enc || !qtmux || !filter3 || !filter4) {
    g_printerr("one element could not be created. Exiting.\n");
    return -1;
  }
  /* we set the input filename to the source element */
  g_object_set (G_OBJECT (source), "location", argv[1], NULL);
    
  //g_object_set(G_OBJECT(sink), "location", "out_test1.mp4", NULL);

  /* Set all the necessary properties of the nvinfer element,
   * the necessary ones are : */
  g_object_set (G_OBJECT (pgie),
      "config-file-path", "dstest4_pgie_config.txt", NULL);

  /* we set the osd properties here */
  g_object_set (G_OBJECT (nvosd), "font-size", 15, NULL);

  g_object_set (G_OBJECT(msgconv), "config", "dstest4_msgconv_config.txt", NULL);

  g_object_set (G_OBJECT(msgbroker), "proto-lib", PROTOCOL_ADAPTOR_LIB,
                "conn-str", CONNECTION_STRING, "sync", FALSE, NULL);

  /* we add a message handler */
  bus = gst_pipeline_get_bus (GST_PIPELINE (pipeline));
  bus_watch_id = gst_bus_add_watch (bus, bus_call, loop);
  gst_object_unref (bus);

  /* Set up the pipeline */
  /* we add all elements into the pipeline */
  gst_bin_add_many (GST_BIN (pipeline),
      source, h264parser, decoder, pgie,
      filter1, nvvidconv, filter2,nvvidconv1,nvvidconv1, filter3,
      videoconvert, filter4, x264enc, qtmux, nvosd, tee, queue1, queue2, msgconv,
      msgbroker, sink, NULL);
    


  /* we link the elements together */
  /* file-source -> h264-parser -> nvh264-decoder ->
   * nvinfer -> nvvidconv -> nvosd -> tee -> video-renderer
   *                                      |
   *                                      |-> msgconv -> msgbroker  */
  caps1 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=NV12");
  g_object_set (G_OBJECT (filter1), "caps", caps1, NULL);
  gst_caps_unref (caps1);
  caps2 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=RGBA");
  g_object_set (G_OBJECT (filter2), "caps", caps2, NULL);
  gst_caps_unref (caps2);
  caps3 = gst_caps_from_string("video/x-raw, format=RGBA");
  g_object_set(G_OBJECT(filter3), "caps", caps3, NULL);
  gst_caps_unref(caps3);
  caps4 = gst_caps_from_string("video/x-raw, format=NV12");
  g_object_set(G_OBJECT(filter4), "caps", caps4, NULL);
  gst_caps_unref(caps4);
    
    
  if (!gst_element_link_many (source, h264parser, decoder, pgie,filter1,
      nvvidconv,filter2, nvosd,nvvidconv1, filter3,
      videoconvert, filter4, tee, NULL)) {
    g_printerr ("Elements could not be linked. Exiting.\n");
    return -1;
  }

  if (!gst_element_link_many (queue1, msgconv, msgbroker, NULL)) {
    g_printerr ("Elements could not be linked. Exiting.\n");
    return -1;
  }

  if (!gst_element_link_many (queue2,  sink, NULL)) {
    g_printerr ("Elements could not be linked. Exiting.\n");
    return -1;
  }

  sink_pad = gst_element_get_static_pad (queue1, "sink");
  tee_msg_pad = gst_element_get_request_pad (tee, "src_%u");
  tee_render_pad = gst_element_get_request_pad (tee, "src_%u");
  if (!tee_msg_pad || !tee_render_pad) {
    g_printerr ("Unable to get request pads\n");
    return -1;
  }

  if (gst_pad_link (tee_msg_pad, sink_pad) != GST_PAD_LINK_OK) {
    g_printerr ("Unable to link tee and message converter\n");
    gst_object_unref (sink_pad);
    return -1;
  }

  gst_object_unref (sink_pad);

  sink_pad = gst_element_get_static_pad (queue2, "sink");
  if (gst_pad_link (tee_render_pad, sink_pad) != GST_PAD_LINK_OK) {
    g_printerr ("Unable to link tee and render\n");
    gst_object_unref (sink_pad);
    return -1;
  }

  gst_object_unref (sink_pad);

  /* Lets add probe to get informed of the meta data generated, we add probe to
   * the sink pad of the osd element, since by that time, the buffer would have
   * had got all the metadata. */
  osd_sink_pad = gst_element_get_static_pad (nvosd, "sink");
  if (!osd_sink_pad)
    g_print ("Unable to get sink pad\n");
  else
    osd_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER,
        osd_sink_pad_buffer_probe, NULL, NULL);

  /* Set the pipeline to "playing" state */
  g_print ("Now playing: %s\n", argv[1]);
  gst_element_set_state (pipeline, GST_STATE_PLAYING);

  /* Wait till pipeline encounters an error or EOS */
  g_print ("Running...\n");
  g_main_loop_run (loop);

  /* Out of the main loop, clean up nicely */
  g_print ("Returned, stopping playback\n");

  /* Release the request pads from the tee, and unref them */
  gst_element_release_request_pad (tee, tee_msg_pad);
  gst_element_release_request_pad (tee, tee_render_pad);
  gst_object_unref (tee_msg_pad);
  gst_object_unref (tee_render_pad);

  gst_element_set_state (pipeline, GST_STATE_NULL);
  g_print ("Deleting pipeline\n");
  gst_object_unref (GST_OBJECT (pipeline));
  g_source_remove (bus_watch_id);
  g_main_loop_unref (loop);
  return 0;
}
"""

In [49]:
!rm DeepStream_Release/sources/apps/deepstream-test4/deepstream-test4-app
!rm DeepStream_Release/sources/apps/deepstream-test4/deepstream_test4_app.o
!make -C DeepStream_Release/sources/apps/deepstream-test4/

!cd DeepStream_Release/sources/apps/deepstream-test4 && \
./deepstream-test4-app  ../../../samples/streams/sample_720p.h264

rm: cannot remove 'DeepStream_Release/sources/apps/deepstream-test4/deepstream-test4-app': No such file or directory
rm: cannot remove 'DeepStream_Release/sources/apps/deepstream-test4/deepstream_test4_app.o': No such file or directory
make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test4'
cc -I../../includes `pkg-config --cflags gstreamer-1.0`   -c -o deepstream_test4_app.o deepstream_test4_app.c
cc -o deepstream-test4-app deepstream_test4_app.o `pkg-config --libs gstreamer-1.0` -L/usr/local/deepstream/ -lnvdsgst_meta -lrt -Wl,-rpath,/usr/local/deepstream
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test4'

(deepstream-test4-app:581): GStreamer-WARNING **: Name 'nvvideo-converter1' is not unique in bin 'dstest4-pipeline', not adding
Now playing: ../../../samples/streams/sample_720p.h264
>>> Generating new TRT model engine
Using INT8 data type.

 ***** Storing serialized engine file as /dli/task

Frame Number = 97 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 98 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 99 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 100 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 101 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 102 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 103 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 104 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 105 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 106 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 107 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 108 Number of objects = 9 Vehicle Count = 5 Person Count = 4
Frame Number = 109 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Fram

Frame Number = 212 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 213 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 214 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 215 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 216 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 217 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 218 Number of objects = 10 Vehicle Count = 7 Person Count = 2
Frame Number = 219 Number of objects = 9 Vehicle Count = 6 Person Count = 2
Frame Number = 220 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 221 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 222 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 223 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 224 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Fram

Frame Number = 326 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 327 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 328 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Frame Number = 329 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 330 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 331 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 332 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 333 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 334 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 335 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 336 Number of objects = 14 Vehicle Count = 10 Person Count = 4
Frame Number = 337 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 338 Number of objects = 13 Vehicle Count = 9 Person Count = 4


Frame Number = 438 Number of objects = 12 Vehicle Count = 7 Person Count = 4
Frame Number = 439 Number of objects = 14 Vehicle Count = 8 Person Count = 5
Frame Number = 440 Number of objects = 11 Vehicle Count = 7 Person Count = 3
Frame Number = 441 Number of objects = 13 Vehicle Count = 9 Person Count = 3
Frame Number = 442 Number of objects = 9 Vehicle Count = 6 Person Count = 2
Frame Number = 443 Number of objects = 7 Vehicle Count = 4 Person Count = 2
Frame Number = 444 Number of objects = 8 Vehicle Count = 6 Person Count = 1
Frame Number = 445 Number of objects = 9 Vehicle Count = 5 Person Count = 4
Frame Number = 446 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 447 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 448 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 449 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 450 Number of objects = 12 Vehicle Count = 10 Person Count = 2


...

Frame Number = 1006 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1007 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1008 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1009 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1010 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1011 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1012 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1013 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1014 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1015 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 1016 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 1017 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1018 Number of objects = 9 Vehicle Count = 6 Person Count 

Frame Number = 1112 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1113 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1114 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1115 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1116 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 1117 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1118 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1119 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1120 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1121 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1122 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1123 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1124 Number of objects = 8 Vehicle Count = 6 Person Count = 2

Frame Number = 1225 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1226 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1227 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1228 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1229 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1230 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1231 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1232 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1233 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1234 Number of objects = 7 Vehicle Count = 4 Person Count = 3
Frame Number = 1235 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1236 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 1237 Number of objects = 8 Vehicle Count = 5 Person Count = 3

Frame Number = 1332 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1333 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1334 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1335 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1336 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1337 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1338 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1339 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1340 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1341 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1342 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1343 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1344 Number of objects = 9 Vehicle Count = 7 Person Count 

Deleting pipeline


You may have noticed that we write the broker message into the logs.txt file. Let's have a look at the content of this file:

In [50]:
!head DeepStream_Release/sources/apps/deepstream-test4/logs.txt -n 1000


Connecting

Connected

{
  "messageid" : "9bc927f0-9e38-4ec2-9209-b5a499863e8f",
  "mdsversion" : "1.0",
  "@timestamp" : "2022-09-03T18:26:52.199Z",
  "place" : {
    "id" : "1",
    "name" : "XYZ",
    "type" : "garage",
    "location" : {
      "lat" : 30.32,
      "lon" : -40.549999999999997,
      "alt" : 100
    },
    "aisle" : {
      "id" : "walsh",
      "name" : "lane1",
      "level" : "P2",
      "coordinate" : {
        "x" : 1,
        "y" : 2,
        "z" : 3
      }
    }
  },
  "sensor" : {
    "id" : "CAMERA_ID",
    "type" : "Camera",
    "description" : "\"Entrance of Garage Right Lane\"",
    "location" : {
      "lat" : 45.293701446999997,
      "lon" : -75.830391449900006,
      "alt" : 48.155747933800001
    },
    "coordinate" : {
      "x" : 5.2000000000000002,
      "y" : 10.1,
      "z" : 11.199999999999999
    }
  },
  "analyticsModule" : {
    "id" : "XYZ",
    "description" : "\"Vehicle Detection and License Plate Recognition\"",
    "source" : "OpenALR

As you can see the meta-data from the `dstest4_msgconv_config.txt` is attached as `NVDS_META_PAYLOAD` type metadata to the buffer as a custom buffer. Moreover, you can add the meta-data dynamically to other elements of the pipeline in a similar manner by adding a probe to the element event and attaching `NVDS_META_PAYLOAD` data. 

<a id='PERFORMANCE_ANALYSIS'></a>
## 11. Performance Analysis
---

<a id='gen-kpi'></a>
### 11.1 Generating Performance KPIs 
    
In this section, we will learn how to generate performance KPIs for the workload created in section 4. The key metrics we will highlight are: 

* Throughput: Using gst probes installed in the display plugin
* GPU Performance Metrics: Using nvidia-smi
* Latency: Using gst logs / gst tracer


<a id='throughput'></a>
### 11.2 Throughput

Just as we previously used probes to access metadata, we can also use [probes](https://gstreamer.freedesktop.org/documentation/application-development/advanced/pipeline-manipulation.html#using-probes) to measure throughput and get a sense of the dataflow. As we saw before, we installed our function for metadata handling with `gst_pad_add_probe`.

Below, instead of handling metadata, we are going to install a second probe that will log the time it takes for a frame to pass through the on screen display plugin. We are going to print out our frame rate for a single video stream, but we could expand this to generate metrics such as minimum, maximum, and average frame throughput at a granular level for each video stream.


Open deepstream_test1_app.c  and uncomment the following lines of code (lines 355 and 356 unless you have added new lines to the file).

```c
perf_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER, sink_bin_buf_probe, NULL, NULL);
```
     
With this line, we are adding another user-defined callback function, `sink_bin_buf_probe`, to our pipeline (it's defined beginning at line 130 in the code). We have copied the callback function below for ease of explanation.


```c
static GstPadProbeReturn
sink_bin_buf_probe (GstPad * pad, GstPadProbeInfo * info, gpointer u_data)
{

  static struct timeval last_fps_time;
  static struct timeval curr_fps_time;
  static int numbuff = 0;
  
  /* this parameter determines after how many frames fps metrics are reported */
  const int FPS_DISPLAY_FREQ = 10; 

  if ((numbuff++ % FPS_DISPLAY_FREQ) == 0) {
    //last fps is not recorded
    if (last_fps_time.tv_sec == 0
        && last_fps_time.tv_usec == 0)
      /* first time around */
      gettimeofday (&last_fps_time, NULL); 
    else {
      gettimeofday (&curr_fps_time, NULL);
      gdouble elapsedtime  =
          (curr_fps_time.tv_sec +
            curr_fps_time.tv_usec / 1000000.0) -
          (last_fps_time.tv_sec +
            last_fps_time.tv_usec / 1000000.0);
      g_print ("%.2f fps\n", (FPS_DISPLAY_FREQ/elapsedtime));
      last_fps_time = curr_fps_time;
    }
      
  }
  return GST_PAD_PROBE_OK;
  
}
```

This probe is simple. Every `FPS_DISPLAY_FREQ` number of frames (currently set to 10), we are going to calculate how much time has elapsed. We then divide the number of frames by the time elapsed (in seconds) to get our current rate of frames per second. We print that value out, and return an OK signal, which tells the pipeline that we are operating correctly.


When you are confident you understand how the probe works, you are ready to build the application in the next cell.

**deepstream_test1_app.c**

In [ ]:
"""
#include <gst/gst.h>
#include <glib.h>!make -C DeepStream_Release/sources/apps/deepstream-test1 clean

!make -C DeepStream_Release/sources/apps/deepstream-test1
#include <sys/time.h>
#include "gstnvdsmeta.h"

#define MAX_DISPLAY_LEN 64

#define PGIE_CLASS_ID_VEHICLE 0
#define PGIE_CLASS_ID_PERSON 2

gint frame_number = 0;
gchar pgie_classes_str[4][32] = { "Vehicle", "TwoWheeler", "Person",
  "Roadsign"
};

static GstPadProbeReturn
sink_bin_buf_probe (GstPad * pad, GstPadProbeInfo * info, gpointer u_data)
{

  static struct timeval last_fps_time;
  static struct timeval curr_fps_time;
  static int numbuff = 0;

  /* this parameter determines after how many frames fps metrics are reported */
  const int FPS_DISPLAY_FREQ = 10; 

  if ((numbuff++ % FPS_DISPLAY_FREQ) == 0) {
    //last fps is not recorded
    if (last_fps_time.tv_sec == 0
        && last_fps_time.tv_usec == 0)
      /* first time around */
      gettimeofday (&last_fps_time, NULL); 
    else {
      gettimeofday (&curr_fps_time, NULL);
      gdouble elapsedtime  =
          (curr_fps_time.tv_sec +
            curr_fps_time.tv_usec / 1000000.0) -
          (last_fps_time.tv_sec +
            last_fps_time.tv_usec / 1000000.0);
      g_print ("%.2f fps\n", (FPS_DISPLAY_FREQ/elapsedtime));
      last_fps_time = curr_fps_time;
    }

  }
  return GST_PAD_PROBE_OK;

}




/* osd_sink_pad_buffer_probe  will extract metadata received on OSD sink pad
 * and update params for drawing rectangle, object information etc. */

static GstPadProbeReturn
osd_sink_pad_buffer_probe (GstPad * pad, GstPadProbeInfo * info,
    gpointer u_data)
{

  GstMeta *gst_meta = NULL;
  NvDsMeta *nvdsmeta = NULL;
  gpointer state = NULL;
  static GQuark _nvdsmeta_quark = 0;
  GstBuffer *buf = (GstBuffer *) info->data;
  NvDsFrameMeta *frame_meta = NULL;
  guint num_rects = 0, rect_index = 0, l_index = 0;
  NvDsObjectParams *obj_meta = NULL;
  guint i = 0;
  NvOSD_TextParams *txt_params = NULL;
  guint vehicle_count = 0;
  guint person_count = 0;

  if (!_nvdsmeta_quark)
    _nvdsmeta_quark = g_quark_from_static_string (NVDS_META_STRING);

  while ((gst_meta = gst_buffer_iterate_meta (buf, &state))) {
    if (gst_meta_api_type_has_tag (gst_meta->info->api, _nvdsmeta_quark)) {

      nvdsmeta = (NvDsMeta *) gst_meta;

      /* We are interested only in intercepting Meta of type
       * "NVDS_META_FRAME_INFO" as they are from our infer elements. */
      if (nvdsmeta->meta_type == NVDS_META_FRAME_INFO) {
        frame_meta = (NvDsFrameMeta *) nvdsmeta->meta_data;
        if (frame_meta == NULL) {
          g_print ("NvDS Meta contained NULL meta \n");
          return GST_PAD_PROBE_OK;
        }

        /* We reset the num_strings here as we plan to iterate through the
         *  the detected objects and form our own strings.
         *  The pipeline generated strings shall be discarded.
         */
        frame_meta->num_strings = 0;

        num_rects = frame_meta->num_rects;

        /* This means we have num_rects in frame_meta->obj_params,
         * now lets iterate through them */

        for (rect_index = 0; rect_index < num_rects; rect_index++) {
          /* Now using above information we need to form a text that should
           * be displayed on top of the bounding box, so lets form it here. */

          obj_meta = (NvDsObjectParams *) & frame_meta->obj_params[rect_index];

          txt_params = &(obj_meta->text_params);
          if (txt_params->display_text)
            g_free (txt_params->display_text);

          txt_params->display_text = g_malloc0 (MAX_DISPLAY_LEN);

          g_snprintf (txt_params->display_text, MAX_DISPLAY_LEN, "%s ",
              pgie_classes_str[obj_meta->class_id]);

          if (obj_meta->class_id == PGIE_CLASS_ID_VEHICLE)
            vehicle_count++;
          if (obj_meta->class_id == PGIE_CLASS_ID_PERSON)
            person_count++;

          /* Now set the offsets where the string should appear */
          txt_params->x_offset = obj_meta->rect_params.left;
          txt_params->y_offset = obj_meta->rect_params.top - 25;

          /* Font , font-color and font-size */
          txt_params->font_params.font_name = "Arial";
          txt_params->font_params.font_size = 10;
          txt_params->font_params.font_color.red = 1.0;
          txt_params->font_params.font_color.green = 1.0;
          txt_params->font_params.font_color.blue = 1.0;
          txt_params->font_params.font_color.alpha = 1.0;

          /* Text background color */
          txt_params->set_bg_clr = 1;
          txt_params->text_bg_clr.red = 0.0;
          txt_params->text_bg_clr.green = 0.0;
          txt_params->text_bg_clr.blue = 0.0;
          txt_params->text_bg_clr.alpha = 1.0;

          frame_meta->num_strings++;
        }
      }
    }
  }
  g_print ("Frame Number = %d Number of objects = %d "
      "Vehicle Count = %d Person Count = %d\n",
      frame_number, num_rects, vehicle_count, person_count);
  frame_number++;

  return GST_PAD_PROBE_OK;
}

static gboolean
bus_call (GstBus * bus, GstMessage * msg, gpointer data)
{
  GMainLoop *loop = (GMainLoop *) data;
  switch (GST_MESSAGE_TYPE (msg)) {
    case GST_MESSAGE_EOS:
      g_print ("End of stream\n");
      g_main_loop_quit (loop);
      break;
    case GST_MESSAGE_ERROR:{
      gchar *debug;
      GError *error;
      gst_message_parse_error (msg, &error, &debug);
      g_printerr ("ERROR from element %s: %s\n",
          GST_OBJECT_NAME (msg->src), error->message);
      if (debug)
        g_printerr ("Error details: %s\n", debug);
      g_free (debug);
      g_error_free (error);
      g_main_loop_quit (loop);
      break;
    }
    default:
      break;
  }
  return TRUE;
}

int
main (int argc, char *argv[])
{
  GMainLoop *loop = NULL;
  GstElement *pipeline = NULL, *source = NULL, *h264parser =
      NULL,
      *decoder = NULL, *sink = NULL, *pgie = NULL, *nvvidconv =
      NULL, *nvosd = NULL, *filter1 = NULL, *filter2 = NULL;
  GstBus *bus = NULL;
  guint bus_watch_id;
  GstCaps *caps1 = NULL, *caps2 = NULL;
  gulong osd_probe_id = 0;
  gulong perf_probe_id = 0;
  GstPad *osd_sink_pad = NULL;

  GstElement *nvvidconv1 = NULL;
  GstElement *filter3 = NULL;
  GstElement *videoconvert = NULL;
  GstElement *filter4 = NULL;
  GstElement *x264enc = NULL;
  GstElement *qtmux = NULL;
  GstCaps *caps3 = NULL, *caps4 = NULL;

  /* Check input arguments */
  if (argc != 2) {
    g_printerr ("Usage: %s <H264 filename>\n", argv[0]);
    return -1;
  }

  /* Standard GStreamer initialization */
  gst_init (&argc, &argv);
  loop = g_main_loop_new (NULL, FALSE);

  /* Create gstreamer elements */
  /* Create Pipeline element that will form a connection of other elements */
  pipeline = gst_pipeline_new ("dstest1-pipeline");

  /* Source element for reading from the file */
  source = gst_element_factory_make ("filesrc", "file-source");

  /* Since the data format in the input file is elementary h264 stream,
   * we need a h264parser */
  h264parser = gst_element_factory_make ("h264parse", "h264-parser");

  /* Use nvdec_h264 for hardware accelerated decode on GPU */
  decoder = gst_element_factory_make ("nvdec_h264", "nvh264-decoder");

  /* Use nvinfer to run inferencing on decoder's output,
   * behaviour of inferencing is set through config file */
  pgie = gst_element_factory_make ("nvinfer", "primary-nvinference-engine");

  /* Use convertor to convert from NV12 to RGBA as required by nvosd */
  nvvidconv = gst_element_factory_make ("nvvidconv", "nvvideo-converter");

  /* Create OSD to draw on the converted RGBA buffer */
  nvosd = gst_element_factory_make ("nvosd", "nv-onscreendisplay");

  nvvidconv1 = gst_element_factory_make("nvvidconv", "nvvideo-converter1");
  videoconvert = gst_element_factory_make("videoconvert", "converter");
  x264enc = gst_element_factory_make("x264enc", "h264 encoder");
  qtmux = gst_element_factory_make("qtmux", "muxer");

  /* Finally render the osd output */
  sink = gst_element_factory_make ("filesink", "filesink");

  /* caps filter for nvvidconv to convert NV12 to RGBA as nvosd expects input
   * in RGBA format */
  filter1 = gst_element_factory_make ("capsfilter", "filter1");
  filter2 = gst_element_factory_make ("capsfilter", "filter2");
  filter3 = gst_element_factory_make ("capsfilter", "filter3");
  filter4 = gst_element_factory_make ("capsfilter", "filter4");
  if (!pipeline || !source || !h264parser || !decoder || !pgie
      || !filter1 || !nvvidconv || !filter2 || !nvosd || !sink) {
    g_printerr ("One element could not be created. Exiting.\n");
    return -1;
  }

  if (!nvvidconv1 || !x264enc || !qtmux || !filter3 || !filter4) {
    g_printerr("one element could not be created. Exiting.\n");
    return -1;
  }

  /* we set the input filename to the source element */
  g_object_set (G_OBJECT (source), "location", argv[1], NULL);

  g_object_set(G_OBJECT(sink), "location", "out_test1.mp4", NULL);

  /* Set all the necessary properties of the nvinfer element,
   * the necessary ones are : */
  g_object_set (G_OBJECT (pgie),
      "config-file-path", "dstest1_pgie_config.txt", NULL);

  /* we set the osd properties here */
  g_object_set (G_OBJECT (nvosd), "font-size", 15, NULL);

  /* we add a message handler */
  bus = gst_pipeline_get_bus (GST_PIPELINE (pipeline));
  bus_watch_id = gst_bus_add_watch (bus, bus_call, loop);
  gst_object_unref (bus);

  /*
    ////////////////////////////////////////////////////////////////////
    // <1> Set up the pipeline by adding all the elements
    ////////////////////////////////////////////////////////////////////
    // TODO1
    // Hints:
    //     1> Some elements are missing from the pipeline. You can refer to the elements defined above
         to see which ones aren't currently incorporated.
         2> Think about the kind of data stream we're handling
    */

  gst_bin_add_many (GST_BIN (pipeline),
      source, h264parser, decoder, pgie,
      filter1, nvvidconv, filter2, nvosd, nvvidconv1, filter3,
      videoconvert, filter4, x264enc, qtmux, sink, NULL);

  caps1 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=NV12");
  g_object_set (G_OBJECT (filter1), "caps", caps1, NULL);
  gst_caps_unref (caps1);
  caps2 = gst_caps_from_string ("video/x-raw(memory:NVMM), format=RGBA");
  g_object_set (G_OBJECT (filter2), "caps", caps2, NULL);
  gst_caps_unref (caps2);
  caps3 = gst_caps_from_string("video/x-raw, format=RGBA");
  g_object_set(G_OBJECT(filter3), "caps", caps3, NULL);
  gst_caps_unref(caps3);
  caps4 = gst_caps_from_string("video/x-raw, format=NV12");
  g_object_set(G_OBJECT(filter4), "caps", caps4, NULL);
  gst_caps_unref(caps4);
  

  /* we link the elements together */
  /* file-source -> h264-parser -> nvh264-decoder ->
   * nvinfer -> filter1 -> nvvidconv -> filter2 -> nvosd -> video-renderer */
  gst_element_link_many (source, h264parser, decoder, pgie, filter1,
      nvvidconv, filter2, nvosd, nvvidconv1, filter3,
      videoconvert, filter4,
      x264enc, qtmux, sink, NULL);

  /* Lets add probe to get informed of the meta data generated, we add probe to
   * the sink pad of the osd element, since by that time, the buffer would have
   * had got all the metadata. */
  osd_sink_pad = gst_element_get_static_pad (nvosd, "sink");
  if (!osd_sink_pad)
    g_print ("Unable to get sink pad\n");
  else {
    osd_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER, 
        osd_sink_pad_buffer_probe, NULL, NULL); 

    /* enable this for Performance Analysis Exercise */
   perf_probe_id = gst_pad_add_probe (osd_sink_pad, GST_PAD_PROBE_TYPE_BUFFER,
           sink_bin_buf_probe, NULL, NULL);
  }
 /*
    ////////////////////////////////////////////////////////////////////
    // <1> Set the pipeline state to actually render incoming data
    ////////////////////////////////////////////////////////////////////
    // TODO2
    // Hints:
    //   1> See https://gstreamer.freedesktop.org/documentation/plugin-development/basics/states.html
            to find the list of possible states
         2> We want to choose the state that allows us to send data all the way through
    */
  g_print ("Now playing: %s\n", argv[1]);
  gst_element_set_state (pipeline, GST_STATE_PLAYING);

  /* Wait till pipeline encounters an error or EOS */
  g_print ("Running...\n");
  g_main_loop_run (loop);

  /* Out of the main loop, clean up nicely */
  g_print ("Returned, stopping playback\n");

  /*
    ////////////////////////////////////////////////////////////////////
    // <1> Change the pipeline state to close devices and clean up
    ////////////////////////////////////////////////////////////////////
    // TODO2
    // Hints:
    //   1> See https://gstreamer.freedesktop.org/documentation/plugin-development/basics/states.html
            to find the list of possible states
         2> We want to choose the state that clears our resources.
    */
  
  gst_element_set_state (pipeline, GST_STATE_NULL);
  g_print ("Deleting pipeline\n");
  gst_object_unref (GST_OBJECT (pipeline));
  g_source_remove (bus_watch_id);
  g_main_loop_unref (loop);
  return 0;


}

"""

In [6]:
!make -C DeepStream_Release/sources/apps/deepstream-test1 clean

!make -C DeepStream_Release/sources/apps/deepstream-test1

make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
rm -rf deepstream_test1_app.o deepstream-test1-app
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
make: Entering directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'
cc -I../../includes `pkg-config --cflags gstreamer-1.0`   -c -o deepstream_test1_app.o deepstream_test1_app.c
cc -o deepstream-test1-app deepstream_test1_app.o `pkg-config --libs gstreamer-1.0`
make: Leaving directory '/dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1'


With the application built, we are ready to run it.

In [7]:
!cd DeepStream_Release/sources/apps/deepstream-test1 && \
./deepstream-test1-app  ../../../samples/streams/sample_720p.h264

Now playing: ../../../samples/streams/sample_720p.h264
>>> Generating new TRT model engine
Using INT8 data type.

 ***** Storing serialized engine file as /dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1/../../../samples/models/Primary_Detector/resnet10.caffemodel_b1_int8.engine batchsize = 1 *****

Running...
Frame Number = 0 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 2 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 3 Number of objects = 6 Vehicle Count = 3 Person Count = 3
Frame Number = 4 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 5 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 6 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 7 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 8 Number of objects = 5 Vehicle Count = 3 Person Count = 

Frame Number = 103 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 104 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 105 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 106 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 107 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 108 Number of objects = 9 Vehicle Count = 5 Person Count = 4
Frame Number = 109 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Frame Number = 110 Number of objects = 9 Vehicle Count = 4 Person Count = 5
65.97 fps
Frame Number = 111 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 112 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 113 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 114 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 115 Number of objects = 7 Vehicle Count = 3 Person Count =

Frame Number = 210 Number of objects = 9 Vehicle Count = 6 Person Count = 3
81.28 fps
Frame Number = 211 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 212 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 213 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 214 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 215 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 216 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 217 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 218 Number of objects = 10 Vehicle Count = 7 Person Count = 2
Frame Number = 219 Number of objects = 9 Vehicle Count = 6 Person Count = 2
Frame Number = 220 Number of objects = 9 Vehicle Count = 7 Person Count = 2
98.83 fps
Frame Number = 221 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 222 Number of objects = 7 Vehicle Count = 5 

Frame Number = 317 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 318 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 319 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Frame Number = 320 Number of objects = 9 Vehicle Count = 5 Person Count = 4
53.88 fps
Frame Number = 321 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 322 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 323 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 324 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 325 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 326 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 327 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 328 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Frame Number = 329 Number of objects = 12 Vehicle Count = 9 Person Cou

Frame Number = 424 Number of objects = 14 Vehicle Count = 7 Person Count = 5
Frame Number = 425 Number of objects = 15 Vehicle Count = 8 Person Count = 5
Frame Number = 426 Number of objects = 15 Vehicle Count = 8 Person Count = 5
Frame Number = 427 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 428 Number of objects = 13 Vehicle Count = 7 Person Count = 4
Frame Number = 429 Number of objects = 13 Vehicle Count = 7 Person Count = 4
Frame Number = 430 Number of objects = 11 Vehicle Count = 5 Person Count = 5
72.27 fps
Frame Number = 431 Number of objects = 11 Vehicle Count = 6 Person Count = 4
Frame Number = 432 Number of objects = 13 Vehicle Count = 7 Person Count = 6
Frame Number = 433 Number of objects = 13 Vehicle Count = 7 Person Count = 4
Frame Number = 434 Number of objects = 13 Vehicle Count = 7 Person Count = 5
Frame Number = 435 Number of objects = 12 Vehicle Count = 7 Person Count = 4
Frame Number = 436 Number of objects = 11 Vehicle Count = 6 Person

...

Frame Number = 966 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 967 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 968 Number of objects = 13 Vehicle Count = 11 Person Count = 2
Frame Number = 969 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 970 Number of objects = 10 Vehicle Count = 8 Person Count = 2
55.65 fps
Frame Number = 971 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 972 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 973 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 974 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 975 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 976 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 977 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 978 Number of objects = 11 Vehicle Count = 8 Pers

Frame Number = 1073 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1074 Number of objects = 7 Vehicle Count = 4 Person Count = 3
Frame Number = 1075 Number of objects = 7 Vehicle Count = 4 Person Count = 3
Frame Number = 1076 Number of objects = 7 Vehicle Count = 4 Person Count = 3
Frame Number = 1077 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1078 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1079 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1080 Number of objects = 12 Vehicle Count = 9 Person Count = 3
62.38 fps
Frame Number = 1081 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1082 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1083 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1084 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1085 Number of objects = 11 Vehicle Count = 8 

Frame Number = 1180 Number of objects = 10 Vehicle Count = 8 Person Count = 2
52.03 fps
Frame Number = 1181 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1182 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1183 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1184 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1185 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1186 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1187 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1188 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1189 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1190 Number of objects = 8 Vehicle Count = 6 Person Count = 2
72.16 fps
Frame Number = 1191 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1192 Number of objects = 7 Vehicle 

Frame Number = 1285 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1286 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1287 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1288 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1289 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1290 Number of objects = 8 Vehicle Count = 6 Person Count = 2
86.02 fps
Frame Number = 1291 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1292 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1293 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1294 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1295 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1296 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1297 Number of objects = 7 Vehicle Count = 5 Person

Frame Number = 1390 Number of objects = 10 Vehicle Count = 8 Person Count = 2
71.95 fps
Frame Number = 1391 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1392 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1393 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1394 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1395 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1396 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1397 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1398 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1399 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1400 Number of objects = 10 Vehicle Count = 8 Person Count = 2
78.17 fps
Frame Number = 1401 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1402 Number of objects = 11 Vehicl

If you scroll through the output, you can see that we are operating with a high frame rate, but it does vary. Logging the minimum, maximum, and average frame rates for your applications is highly recommended to understand any potentially unexpected performance issues.

<a id='gpu-perf'></a>
### 11.3 GPU Performance Metrics

We can use `nvidia-smi` to explore the GPU performance metrics while our application is running. GPU utilization is something we want to pay attention to, and we will discuss it below. Run the cell below to re-run the application while logging the results of `nvidia-smi`.

In [8]:
"""
%%bash
cd DeepStream_Release/sources/apps/deepstream-test1
nvidia-smi dmon -i 0 -s ucmt -c 20 > smi.log &
./deepstream-test1-app  ../../../samples/streams/sample_720p.h264 
"""

Now playing: ../../../samples/streams/sample_720p.h264
>>> Generating new TRT model engine
Using INT8 data type.

 ***** Storing serialized engine file as /dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1/../../../samples/models/Primary_Detector/resnet10.caffemodel_b1_int8.engine batchsize = 1 *****

Running...
Frame Number = 0 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 2 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 3 Number of objects = 6 Vehicle Count = 3 Person Count = 3
Frame Number = 4 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 5 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 6 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 7 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 8 Number of objects = 5 Vehicle Count = 3 Person Count = 

Open smi.log to investigate our utilization metrics. If you have the file open while the pipeline is running, you will need to refresh the `smi.log` page to see updated metrics.

#### Understanding nvidia-smi

The cell block above passed the following arguments to `nvidia-smi`:

- `dmon -i 0`:
    - Reports default metrics (device monitoring) for the devices selected by comma separated device list. In this case, we are reporting default metrics for GPU with index 0 since that is the GPU we are using.


- `-s ucmt`:
    - We can choose which metrics we want to display. In this case, we supplied `ucmt` to indicate we want metrics for
        - u: Utilization (SM, Memory, Encoder and Decoder Utilization in %)
        - c: Proc and Mem Clocks (in MHz)
        - m: Frame Buffer and Bar1 memory usage (in MB)
        - t: PCIe Rx and Tx Throughput in MB/s (Maxwell and above)
        
- `-c 20`
     - We can configure the number of iterations for which we are monitoring. In this case, we choose 20 iterations.
     
Let's dive a bit deeper into a few of the metrics we selected, since they are particularly useful to monitor.

__Utilization__ metrics report how busy each GPU is over time and can be used to determine how much an application is using the GPUs in the system. In particular, the __sm__ column tracks the percent of time over the past sample period during which one or more kernels was executing on the GPU. __fb__ reports the GPU's frame buffer memory usage. For those interested in learning more, more detailed and comprehensive documentation can be accessed [here](http://developer.download.nvidia.com/compute/DCGM/docs/nvidia-smi-367.38.pdf).


Take a quick look at your metrics in `smi.log`. Does it look like our GPU was highly utilized? Keep your answer in your head -- we will explore utilization in the next section.

<a id='gen_latency'></a>
### 11.4 Generating Latency Metrics with GStreamer Logs

We can also leverage GStreamer's built in [debugging](https://gstreamer.freedesktop.org/documentation/tutorials/basic/debugging-tools.html#the-debug-log) capabilities to measure latency across our pipeline. By setting `GST_DEBUG` environment variables, we can control what kinds of logs we get. `GST_SCHEDULING:7` is the Trace setting, which logs all trace messages. This logs every time things like Buffers are modified, giving us detailed information about our pipeline.

Use the cell below to run our application with debugging set to the Trace setting.

In [9]:
!cd DeepStream_Release/sources/apps/deepstream-test1 && \
LD_LIBRARY_PATH=$LD_LIBRARY_PATH:/usr/local/opencv-3.4.1/lib && \
GST_DEBUG="GST_SCHEDULING:7" GST_DEBUG_FILE=trace.log ./deepstream-test1-app ../../../samples/streams/sample_720p.h264

Now playing: ../../../samples/streams/sample_720p.h264
>>> Generating new TRT model engine
Using INT8 data type.

 ***** Storing serialized engine file as /dli/tasks/l-iv-04/task/DeepStream_Release/sources/apps/deepstream-test1/../../../samples/models/Primary_Detector/resnet10.caffemodel_b1_int8.engine batchsize = 1 *****

Running...
Frame Number = 0 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 1 Number of objects = 4 Vehicle Count = 2 Person Count = 2
Frame Number = 2 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 3 Number of objects = 6 Vehicle Count = 3 Person Count = 3
Frame Number = 4 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 5 Number of objects = 5 Vehicle Count = 3 Person Count = 2
Frame Number = 6 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 7 Number of objects = 6 Vehicle Count = 4 Person Count = 2
Frame Number = 8 Number of objects = 5 Vehicle Count = 3 Person Count = 

Frame Number = 103 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 104 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 105 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 106 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 107 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 108 Number of objects = 9 Vehicle Count = 5 Person Count = 4
Frame Number = 109 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Frame Number = 110 Number of objects = 9 Vehicle Count = 4 Person Count = 5
72.59 fps
Frame Number = 111 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 112 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 113 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 114 Number of objects = 7 Vehicle Count = 3 Person Count = 4
Frame Number = 115 Number of objects = 7 Vehicle Count = 3 Person Count =

Frame Number = 211 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 212 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 213 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 214 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 215 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 216 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 217 Number of objects = 13 Vehicle Count = 9 Person Count = 4
Frame Number = 218 Number of objects = 10 Vehicle Count = 7 Person Count = 2
Frame Number = 219 Number of objects = 9 Vehicle Count = 6 Person Count = 2
Frame Number = 220 Number of objects = 9 Vehicle Count = 7 Person Count = 2
79.14 fps
Frame Number = 221 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 222 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 223 Number of objects = 8 Vehicle Count = 6 Person Cou

Frame Number = 322 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 323 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 324 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 325 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 326 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 327 Number of objects = 10 Vehicle Count = 6 Person Count = 4
Frame Number = 328 Number of objects = 8 Vehicle Count = 4 Person Count = 4
Frame Number = 329 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 330 Number of objects = 11 Vehicle Count = 8 Person Count = 3
64.21 fps
Frame Number = 331 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 332 Number of objects = 12 Vehicle Count = 8 Person Count = 4
Frame Number = 333 Number of objects = 11 Vehicle Count = 7 Person Count = 4
Frame Number = 334 Number of objects = 13 Vehicle Count = 9 Person C

Frame Number = 430 Number of objects = 11 Vehicle Count = 5 Person Count = 5
82.72 fps
Frame Number = 431 Number of objects = 11 Vehicle Count = 6 Person Count = 4
Frame Number = 432 Number of objects = 13 Vehicle Count = 7 Person Count = 6
Frame Number = 433 Number of objects = 13 Vehicle Count = 7 Person Count = 4
Frame Number = 434 Number of objects = 13 Vehicle Count = 7 Person Count = 5
Frame Number = 435 Number of objects = 12 Vehicle Count = 7 Person Count = 4
Frame Number = 436 Number of objects = 11 Vehicle Count = 6 Person Count = 4
Frame Number = 437 Number of objects = 13 Vehicle Count = 8 Person Count = 4
Frame Number = 438 Number of objects = 12 Vehicle Count = 7 Person Count = 4
Frame Number = 439 Number of objects = 14 Vehicle Count = 8 Person Count = 5
Frame Number = 440 Number of objects = 11 Vehicle Count = 7 Person Count = 3
55.91 fps
Frame Number = 441 Number of objects = 13 Vehicle Count = 9 Person Count = 3
Frame Number = 442 Number of objects = 9 Vehicle Count =

...

Frame Number = 967 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 968 Number of objects = 13 Vehicle Count = 11 Person Count = 2
Frame Number = 969 Number of objects = 13 Vehicle Count = 10 Person Count = 3
Frame Number = 970 Number of objects = 10 Vehicle Count = 8 Person Count = 2
52.65 fps
Frame Number = 971 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 972 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 973 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 974 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 975 Number of objects = 12 Vehicle Count = 9 Person Count = 3
Frame Number = 976 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 977 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 978 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 979 Number of objects = 10 Vehicle Count = 7 Pers

Frame Number = 1072 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1073 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1074 Number of objects = 7 Vehicle Count = 4 Person Count = 3
Frame Number = 1075 Number of objects = 7 Vehicle Count = 4 Person Count = 3
Frame Number = 1076 Number of objects = 7 Vehicle Count = 4 Person Count = 3
Frame Number = 1077 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1078 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1079 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1080 Number of objects = 12 Vehicle Count = 9 Person Count = 3
70.02 fps
Frame Number = 1081 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1082 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1083 Number of objects = 11 Vehicle Count = 8 Person Count = 3
Frame Number = 1084 Number of objects = 11 Vehicle Count = 8 P

Frame Number = 1178 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1179 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1180 Number of objects = 10 Vehicle Count = 8 Person Count = 2
68.91 fps
Frame Number = 1181 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1182 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1183 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1184 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1185 Number of objects = 10 Vehicle Count = 7 Person Count = 3
Frame Number = 1186 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1187 Number of objects = 9 Vehicle Count = 6 Person Count = 3
Frame Number = 1188 Number of objects = 8 Vehicle Count = 5 Person Count = 3
Frame Number = 1189 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1190 Number of objects = 8 Vehicle Count = 

Frame Number = 1284 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1285 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1286 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1287 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1288 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1289 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1290 Number of objects = 8 Vehicle Count = 6 Person Count = 2
71.59 fps
Frame Number = 1291 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1292 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1293 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1294 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1295 Number of objects = 7 Vehicle Count = 5 Person Count = 2
Frame Number = 1296 Number of objects = 7 Vehicle Count = 5 Person

Frame Number = 1392 Number of objects = 8 Vehicle Count = 6 Person Count = 2
Frame Number = 1393 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1394 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1395 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1396 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1397 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1398 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1399 Number of objects = 10 Vehicle Count = 8 Person Count = 2
Frame Number = 1400 Number of objects = 10 Vehicle Count = 8 Person Count = 2
90.97 fps
Frame Number = 1401 Number of objects = 9 Vehicle Count = 7 Person Count = 2
Frame Number = 1402 Number of objects = 11 Vehicle Count = 9 Person Count = 2
Frame Number = 1403 Number of objects = 8 Vehicle Count = 7 Person Count = 1
Frame Number = 1404 Number of objects = 7 Vehicle Count = 6

In [10]:
!cat DeepStream_Release/sources/apps/deepstream-test1/trace.log

0:00:00.046384194   204      0x1c23a60 LOG           GST_SCHEDULING gstpad.c:1381:gst_pad_add_probe:<nv-onscreendisplay:sink> adding probe for mask 0x00000010
0:00:00.046433091   204      0x1c23a60 LOG           GST_SCHEDULING gstpad.c:1407:gst_pad_add_probe:<nv-onscreendisplay:sink> got probe id 1
0:00:00.046441910   204      0x1c23a60 LOG           GST_SCHEDULING gstpad.c:1381:gst_pad_add_probe:<nv-onscreendisplay:sink> adding probe for mask 0x00000010
0:00:00.046447378   204      0x1c23a60 LOG           GST_SCHEDULING gstpad.c:1407:gst_pad_add_probe:<nv-onscreendisplay:sink> got probe id 2
0:00:00.355914011   204      0x1c23a60 LOG           GST_SCHEDULING gstpad.c:3602:do_probe_callbacks:<nv-onscreendisplay:sink> do probes cookie 1
0:00:00.355954082   204      0x1c23a60 LOG           GST_SCHEDULING gstpad.c:3498:probe_hook_marshal:<nv-onscreendisplay:sink> hook 1, cookie 1 with flags 0x00003010 does not match 00001402
0:00:00.355964451   204      0x1c23a60 LOG           GST_SCHEDUL

0:00:08.360244153   204      0x1c26940 DEBUG         GST_SCHEDULING gstpad.c:4186:gst_pad_chain_data_unchecked:<primary-nvinference-engine:sink> calling chainfunction &gst_base_transform_chain with buffer buffer: 0x7ff720ffd4e0, pts 0:00:01.533333318, dts 99:99:99.999999999, dur 0:00:00.033333333, size 8224, offset none, offset_end none, flags 0x4000
0:00:08.360323719   204      0x1c26940 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<primary-nvinference-engine:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720ffd4e0, returned ok
0:00:08.360351101   204      0x1c26940 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<nvh264-decoder:sink> called chainfunction &gst_video_decoder_chain with buffer 0x7ff7200169b0, returned ok
0:00:08.360341883   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4186:gst_pad_chain_data_unchecked:<filter1:sink> calling chainfunction &gst_base_transform_chain with buffer buffer: 0x

0:00:09.300847684   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4186:gst_pad_chain_data_unchecked:<nv-onscreendisplay:sink> calling chainfunction &gst_base_transform_chain with buffer buffer: 0x7ff720ffd0a0, pts 0:00:02.999999970, dts 99:99:99.999999999, dur 0:00:00.033333333, size 8224, offset none, offset_end none, flags 0x4000
0:00:09.302591971   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4186:gst_pad_chain_data_unchecked:<nvvideo-converter1:sink> calling chainfunction &gst_base_transform_chain with buffer buffer: 0x7ff720ffd0a0, pts 0:00:02.999999970, dts 99:99:99.999999999, dur 0:00:00.033333333, size 8224, offset none, offset_end none, flags 0x4000
0:00:09.303234728   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4186:gst_pad_chain_data_unchecked:<filter3:sink> calling chainfunction &gst_base_transform_chain with buffer buffer: 0x7ff720016790, pts 0:00:02.999999970, dts 99:99:99.999999999, dur 0:00:00.033333333, size 3686400, offset none, off

0:00:09.906844362   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<nv-onscreendisplay:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720016ce0, returned ok
0:00:09.906857275   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<filter2:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720016ce0, returned ok
0:00:09.906870008   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<nvvideo-converter:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720ffd2c0, returned ok
0:00:09.906881984   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<filter1:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720ffd2c0, returned ok
0:00:09.907015248   204      0x1c26940 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<primary-nvinfer

0:00:10.392307635   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<h264 encoder:sink> called chainfunction &gst_video_encoder_chain with buffer 0x7ff722796930, returned ok
0:00:10.392319887   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<filter4:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff722796930, returned ok
0:00:10.392331749   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<converter:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720016020, returned ok
0:00:10.392342300   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<filter3:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720016020, returned ok
0:00:10.392352974   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<nvvideo-converter1:sink> calle

0:00:11.022605841   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<converter:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720016130, returned ok
0:00:11.022615886   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<filter3:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720016130, returned ok
0:00:11.022625307   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<nvvideo-converter1:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720ffd0a0, returned ok
0:00:11.022634581   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<nv-onscreendisplay:sink> called chainfunction &gst_base_transform_chain with buffer 0x7ff720ffd0a0, returned ok
0:00:11.022643613   204      0x1c26450 DEBUG         GST_SCHEDULING gstpad.c:4192:gst_pad_chain_data_unchecked:<filter2:sink

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



* trace.log is a huge file, so we will highlight an instance of the decoder plugin latency from the trace log.



    0:00:05.137672361  <omxh264dec-omxh264dec0:sink> calling chainfunction &gst_video_decoder_chain with buffer buffer: 0x7f9c02bc00, pts 0:00:35.719066666, dts 0:00:35.719033333, dur 0:00:00.016683333, size 56047, offset 172403525, offset_end none, flags 0x2400
    0:00:05.170122161  <src_0:proxypad3> calling chainfunction &gst_proxy_pad_chain_default with buffer buffer: 0x7f714c5020, pts 0:00:35.719066666, dts 99:99:99.999999999, dur 0:00:00.016683333, size 808, offset none, offset_end none, flags 0x0

You can see the time a frame entered at the input of the decoder plugin to when it entered the next input is __33ms__ which would equate to roughly __30__ frames per second.

<a id='util-2'></a>
### 11.5 More on GPU Utilization

In this last section, we will switch to using our section 5 application to explore how utilization metrics vary with the workload. Specifically, we will look at how utilization varies with:

* Different number of input streams 
* The addition of secondary inference components to the pipeline

Based on these results, you will begin to see factors that ultimately saturate pipeline performance.

* **configs/deepstream-app/source4_720p_dec_infer-resnet_tracker_sgie_tiled_display_int8.txt** and keep it open to change stream count later on.

In [ ]:
"""
# Copyright (c) 2018 NVIDIA Corporation.  All rights reserved.
#
# NVIDIA Corporation and its licensors retain all intellectual property
# and proprietary rights in and to this software, related documentation
# and any modifications thereto.  Any use, reproduction, disclosure or
# distribution of this software and related documentation without an express
# license agreement from NVIDIA Corporation is strictly prohibited.

[application]
enable-perf-measurement=1
perf-measurement-interval-sec=5
#gie-kitti-output-dir=streamscl

[tiled-display]
enable=0
rows=2
columns=2
width=1280
height=720
gpu-id=0
# 0 - cuda pinned/host memory
# 1 - cuda device memory
# 2 - cuda unified memory
cuda-memory-type=1

[source0]
enable=1
#Type - 1=CameraV4L2 2=URI 3=MultiURI
type=3
uri=file://../../streams/sample_720p.mp4
num-sources=4
gpu-id=0
# 0 - cuda pinned/host memory
# 1 - cuda device memory
# 2 - cuda unified memory
cuda-memory-type=1

[sink0]
enable=1
#Type - 1=FakeSink 2=EglSink 3=File
type=1
sync=1
source-id=0
gpu-id=0
cuda-memory-type=1

[sink1]
enable=0
type=3
#1=mp4 2=mkv
container=1
#1=h264 2=h265 3=mpeg4
## only SW mpeg4 is supported right now.
codec=3
sync=0
bitrate=2000000
output-file=out.mp4
source-id=0

[sink2]
enable=0
#Type - 1=FakeSink 2=EglSink 3=File 4=RTSPStreaming
type=4
#1=mp4 2=mkv
container=2
#1=h264 2=h265 3=mpeg4
## only mpeg4 is supported right now.
codec=1
sync=0
bitrate=4000
# set below properties in case of RTSPStreaming
rtsp-port=8554
udp-port=5400


[osd]
enable=0
gpu-id=0
border-width=1
text-size=15
text-color=1;1;1;1;
text-bg-color=0.3;0.3;0.3;1
font=Arial
show-clock=0
clock-x-offset=800
clock-y-offset=820
clock-text-size=12
clock-color=1;0;0;0
cuda-memory-type=1

[streammux]
gpu-id=0
##Boolean property to inform muxer that sources are live
live-source=0
batch-size=4
##time out in usec, to wait after the first buffer is available
##to push the batch even if the complete batch is not formed
batched-push-timeout=40000
## Set muxer output width and height
width=1280
height=720
##Enable to maintain aspect ratio wrt source, and allow black borders, works
##along with width, height properties
enable-padding=0
cuda-memory-type=1

# config-file property is mandatory for any gie section.
# Other properties are optional and if set will override the properties set in
# the infer config file.
[primary-gie]
enable=1
gpu-id=0
model-engine-file=../../models/Primary_Detector/resnet10.caffemodel_b4_int8.engine
labelfile-path=../../models/Primary_Detector/labels.txt
batch-size=4
#Required by the app for OSD, not a plugin property
bbox-border-color0=1;0;0;1
bbox-border-color1=0;1;1;1
bbox-border-color2=0;0;1;1
bbox-border-color3=0;1;0;1
interval=0
gie-unique-id=1
cuda-memory-type=1
config-file=config_infer_primary.txt

[tracker]
enable=1
tracker-width=640
tracker-height=368
gpu-id=0

[secondary-gie0]
enable=1
model-engine-file=../../models/Secondary_VehicleTypes/resnet18.caffemodel_b16_int8.engine
labelfile-path=../../models/Secondary_VehicleTypes/labels.txt
gpu-id=0
batch-size=16
gie-unique-id=4
operate-on-gie-id=1
operate-on-class-ids=0;
config-file=config_infer_secondary_vehicletypes.txt

[secondary-gie1]
enable=1
model-engine-file=../../models/Secondary_CarColor/resnet18.caffemodel_b16_int8.engine
labelfile-path=../../models/Secondary_CarColor/labels.txt
batch-size=16
gpu-id=0
gie-unique-id=5
operate-on-gie-id=1
operate-on-class-ids=0;
config-file=config_infer_secondary_carcolor.txt

[secondary-gie2]
enable=1
model-engine-file=../../models/Secondary_CarMake/resnet18.caffemodel_b16_int8.engine
labelfile-path=../../models/Secondary_CarMake/labels.txt
batch-size=16
gpu-id=0
gie-unique-id=6
operate-on-gie-id=1
operate-on-class-ids=0;
config-file=config_infer_secondary_carmake.txt

[tests]
file-loop=0
"""

In [11]:
 rm ~/.cache/gstreamer-1.0/ -rf

In [12]:
!LD_LIBRARY_PATH=$LD_LIBRARY_PATH:/usr/include/opencv && \
cd DeepStream_Release/samples && \
sh -c 'nvidia-smi dmon -i 0 -s ucmt -c 20 > smi.log &' && \
deepstream-app -c configs/deepstream-app/source4_720p_dec_infer-resnet_tracker_sgie_tiled_display_int8.txt

>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_CarMake/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause errors.
>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_CarColor/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause errors.
>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_VehicleTypes/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause err

Open smi.log and observe decoder and SM utilization. It should look pretty similar to the output from the previous section, with several utilization metrics slightly higher.

```

# gpu    sm   mem   enc   dec  mclk  pclk    fb  bar1 rxpci txpci
# Idx     %     %     %     %   MHz   MHz    MB    MB  MB/s  MB/s
    0     0     0     0     0   877   135     0     2     0     0
    0     5     0     0     0   877  1312   470     7   164    37
    0     5     0     0     0   877  1312   796     7     0    14
    0     4     1     0    12   877  1312  1308     7     8     0
    0     9     1     0    12   877  1312  1308     7     0    86
    0     4     1     0    13   877  1312  1308     7     5     0
    0    10     1     0    11   877  1312  1308     7    38    86
    0     5     1     0    12   877  1312  1308     7     5     0
    0     9     1     0    12   877  1312  1308     7    90   101
    0     4     1     0    12   877  1312  1308     7     5     0
    0     9     1     0    11   877  1312  1308     7    62    91
    0    10     1     0    12   877  1312  1308     7     6     0
    0     4     1     0    12   877  1312  1308     7    10     0
    0     4     1     0    12   877  1312  1308     7     0    86
    0     8     1     0    11   877  1312  1308     7     7    18
    0    10     1     0    12   877  1312  1308     7   194    86
    0     9     1     0    12   877  1312  1308     7     5    11
    0     4     1     0    12   877  1312  1308     7     5    86
    0     9     1     0    12   877  1312  1308     7     2   102
    0     4     1     0    12   877  1312  1308     7     5    86




Now vary stream count to 16 and 32 streams by modifying __num-sources__ under the __\[source0\]__ section within the source4_720p_dec_infer-resnet_tracker_sgie_tiled_display_int8.txt file you just opened. Also remember to change the __batch-size__ in __\[primary-gie\]__ to match the stream count. Then, re-run the application with the modified stream count.

What changes do you notice when you vary the stream count?

1. Are we still able to achieve 30 frames per second?
2. Does the GPU utilization increase or decrease?
3. What changes happen to our frame buffer memory usage?

* **16 Multiple Sources**

In [16]:
 rm ~/.cache/gstreamer-1.0/ -rf

In [17]:
!LD_LIBRARY_PATH=$LD_LIBRARY_PATH:/usr/include/opencv && \
cd DeepStream_Release/samples && \
sh -c 'nvidia-smi dmon -i 0 -s ucmt -c 20 > smi.log &' && \
deepstream-app -c configs/deepstream-app/source4_720p_dec_infer-resnet_tracker_sgie_tiled_display_int8.txt

>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_CarMake/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause errors.
>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_CarColor/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause errors.
>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_VehicleTypes/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause err

```

# gpu    sm   mem   enc   dec  mclk  pclk    fb  bar1 rxpci txpci
# Idx     %     %     %     %   MHz   MHz    MB    MB  MB/s  MB/s
    0     0     0     0     0   877   135     0     2     0     0
    0     8     1     0     0   877  1312   474     7     0    86
    0     5     0     0     0   877  1312   796     7   125     1
    0    38    18     0     0   877  1530  1314     7    13     2
    0    58    14     0     0   877  1530  1264     7    56     2
    0    40     6     0     0   877  1530  1260     7    65     2
    0     5     1     0    31   877  1530  1951     7    34     5
    0     9     2     0    22   877  1530  2200     7     9    88
    0    12     2     0    35   877  1530  2200     7     5   258
    0    20     3     0    32   877  1530  2200     7    21    86
    0    14     3     0    40   877  1530  2200     7    14   258
    0    42     5     0    40   877  1530  2200     7   349   286
    0    12     2     0    26   877  1530  2200     7    11   259
    0    30     3     0    33   877  1530  2200     7   180   124
    0    18     3     0    36   877  1530  2200     7     8   259
    0    23     3     0    35   877  1530  2200     7   326   177
    0    28     3     0    37   877  1530  2200     7   109   259
    0    29     4     0    36   877  1530  2200     7    39    87
    0    15     3     0    41   877  1530  2200     7    44   256
    0    13     2     0    33   877  1530  2200     7    31   136


* **32 Multiple Sources**

In [20]:
 rm ~/.cache/gstreamer-1.0/ -rf

In [21]:
!LD_LIBRARY_PATH=$LD_LIBRARY_PATH:/usr/include/opencv && \
cd DeepStream_Release/samples && \
sh -c 'nvidia-smi dmon -i 0 -s ucmt -c 20 > smi.log &' && \
deepstream-app -c configs/deepstream-app/source4_720p_dec_infer-resnet_tracker_sgie_tiled_display_int8.txt

>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_CarMake/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause errors.
>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_CarColor/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause errors.
>>> Using TRT model serialized engine /dli/tasks/l-iv-04/task/DeepStream_Release/samples/configs/deepstream-app/../../models/Secondary_VehicleTypes/resnet18.caffemodel_b16_int8.engine crypto flags(0)
Using an engine plan file across different models of devices is not recommended and is likely to affect performance or even cause err

WARNING from sink_sub_bin_sink1: A lot of buffers are being dropped.
Debug info: gstbasesink.c(2854): gst_base_sink_is_too_late (): /GstPipeline:pipeline/GstBin:processing_bin_0/GstBin:sink_bin/GstBin:sink_sub_bin1/GstFakeSink:sink_sub_bin_sink1:
There may be a timestamping problem, or this computer is too slow.
**PERF: 14.51 (12.48)	14.51 (12.48)	14.51 (12.48)	14.51 (12.48)	14.51 (12.50)	14.51 (12.50)	14.51 (12.48)	14.55 (12.50)	14.55 (12.49)	14.55 (12.49)	14.55 (12.50)	14.51 (12.48)	14.51 (12.48)	14.51 (12.48)	14.51 (12.48)	14.47 (12.48)	14.47 (12.48)	14.47 (12.48)	14.47 (12.48)	14.52 (12.48)	14.52 (12.48)	14.52 (12.48)	14.52 (12.48)	14.49 (12.48)	14.49 (12.48)	14.49 (12.48)	14.49 (12.48)	14.52 (12.48)	14.52 (12.48)	14.52 (12.48)	14.52 (12.48)	14.51 (12.48)	
WARNING from sink_sub_bin_sink1: A lot of buffers are being dropped.
Debug info: gstbasesink.c(2854): gst_base_sink_is_too_late (): /GstPipeline:pipeline/GstBin:processing_bin_0/GstBin:sink_bin/GstBin:sink_sub_bin1/GstFakeSink:si

WARNING from sink_sub_bin_sink1: A lot of buffers are being dropped.
Debug info: gstbasesink.c(2854): gst_base_sink_is_too_late (): /GstPipeline:pipeline/GstBin:processing_bin_0/GstBin:sink_bin/GstBin:sink_sub_bin1/GstFakeSink:sink_sub_bin_sink1:
There may be a timestamping problem, or this computer is too slow.
WARNING from sink_sub_bin_sink1: A lot of buffers are being dropped.
Debug info: gstbasesink.c(2854): gst_base_sink_is_too_late (): /GstPipeline:pipeline/GstBin:processing_bin_0/GstBin:sink_bin/GstBin:sink_sub_bin1/GstFakeSink:sink_sub_bin_sink1:
There may be a timestamping problem, or this computer is too slow.

**PERF: FPS 0 (Avg)	FPS 1 (Avg)	FPS 2 (Avg)	FPS 3 (Avg)	FPS 4 (Avg)	FPS 5 (Avg)	FPS 6 (Avg)	FPS 7 (Avg)	FPS 8 (Avg)	FPS 9 (Avg)	FPS 10 (Avg)	FPS 11 (Avg)	FPS 12 (Avg)	FPS 13 (Avg)	FPS 14 (Avg)	FPS 15 (Avg)	FPS 16 (Avg)	FPS 17 (Avg)	FPS 18 (Avg)	FPS 19 (Avg)	FPS 20 (Avg)	FPS 21 (Avg)	FPS 22 (Avg)	FPS 23 (Avg)	FPS 24 (Avg)	FPS 25 (Avg)	FPS 26 (Avg)	FPS 27 (Avg)	FPS 28 (A

```

# gpu    sm   mem   enc   dec  mclk  pclk    fb  bar1 rxpci txpci
# Idx     %     %     %     %   MHz   MHz    MB    MB  MB/s  MB/s
    0     0     0     0     0   877   135     0     2     0     0
    0     4     0     0     0   877  1312   426     7   736    37
    0     5     0     0     0   877  1312   774     7   118     0
    0    46    14     0     0   877  1530  1714     7    18     6
    0    60    14     0     0   877  1530  1314     7    16     3
    0    52    11     0     0   877  1530  1296     7   129    70
    0    33     7     0     0   877  1530  1258     7     3   138
    0     3     1     0    43   877  1530  3378     7    14    87
    0     9     2     0    27   877  1530  3384     7    13   173
    0    10     2     0    29   877  1530  3384     7    35    89
    0    10     2     0    26   877  1530  3384     7     6   172
    0    14     3     0    39   877  1530  3384     7    68   180
    0    34     4     0    36   877  1530  3384     7    57     0
    0    15     3     0    46   877  1530  3384     7     8    86
    0    11     2     0    32   877  1530  3384     7    16   190
    0    12     2     0    35   877  1530  3384     7    34   173
    0    19     3     0    39   877  1530  3384     7     5   262
    0    37     5     0    35   877  1530  3384     7   154   162
    0    12     2     0    34   877  1530  3384     7     6   259
    0    13     3     0    38   877  1530  3384     7     8   171


<a id='summary'></a>
## Summary


* The building blocks of DeepStream
* How to use DeepStream for single and multiple neural network-based inferencing
* How to access and handle metadata
* How to use the NvInfer component to accommodate any TensorRT compatible neural network detector
* How to customize a DeepStream pipeline and incorporate custom image processing using C++ code
* How to batch multiple input streams together into a single DeepStream pipeline
* How to use unwarp plugin for 360 camera streams
* how to utilize "nvmsgconv" and "nvmsgbroker" plugins in the pipeline
* Performance metrics and how to measure them